In [2]:
from data_loader import DataLoader
from concept_deconflict import (pairs_to_locs, hierarchize_concepts, 
                                DummyTagAwareModel, ConflictResolver)

In [3]:
# Here we load the gold set using Dasha's code
dataLoader = DataLoader()
annotations = dataLoader.load_annotations('/Users/ritvikkhandelwal/Desktop/elsevier docs/Elsevier projects/Knowledge minor Gold standard /gold_data')
#the dataloader.load_annotations returns two dictionaries (text dictionary and annotations dictionary) and these 2 dictionaries are sotred in the annotations variable


In [4]:
# Now we already have the text and annotations dictionary but we want to extract some information from these 2 dictionaries to perform NER easily. 
# So for that we first initialize 4 empty dictionaries and then we wrtie a loop to populate these 4 dictionaries with relevant information from the text and annotations dictionary

pairs = {} #will capture the start and end (span) of every annotation in every document inside every folder 
tags = {}  #will capture the semantic group corressponding to the particular pair/span in everye document inside every folder
emmet = {}
text = {} #will capture the text corressponding to every document inside every other folder
for folder in annotations[0]: #iterating across each folder(primary keys) of the text dictionary 
    pairs[folder] = {} # initializing pairs corresponding to every folder as null ---> iteration 1 - pairs['6-s2.0-5104'] = {}, iteration 2 - pairs['6-s2.0-3792'] = {}, ...etc
    tags[folder] = {} #initializing tags corresponding to every folder as null ---> iteration 1 - tags['6-s2.0-5104'] = {}, iteration 2 - tags['6-s2.0-3792'] = {}, ....etc 
    emmet[folder] = {}
    text[folder] = {} #initializing tags corresponding to every folder as null -----> iteration 1 - text['6-s2.0-5104'] = {}, iteration 2 - text['6-s2.0-3792'] = {}, ....etc 
    for doc in annotations[0][folder]: #iterating accross each document inside every folder of the text dictionary 
        text[folder][doc]  = annotations[0][folder][doc]  #text['6-s2.0-5104']['01'] = assign the text corresponding to the folder and document number 
        ann = annotations[1][folder][doc]  #annotations[1]['6-s2.0-5104']['01']........getting the annotations of the corresponding text file and that is stores in ann
        pairs[folder][doc] = []   # initializing pairs corresponding to each folder and document as null. we are going to populate these in the next nested for loop
        tags[folder][doc] = {}  #initializing tags corresponding to each folder and document as null. we are going to populate these in the next nested for loop
        emmet[folder][doc] = {}
        for annotation in ann.annotations.values():
            #print(annotation)
            #from each annotation we are essentially trying to get the start and ending (spans)
            pair = (annotation.start, annotation.end)
            pairs[folder][doc].append(pair) #pairs['6-s2.0-5104']['01']
            tags[folder][doc][pair] = annotation.ann_type
            if annotation.norm is not None:
                emmet[folder][doc][pair] = annotation.norm.norm
            else:
                emmet[folder][doc][pair] = None

In [5]:
all_sentences = [] #list containing all the sentences in the dataset 
all_entities = [] #list containing the tags of each and every sentence 
for folder, file_dict in text.items():
    for file_num, file_text in file_dict.items():
        txt_sentences = file_text.split("\n")
        len_tracker = []
        entities = []
        entities_in_sent = []
        sent_end_tracker = []
        sentences = []
        file_tags = tags[folder][file_num]
        for i,sentence in enumerate(txt_sentences):
            entities = []
            len_tracker.append(len(sentence))
            if(i == 0):
                sent_start = 0
                sent_end = len_tracker[i]
                sent_end_tracker.append(sent_end)
            else:
                sent_start = sent_end_tracker[i-1]+1
                sent_end = sent_start + len_tracker[i]
                sent_end_tracker.append(sent_end)
            #print(sent_start,sent_end)
            for span, entity in file_tags.items():
                start, end = span 
                if (start>= sent_start and end < sent_end):
                    new_annotations = f"@@{file_text[start:end]}:{entity}##"
                    entities.append(new_annotations)
                else:
                    continue
            sentences.append(sentence)
            all_sentences.append(sentence)
            entities_in_sent.append(entities)
            all_entities.append(entities)

In [6]:
replacement_string = "There are none"

for i, sublist in enumerate(all_entities):
    if not sublist:  # Check if the sublist is empty
        all_entities[i] = [replacement_string]

# Now all the empty lists have been replaced with [replacement_string]


In [7]:
# Find indices of sentences with less than 4 words
short_sentence_indices = [i for i, sentence in enumerate(all_sentences) if len(sentence.split()) < 4]

# Remove the short sentences and their corresponding annotations
filtered_all_sentences = [sentence for i, sentence in enumerate(all_sentences) if i not in short_sentence_indices]
filtered_all_entities = [annotations for i, annotations in enumerate(all_entities) if i not in short_sentence_indices]

# Print the filtered sentences and their corresponding annotations
#for sentence, annotations in zip(filtered_all_sentences, filtered_all_entities):
 #   print("Filtered Sentence:", sentence)
  #  print("Filtered Annotations:", annotations)
   # print("-" * 30)


In [8]:
print(len(filtered_all_sentences))
len((filtered_all_entities))

11026


11026

In [9]:
print(filtered_all_sentences[2])
filtered_all_entities[2]

At 12 weeks, a significantly higher proportion of sarecycline-treated patients had improved acne and a reduction in inflammatory acne lesions compared with placebo. 


['@@weeks:Qualifier##',
 '@@significantly:Socialcontext##',
 '@@higher:Qualifier##',
 '@@proportion:Qualifier##',
 '@@sarecycline:Drugs##',
 '@@patients:Socialcontext##',
 '@@improved:Qualifier##',
 '@@acne:Diseases##',
 '@@reduction:Qualifier##',
 '@@inflammatory:Qualifier##',
 '@@inflammatory acne:Diseases##',
 '@@acne:Diseases##',
 '@@lesions:Symptoms##',
 '@@compared:Event##',
 '@@placebo:Substance##']

In [10]:
import re
# Remove occurrences of any number of digits enclosed in []
pattern = r'\[\d+\]'  # Regular expression pattern for matching [12345], [98765], etc.
cleaned_sentences = [re.sub(pattern, '', sentence) for sentence in filtered_all_sentences]

# Print the cleaned sentences
#for cleaned_sentence in cleaned_sentences:
    #print(cleaned_sentence)

In [11]:
len(cleaned_sentences)

11026

In [12]:
all_sentences = cleaned_sentences
all_entities = filtered_all_entities
#contain min 4 words and all entities

In [13]:
print(len(all_sentences))
len((all_entities))

11026


11026

In [14]:
#creation of 8_entities list 

# Annotations to remove
annotations_to_remove = ['Socialcontext', 'Substance', 'Environmentgeographicallocation', 'Qualifier', 'Event', 'Physicalobjects']

# Remove unwanted annotations from each list in entities_sub
updated_entities = []

for annotations_list in all_entities:
    updated_annotations = [annotation for annotation in annotations_list if all(tag not in annotation for tag in annotations_to_remove)]
    updated_entities.append(updated_annotations)
    
replacement_string = "There are none"

for i, sublist in enumerate(updated_entities):
    if not sublist:  # Check if the sublist is empty
        updated_entities[i] = [replacement_string]

In [15]:
updated_entities

[['@@Sarecycline:Drugs##',
  '@@tetracycline:Drugs##',
  '@@lesions:Symptoms##',
  '@@acne:Diseases##',
  '@@acne vulgaris:Diseases##',
  '@@age:Clinicalfinding##',
  '@@tetracycline-class antibiotic:Drugs##'],
 ['@@sarecycline:Drugs##', '@@acne:Diseases##'],
 ['@@sarecycline:Drugs##',
  '@@acne:Diseases##',
  '@@inflammatory acne:Diseases##',
  '@@acne:Diseases##',
  '@@lesions:Symptoms##'],
 ['@@sarecycline:Drugs##',
  '@@permanent tooth:Anatomy##',
  '@@tooth:Anatomy##',
  '@@tooth discoloration:Symptoms##',
  '@@discoloration:Symptoms##',
  '@@decay:Diseases##',
  '@@tooth:Anatomy##',
  '@@tooth development:Clinicalfinding##',
  '@@development:Clinicalfinding##',
  '@@tooth discoloration and decay:Diseases##'],
 ['@@sarecycline:Drugs##',
  '@@lesions:Diseases##',
  '@@acne:Diseases##',
  '@@acne vulgaris:Diseases##'],
 ['@@bacteriostatic:Clinicalfinding##', '@@organisms:Organism##'],
 ['@@Bacteriostatic:Clinicalfinding##',
  '@@binding:Clinicalfinding##',
  '@@organisms:Organism##'

In [16]:
sentences_8_dup = all_sentences 
entities_8_dup = all_entities
print(len(sentences_8_dup))
print(len(entities_8_dup))

11026
11026


In [17]:
#Drugs

filtered_tags_drugs = []

# Iterate through both lists
for sentence, entity in zip(all_sentences, all_entities):
    drugs_tags = [entity for entity in entity if "Drugs" in entity]  # Filter "Drugs" tags
    if drugs_tags:
        filtered_tags_drugs.append(drugs_tags)
    else:
        filtered_tags_drugs.append(["There are none"])  # Add a placeholder if no "Drugs" tag is found


In [18]:
print(len(filtered_tags_drugs))
print(len(all_entities))

11026
11026


In [19]:
#Procedures

filtered_procedures = []

# Iterate through both lists
for sentence, entity in zip(all_sentences, all_entities):
    proc_tags = [entity for entity in entity if "Procedures" in entity]  # Filter "Drugs" tags
    if proc_tags:
        filtered_procedures.append(proc_tags)
    else:
        filtered_procedures.append(["There are none"])  # Add a placeholder if no "Drugs" tag is found


In [20]:
print(len(filtered_procedures))
print(len(all_entities))

11026
11026


In [21]:
#Symptoms 

filtered_symptoms = []

# Iterate through both lists
for sentence, entity in zip(all_sentences, all_entities):
    sym_tags = [entity for entity in entity if "Symptoms" in entity]  # Filter "Drugs" tags
    if sym_tags:
        filtered_symptoms.append(sym_tags)
    else:
        filtered_symptoms.append(["There are none"])  # Add a placeholder if no "Drugs" tag is found


In [22]:
print(len(filtered_symptoms))
print(len(all_entities))

11026
11026


In [23]:
#Organisms 

filtered_organisms = []

# Iterate through both lists
for sentence, entity in zip(all_sentences, all_entities):
    org_tags = [entity for entity in entity if "Organism" in entity]  # Filter "Drugs" tags
    if org_tags:
        filtered_organisms.append(org_tags)
    else:
        filtered_organisms.append(["There are none"])  # Add a placeholder if no "Drugs" tag is found


In [24]:
print(len(filtered_organisms))
print(len(all_entities))

11026
11026


In [25]:

# Find indices and display lists containing "Organisms"
indices_with_organisms = [index for index, sublist in enumerate(filtered_organisms) if 'Organism' in sublist[0]]
lists_with_organisms = [sublist[0] for index, sublist in enumerate(filtered_organisms) if 'Organism' in sublist[0]]

# Display results
#print("Indices with 'Organisms':", indices_with_organisms)
#print("Lists with 'Organisms':", lists_with_organisms)
print(len(indices_with_organisms))

460


In [26]:
#Diseases 

filtered_diseases = []

# Iterate through both lists
for sentence, entity in zip(all_sentences, all_entities):
    dis_tags = [entity for entity in entity if "Diseases" in entity]  # Filter "Drugs" tags
    if dis_tags:
        filtered_diseases.append(dis_tags)
    else:
        filtered_diseases.append(["There are none"])  # Add a placeholder if no "Drugs" tag is found


In [27]:
print(len(filtered_diseases))
print(len(all_entities))

11026
11026


In [28]:
#Socialcontext

filtered_socialcontext = []

# Iterate through both lists
for sentence, entity in zip(all_sentences, all_entities):
    soc_tags = [entity for entity in entity if "Socialcontext" in entity]  # Filter "Drugs" tags
    if soc_tags:
        filtered_socialcontext.append(soc_tags)
    else:
        filtered_socialcontext.append(["There are none"])  # Add a placeholder if no "Drugs" tag is found


In [29]:
print(len(filtered_socialcontext))
print(len(all_entities))

11026
11026


In [30]:
#Anatomy 

filtered_anatomy = []

# Iterate through both lists
for sentence, entity in zip(all_sentences, all_entities):
    ana_tags = [entity for entity in entity if "Anatomy" in entity]  # Filter "Drugs" tags
    if ana_tags:
        filtered_anatomy.append(ana_tags)
    else:
        filtered_anatomy.append(["There are none"])  # Add a placeholder if no "Drugs" tag is found


In [31]:
print(len(filtered_anatomy))
print(len(all_entities))

11026
11026


In [32]:
#Specialty 

filtered_specialty = []

# Iterate through both lists
for sentence, entity in zip(all_sentences, all_entities):
    spe_tags = [entity for entity in entity if "Specialty" in entity]  # Filter "Drugs" tags
    if spe_tags:
        filtered_specialty.append(spe_tags)
    else:
        filtered_specialty.append(["There are none"])  # Add a placeholder if no "Drugs" tag is found


In [33]:
print(len(filtered_specialty))
print(len(all_entities))

11026
11026


In [34]:
#Substance 

filtered_substance = []

# Iterate through both lists
for sentence, entity in zip(all_sentences, all_entities):
    sub_tags = [entity for entity in entity if "Substance" in entity]  # Filter "Drugs" tags
    if sub_tags:
        filtered_substance.append(sub_tags)
    else:
        filtered_substance.append(["There are none"])  # Add a placeholder if no "Drugs" tag is found


In [35]:
print(len(filtered_substance))
print(len(all_entities))

11026
11026


In [36]:
#Qualifier 

filtered_qualifier = []

# Iterate through both lists
for sentence, entity in zip(all_sentences, all_entities):
    qual_tags = [entity for entity in entity if "Qualifier" in entity]  # Filter "Drugs" tags
    if qual_tags:
        filtered_qualifier.append(qual_tags)
    else:
        filtered_qualifier.append(["There are none"])  # Add a placeholder if no "Drugs" tag is found


In [37]:
print(len(filtered_qualifier))
print(len(all_entities))

11026
11026


In [38]:
#Clinicalfinding

filtered_cli = []

# Iterate through both lists
for sentence, entity in zip(all_sentences, all_entities):
    cli_tags = [entity for entity in entity if "Clinicalfinding" in entity]  # Filter "Drugs" tags
    if cli_tags:
        filtered_cli.append(cli_tags)
    else:
        filtered_cli.append(["There are none"])  # Add a placeholder if no "Drugs" tag is found


In [39]:
print(len(filtered_cli))
print(len(all_entities))

11026
11026


In [40]:
#Event 

filtered_event = []

# Iterate through both lists
for sentence, entity in zip(all_sentences, all_entities):
    eve_tags = [entity for entity in entity if "Event" in entity]  # Filter "Drugs" tags
    if eve_tags:
        filtered_event.append(eve_tags)
    else:
        filtered_event.append(["There are none"])  # Add a placeholder if no "Drugs" tag is found


In [41]:
print(len(filtered_event))
print(len(all_entities))

11026
11026


In [42]:
#Physicalobjects 

filtered_phy = []

# Iterate through both lists
for sentence, entity in zip(all_sentences, all_entities):
    phy_tags = [entity for entity in entity if "Physicalobjects" in entity]  # Filter "Drugs" tags
    if phy_tags:
        filtered_phy.append(phy_tags)
    else:
        filtered_phy.append(["There are none"])  # Add a placeholder if no "Drugs" tag is found


In [43]:
print(len(filtered_phy))
print(len(all_entities))

11026
11026


Procedures, Symptoms, Organism, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects.

['Procedures',
'Symptoms',
'Organism',
'Diseases',
'Anatomy',
'Specialty',
'Clinicalfinding',
'Drugs',]

removed - socialcontext, Substance, environmentgeographicallocation, qualifier, event, physical objects 

In [44]:
sentences_8 = all_sentences 
entities_8 = all_entities

In [45]:
all_entities = updated_entities
print(len(all_entities))
print(len(all_sentences))
print(len(sentences_8))
print(len(entities_8))

11026
11026
11026
11026


In [46]:
#template 1

In [47]:
import pandas as pd
import json

input_txt = all_sentences[:10]       
output = all_entities[:10]           

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Analyze the text and note below all the Procedures, Symptoms, Organisms,Diseases,Anatomy,Specialty, Clinicalfinding, Drugs",
        "input":f"{text}",
        "output":f"After analysing the text, the list of entities identified are {entities_str}" 
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 1.json", "w") as f:     
    f.write(output_json)


In [48]:
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Anatomies, Specialties, Clinical findings, Drugs"

In [49]:
#template 2

In [50]:
import pandas as pd
import json

input_txt = all_sentences[10:20]       
output = all_entities[10:20]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task": "Named Entity Recognition",
        "instruction": f"Read the following text and identify {list_of_entities}",
        "input": f"{text}",
        "output": entities_str  
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 2.json", "w") as f:     
    f.write(output_json)


In [51]:
#template 3

In [52]:
import pandas as pd
import json

input_txt = all_sentences[20:30]       
output = all_entities[20:30]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"What are the clinical named entities in the given text", 
        "input":f"{text}",
        "output":f"Here are the named clinical entities in the given text {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 3.json", "w") as f:     
    f.write(output_json)


In [53]:
#template 4

In [54]:
import pandas as pd
import json

input_txt = all_sentences[30:40]       
output = all_entities[30:40]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Identify the named entities and provide their entity types", 
        "input":f"{text}",
        "output":f"Here are the named entities: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 4.json", "w") as f:     
    f.write(output_json)


In [55]:
#template 5

In [56]:
import pandas as pd
import json

input_txt = all_sentences[40:50]       
output = all_entities[40:50]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":f"List all the entities from the below text from given entity list [{list_of_entities}].",
        "input":f"{text}",
        "output":f"Here are the entities listed: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 5.json", "w") as f:     
    f.write(output_json)

In [57]:
#template 6

In [58]:
import pandas as pd
import json

input_txt = all_sentences[50:60]       
output = all_entities[50:60]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":f"Examine below text and identify {list_of_entities}",
        "input":f"{text}",
        "output":f"After examining the text, the list of identified entities are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 6.json", "w") as f:     
    f.write(output_json)

In [59]:
#template 7

In [60]:
import pandas as pd
import json

input_txt = all_sentences[60:70]       
output = all_entities[60:70]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":f"Your task is to analyze the following text and note down all the {list_of_entities} mentioned",
        "input":f"{text}",
        "output":f"After analysing the text, the list of entities identified are {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 7.json", "w") as f:     
    f.write(output_json)

In [61]:
#template 8 

In [62]:
import pandas as pd
import json

input_txt = all_sentences[70:80]       
output = all_entities[70:80]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":f"In the given text, find and record all instances of the following {list_of_entities}.",
        "input":f"{text}",
        "output": f"Here are all recorded instances you requested: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 8.json", "w") as f:     
    f.write(output_json)

In [63]:
#template 9 

In [64]:
import pandas as pd
import json

input_txt = all_sentences[80:90]       
output = all_entities[80:90]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":f"Read the provided text and identify all the {list_of_entities} given below.",
        "input":f"{text}",
        "output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 9.json", "w") as f:     
    f.write(output_json)

In [65]:
#template 10 

In [66]:
import pandas as pd
import json

input_txt = all_sentences[90:100]       
output = all_entities[90:100]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":f"Analyze the provided text and identify all the {list_of_entities} mentioned. Record your findings below.",
        "input":f"{text}",
        "output":f"After analysing the text, the list of entities identified are {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 10.json", "w") as f:     
    f.write(output_json)

In [67]:
#template 11

In [68]:
import pandas as pd
import json

input_txt = all_sentences[100:110]       
output = all_entities[100:110]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":f"Your task is to analyze the following text and note any {list_of_entities} present in it.",
        "input":f"{text}",
        "output":f"After analysing the text, the list of entities identified are {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 11.json", "w") as f:     
    f.write(output_json)

In [69]:
#template 12

In [70]:
import pandas as pd
import json

input_txt = all_sentences[110:120]       
output = all_entities[110:120]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":f"Your task is to analyze the following text and note any {list_of_entities} present in it.",
        "input":f"{text}",
        "output":f"After analysing the text, the list of entities identified are {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 12.json", "w") as f:     
    f.write(output_json)

In [71]:
#template 13 

In [72]:
import pandas as pd
import json

input_txt = all_sentences[120:130]       
output = all_entities[120:130]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":f"Please examine the provided text and identify all the {list_of_entities} mentioned within it.",
        "input":f"{text}",
        "output":f"Here is the enumeration of entities that have been recognized in the input text: {entities_str}."
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 13.json", "w") as f:     
    f.write(output_json)

In [73]:
#template 14

In [74]:
import pandas as pd
import json

input_txt = all_sentences[130:140]       
output = all_entities[130:140]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":f"Could you kindly analyze the following text and identify any {list_of_entities} that you find?", 
        "input":f"{text}",
        "output":f"Here is the enumeration of entities that have been recognized in the input text: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 14.json", "w") as f:     
    f.write(output_json)

In [75]:
#template 15 

In [76]:
import pandas as pd
import json

input_txt = all_sentences[140:150]       
output = all_entities[140:150]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Please analyze the following text and make note of any {list_of_entities} mentioned in it.", 
"input":f"{text}",
"output":f"After analysing the text, the list of entities identified are {entities_str}."
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 15.json", "w") as f:     
    f.write(output_json)

In [77]:
#template 16

In [78]:
import pandas as pd
import json

input_txt = all_sentences[150:160]       
output = all_entities[150:160]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Please document the identified entities, along with their types, from the given text.", 
"input":f"{text}",
"output":f"Here is the enumeration of entities that have been documented in the input text: {entities_str}."
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 16.json", "w") as f:     
    f.write(output_json)

In [79]:
#template 17

In [80]:
import pandas as pd
import json

input_txt = all_sentences[160:170]       
output = all_entities[160:170]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Compile a complete list of recognized entities {list_of_entities} along with their types present in the input text.",
"input":f"{text}",
"output":f"These are the list of entities identified from the input text: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 17.json", "w") as f:     
    f.write(output_json)

In [81]:
#template 18

In [82]:
import pandas as pd
import json

input_txt = all_sentences[170:180]       
output = all_entities[170:180]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Present a comprehensive list of recognized entities along with their types here in the form {list_of_entities} from the input text.",
"input":f"{text}", 
"output":f"These are the list of entities identified from the input text: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 18.json", "w") as f:     
    f.write(output_json)

In [83]:
#template 19

In [84]:
import pandas as pd
import json

input_txt = all_sentences[180:190]       
output = all_entities[180:190]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Please go through the given text and note down all the medical concepts such as {list_of_entities} that you find.",
"input":f"{text}",
"output":f"The list of medical entities from the input text are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 19.json", "w") as f:     
    f.write(output_json)

In [85]:
#template 20

In [86]:
import pandas as pd
import json

input_txt = all_sentences[190:200]       
output = all_entities[190:200]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f" please analyze the given text and record any {list_of_entities} present in it?", 
"input":f"{text}",
"output":f"After analysing the text, the list of entities identified are {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 20.json", "w") as f:     
    f.write(output_json)

In [87]:
#template 21

In [88]:
import pandas as pd
import json

input_txt = all_sentences[200:210]       
output = all_entities[200:210]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Please analyze the following text and make note of any {list_of_entities} mentioned in it.", 
"input":f"{text}",
"output":f"After analysing the text, the list of entities identified are {entities_str}."
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 21.json", "w") as f:     
    f.write(output_json)

# single entity templates and all entities templates

In [89]:
#template 22-41

In [90]:
#template 22 - Drugs

In [91]:
import pandas as pd
import json

input_txt = all_sentences[210:220]       
output = filtered_tags_drugs[210:220]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Identify all the Drugs from the given text",
        "input":f"{text}",
        "output":f"Here are all the identified drugs: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 22.json", "w") as f:     
    f.write(output_json)

In [92]:
#template 23 - Drugs 

In [93]:
import pandas as pd
import json

input_txt = all_sentences[220:230]       
output = filtered_tags_drugs[220:230]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Analyze the given text and give me all the drugs",
        "input":f"{text}",
        "output":f"After analysing the text, the list of drugs are {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 23.json", "w") as f:     
    f.write(output_json)

In [94]:
#template 24 - substance 

In [95]:
import pandas as pd
import json

input_txt = all_sentences[230:240]       
output = filtered_substance[230:240]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Provide me a list of all substances from the below text",
        "input":f"{text}",
        "output":f"Here are all the list of substances from the text you gave: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 24.json", "w") as f:     
    f.write(output_json)

In [96]:
#template 25 - substance 

In [97]:
import pandas as pd
import json

input_txt = all_sentences[240:250]       
output = filtered_substance[240:250]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Identify all the substances from the given text",
        "input":f"{text}",
        "output":f"Here are all the list of substances from the text you gave: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 25.json", "w") as f:     
    f.write(output_json)

In [98]:
#template 26 - qualifier 

In [99]:
import pandas as pd
import json

input_txt = all_sentences[250:260]       
output = filtered_qualifier[250:260]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Identify all the qualifiers from the given text",
        "input":f"{text}",
        "output":f"Here are all the list of qualifiers from the text you gave:{entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 26.json", "w") as f:     
    f.write(output_json)

In [100]:
#template 27 - qualifier 

In [101]:
import pandas as pd
import json

input_txt = all_sentences[260:270]       
output = filtered_qualifier[260:270]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Provide me a list of all the qualifiers from the given text",
        "input":f"{text}",
        "output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 27.json", "w") as f:     
    f.write(output_json)

In [102]:
#template 28 - symptoms 

In [103]:
all_entities = entities_8 #entities_8 contains all entities 

In [104]:
filtered_symptoms = filtered_symptoms[270:]
sentences_sub = all_sentences
sentences_sub = sentences_sub[270:]

entities_sub = all_entities
entities_sub = entities_sub[270:]

In [105]:
print(len(filtered_symptoms))
print(len(sentences_sub))
print(len(entities_sub))
print(len(all_entities))
print(len(all_sentences))

10756
10756
10756
11026
11026


In [106]:
# Initialize the lists and indices
fil_symp = []
indices_to_remove = []
fil_sent = []

# Counters for the desired lists
symptoms_count = 0
none_count = 0

# Iterate over the filtered_symptoms_list
for i, sublist in enumerate(filtered_symptoms):
    if 'There are none' in sublist and none_count < 2:
        fil_symp.append(sublist)
        none_count += 1
        indices_to_remove.append(i)
        print(i)
    elif any('Symptoms' in tag for tag in sublist) and symptoms_count < 8:
        fil_symp.append(sublist)
        symptoms_count += 1
        indices_to_remove.append(i)
        print(i)
        
# Get 10 sentences using the remaining indices
for index in indices_to_remove[:10]:
    fil_sent.append(sentences_sub[index])

# Remove the extracted lists from filtered_symptoms_list
for index in sorted(indices_to_remove, reverse=True):
    del filtered_symptoms[index]

# Remove elements from 'sentences' list
for index in sorted(indices_to_remove, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(indices_to_remove, reverse=True):
    del entities_sub[index]
    
# Print the result
print("Extracted Lists:")
for sublist in fil_symp:
    print(sublist)
    
# Print the result
print("Extracted Sentences:")
for sentence in fil_sent:
    print(sentence)

0
1
2
5
8
10
11
19
21
31
Extracted Lists:
['There are none']
['@@progestin-only contraceptives:Symptoms##']
['There are none']
['@@OC failure:Symptoms##']
['@@at risk:Symptoms##', '@@noncompliance:Symptoms##', '@@OC failure:Symptoms##']
['@@progestin-only contraceptives:Symptoms##']
['@@adverse reactions:Symptoms##']
['@@exposure:Symptoms##']
['@@clinical significance:Symptoms##']
['@@pressure:Symptoms##', '@@increased risk:Symptoms##']
Extracted Sentences:
During long-term antibiotic administration, the risk for drug interaction with OCs is less clear, but alternative or additional contraception may be advisable in selected circumstances. 
Data regarding progestin-only contraceptives or for newer combined contraceptive deliveries (e.g., patches, rings) are not available. 
Estradiol: (Moderate) It was previously thought that antibiotics may decrease the effectiveness of oral contraceptives containing estrogens due to stimulation of estrogen metabolism or a reduction in estrogen enteroh

In [107]:
print(len(fil_symp))
print(len(filtered_symptoms))
print(len(sentences_sub))
print(len(entities_sub))
print(len(fil_sent))

10
10746
10746
10746
10


In [108]:
print(fil_sent[6])
print(fil_symp[6])

 Everolimus: (Moderate) Monitor everolimus whole blood trough concentrations as appropriate and watch for everolimus-related adverse reactions if coadministration with sarecycline is necessary. 
['@@adverse reactions:Symptoms##']


In [109]:
import pandas as pd
import json

input_txt = fil_sent      
output = fil_symp           
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Identify all the Symptoms from the given text",
        "input":f"{text}",
        "output":f"These are the identitfied symtoms in the text: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 28.json", "w") as f:     
    f.write(output_json)

In [110]:
#template 29 - Diseases 

In [111]:
#Diseases 

filtered_diseases = []

# Iterate through both lists
for sentence, entity in zip(sentences_sub, entities_sub):
    dis_tags = [entity for entity in entity if "Diseases" in entity]  # Filter "Drugs" tags
    if dis_tags:
        filtered_diseases.append(dis_tags)
    else:
        filtered_diseases.append(["There are none"])  # Add a placeholder if no "Drugs" tag is found
        
        
print(len(filtered_diseases))
print(len(sentences_sub))
print(len(entities_sub))

10746
10746
10746


In [112]:
# Initialize the lists and indices
fil_symp = []
indices_to_remove = []
fil_sent = []

# Counters for the desired lists
symptoms_count = 0
none_count = 0

# Iterate over the filtered_symptoms_list
for i, sublist in enumerate(filtered_diseases):           ##change##
    if 'There are none' in sublist and none_count < 2:
        fil_symp.append(sublist)
        none_count += 1
        indices_to_remove.append(i)
        #print(i)
    elif any('Diseases' in tag for tag in sublist) and symptoms_count < 8:        ##change##
        fil_symp.append(sublist)
        symptoms_count += 1
        indices_to_remove.append(i)
        #print(i)
        
# Get 10 sentences using the remaining indices
for index in indices_to_remove[:10]:
    fil_sent.append(sentences_sub[index])        

# Remove the extracted lists from filtered_symptoms_list
for index in sorted(indices_to_remove, reverse=True):
    del filtered_diseases[index]              ##change##

# Remove elements from 'sentences' list
for index in sorted(indices_to_remove, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(indices_to_remove, reverse=True):
    del entities_sub[index]
    
# Print the result
print("Extracted Lists:")
for sublist in fil_symp:
    print(sublist)
    
# Print the result
print("Extracted Sentences:")
for sentence in fil_sent:
    print(sentence)

Extracted Lists:
['There are none']
['There are none']
['@@phototoxicity:Diseases##']
['@@Pseudotumor:Diseases##', '@@Pseudotumor cerebri:Diseases##']
['@@headache:Diseases##']
['@@infections:Diseases##']
['@@infections:Diseases##']
['@@hepatotoxicity:Diseases##']
['@@hepatotoxic:Diseases##']
['@@toxicities:Diseases##', '@@ventricular tachycardia:Diseases##', '@@tachycardia:Diseases##', '@@torsade:Diseases##', '@@torsade de pointes:Diseases##', '@@cardiac arrest:Diseases##', '@@cardiac toxicities:Diseases##']
Extracted Sentences:
One retrospective study reviewed the literature to determine the effects of oral antibiotics on the pharmacokinetics of contraceptive estrogens and progestins, and also examined clinical studies in which the incidence of pregnancy with oral contraceptives (OCs) and antibiotics was reported. 
It was concluded that the antibiotics ampicillin, ciprofloxacin, clarithromycin, doxycycline, metronidazole, ofloxacin, roxithromycin, temafloxacin, and tetracycline did n

In [113]:
print(len(fil_symp))
print(len(filtered_diseases))
print(len(sentences_sub))
print(len(entities_sub))
print(len(fil_sent))
print(len(all_entities))

10
10736
10736
10736
10
11026


In [114]:
print(fil_sent[6])
print(fil_symp[6])

The clinical relevance of this interaction is poorly defined and for many infections the benefits of combination therapy are likely to outweigh the potential risks. 
['@@infections:Diseases##']


In [115]:
import pandas as pd
import json

input_txt = fil_sent      
output = fil_symp           
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"List all the diseases from the below text",
        "input":f"{text}",
        "output":f"These are the identified diseases from the text: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 29.json", "w") as f:     
    f.write(output_json)

In [116]:
#template 30 - Clinicalfinding

In [117]:
#Clinicalfinding

filtered_cli = []

# Iterate through both lists
for sentence, entity in zip(sentences_sub, entities_sub):
    cli_tags = [entity for entity in entity if "Clinicalfinding" in entity]  # Filter "Drugs" tags
    if cli_tags:
        filtered_cli.append(cli_tags)
    else:
        filtered_cli.append(["There are none"])  # Add a placeholder if no "Drugs" tag is found
        
print(len(filtered_cli))
print(len(sentences_sub))
print(len(entities_sub))

10736
10736
10736


In [118]:
# Initialize the lists and indices
fil_symp = []
indices_to_remove = []
fil_sent = []

# Counters for the desired lists
symptoms_count = 0
none_count = 0

# Iterate over the filtered_symptoms_list
for i, sublist in enumerate(filtered_cli):           ##change##
    if 'There are none' in sublist and none_count < 2:
        fil_symp.append(sublist)
        none_count += 1
        indices_to_remove.append(i)
        #print(i)
    elif any('Clinicalfinding' in tag for tag in sublist) and symptoms_count < 8:        ##change##
        fil_symp.append(sublist)
        symptoms_count += 1
        indices_to_remove.append(i)
        #print(i)
        
# Get 10 sentences using the remaining indices
for index in indices_to_remove[:10]:
    fil_sent.append(sentences_sub[index])        

# Remove the extracted lists from filtered_symptoms_list
for index in sorted(indices_to_remove, reverse=True):
    del filtered_cli[index]              ##change##

# Remove elements from 'sentences' list
for index in sorted(indices_to_remove, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(indices_to_remove, reverse=True):
    del entities_sub[index]
    
# Print the result
print("Extracted Lists:")
for sublist in fil_symp:
    print(sublist)
    
# Print the result
print("Extracted Sentences:")
for sentence in fil_sent:
    print(sentence)

Extracted Lists:
['There are none']
['@@experienced:Clinicalfinding##', '@@ovulate:Clinicalfinding##']
['There are none']
['@@according:Clinicalfinding##']
['@@binding:Clinicalfinding##']
['@@concentrations:Clinicalfinding##', '@@response:Clinicalfinding##']
['@@oral absorption:Clinicalfinding##']
['@@Bacterostatic:Clinicalfinding##', '@@bactericidal:Clinicalfinding##']
['@@interact:Clinicalfinding##']
['@@QT:Clinicalfinding##']
Extracted Sentences:
Based on the study results, these authors recommended that back-up contraception may not be necessary if OCs are used reliably during oral antibiotic use. 
Another review of the subject concurred with these data, but noted that individual patients have been identified who experienced significant decreases in plasma concentrations of combined OC components and who appeared to ovulate; the agents most often associated with these changes were rifampin, tetracyclines and penicillin derivatives. 
During long-term antibiotic administration, the r

In [119]:
print(len(fil_symp))
print(len(filtered_cli))
print(len(sentences_sub))
print(len(entities_sub))
print(len(fil_sent))
print(len(all_entities))

10
10726
10726
10726
10
11026


In [120]:
print(fil_sent[3])
print(fil_symp[3])

Heparin: (Minor) Tetracyclines may partially counteract the anticoagulant actions of heparin, according to the product labels. 
['@@according:Clinicalfinding##']


In [121]:
import pandas as pd
import json

input_txt = fil_sent      
output = fil_symp           
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Examine the text to identify all the Clinicalfindings",
        "input":f"{text}",
        "output":f"These are the identified diseases from the text: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 30.json", "w") as f:     
    f.write(output_json)

In [122]:
#template 31 - Anatomy

In [123]:
#Anatomy 

filtered_anatomy = []

# Iterate through both lists
for sentence, entity in zip(sentences_sub, entities_sub):
    ana_tags = [entity for entity in entity if "Anatomy" in entity]  # Filter "Drugs" tags
    if ana_tags:
        filtered_anatomy.append(ana_tags)
    else:
        filtered_anatomy.append(["There are none"])  # Add a placeholder if no "Drugs" tag is found
        
print(len(filtered_anatomy))
print(len(sentences_sub))
print(len(entities_sub))

10726
10726
10726


In [124]:
# Initialize the lists and indices
fil_symp = []
indices_to_remove = []
fil_sent = []

# Counters for the desired lists
symptoms_count = 0
none_count = 0

# Iterate over the filtered_symptoms_list
for i, sublist in enumerate(filtered_anatomy):           ##change##
    if 'There are none' in sublist and none_count < 2:
        fil_symp.append(sublist)
        none_count += 1
        indices_to_remove.append(i)
        #print(i)
    elif any('Anatomy' in tag for tag in sublist) and symptoms_count < 8:        ##change##
        fil_symp.append(sublist)
        symptoms_count += 1
        indices_to_remove.append(i)
        #print(i)
        
# Get 10 sentences using the remaining indices
for index in indices_to_remove[:10]:
    fil_sent.append(sentences_sub[index])        

# Remove the extracted lists from filtered_symptoms_list
for index in sorted(indices_to_remove, reverse=True):
    del filtered_anatomy[index]              ##change##

# Remove elements from 'sentences' list
for index in sorted(indices_to_remove, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(indices_to_remove, reverse=True):
    del entities_sub[index]
    
print(len(fil_symp))
print(len(filtered_anatomy))
print(len(sentences_sub))
print(len(entities_sub))
print(len(fil_sent))
print(fil_sent[3])
print(fil_symp[3])

10
10716
10716
10716
10
Iron may decrease the oral bioavailability of tetracyclines. 
['@@oral:Anatomy##']


In [125]:
import pandas as pd
import json

input_txt = fil_sent      
output = fil_symp           
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Go through the given sentence and identify all anatomy terms",
        "input":f"{text}",
        "output":f"These are the identified anatomies from the text: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 31.json", "w") as f:     
    f.write(output_json)

In [126]:
#template 32 - Organism 

In [127]:
#Organisms 

filtered_organisms = []

# Iterate through both lists
for sentence, entity in zip(sentences_sub, entities_sub):
    org_tags = [entity for entity in entity if "Organism" in entity]  # Filter "Drugs" tags
    if org_tags:
        filtered_organisms.append(org_tags)
    else:
        filtered_organisms.append(["There are none"])  # Add a placeholder if no "Drugs" tag is found
        
print(len(filtered_organisms))
print(len(sentences_sub))
print(len(entities_sub))

10716
10716
10716


In [128]:
# Initialize the lists and indices
fil_symp = []
indices_to_remove = []
fil_sent = []

# Counters for the desired lists
symptoms_count = 0
none_count = 0

# Iterate over the filtered_symptoms_list
for i, sublist in enumerate(filtered_organisms):           ##change##
    if 'There are none' in sublist and none_count < 2:
        fil_symp.append(sublist)
        none_count += 1
        indices_to_remove.append(i)
        #print(i)
    elif any('Organism' in tag for tag in sublist) and symptoms_count < 8:        ##change##
        fil_symp.append(sublist)
        symptoms_count += 1
        indices_to_remove.append(i)
        #print(i)
        
# Get 10 sentences using the remaining indices
for index in indices_to_remove[:10]:
    fil_sent.append(sentences_sub[index])        

# Remove the extracted lists from filtered_symptoms_list
for index in sorted(indices_to_remove, reverse=True):
    del filtered_organisms[index]              ##change##

# Remove elements from 'sentences' list
for index in sorted(indices_to_remove, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(indices_to_remove, reverse=True):
    del entities_sub[index]
    
print(len(fil_symp))
print(len(filtered_organisms))       ##change##
print(len(sentences_sub))
print(len(entities_sub))
print(len(fil_sent))
print(fil_sent[3])
print(fil_symp[3])

10
10706
10706
10706
10
  St. John&apos;s Wort, Hypericum perforatum: (Moderate) St. John&apos;s Wort is known to cause photosensitivity. 
['@@Hypericum:Organism##']


In [129]:
import pandas as pd
import json

input_txt = fil_sent      
output = fil_symp           
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"List all the Organisms from the below text",
        "input":f"{text}",
        "output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 32.json", "w") as f:     
    f.write(output_json)

In [130]:
#template 33 - Procedures 

In [131]:
#Procedures

filtered_procedures = []

# Iterate through both lists
for sentence, entity in zip(sentences_sub, entities_sub):
    proc_tags = [entity for entity in entity if "Procedures" in entity]  # Filter "Drugs" tags
    if proc_tags:
        filtered_procedures.append(proc_tags)
    else:
        filtered_procedures.append(["There are none"])  # Add a placeholder if no "Drugs" tag is found
        
print(len(filtered_procedures))
print(len(sentences_sub))
print(len(entities_sub))

10706
10706
10706


In [132]:
# Initialize the lists and indices
fil_symp = []
indices_to_remove = []
fil_sent = []

# Counters for the desired lists
symptoms_count = 0
none_count = 0

# Iterate over the filtered_symptoms_list
for i, sublist in enumerate(filtered_procedures):           ##change##
    if 'There are none' in sublist and none_count < 2:
        fil_symp.append(sublist)
        none_count += 1
        indices_to_remove.append(i)
        #print(i)
    elif any('Procedures' in tag for tag in sublist) and symptoms_count < 8:        ##change##
        fil_symp.append(sublist)
        symptoms_count += 1
        indices_to_remove.append(i)
        #print(i)
        
# Get 10 sentences using the remaining indices
for index in indices_to_remove[:10]:
    fil_sent.append(sentences_sub[index])        

# Remove the extracted lists from filtered_symptoms_list
for index in sorted(indices_to_remove, reverse=True):
    del filtered_procedures[index]              ##change##

# Remove elements from 'sentences' list
for index in sorted(indices_to_remove, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(indices_to_remove, reverse=True):
    del entities_sub[index]
    
print(len(fil_symp))
print(len(filtered_procedures))       ##change##
print(len(sentences_sub))
print(len(entities_sub))
print(len(fil_sent))
print(fil_sent[3])
print(fil_symp[3])

10
10696
10696
10696
10
 Lefamulin: (Moderate) Monitor for lefamulin-related adverse effects if oral lefamulin is administered with sarecycline as concurrent use may increase exposure from lefamulin tablets; an interaction is not expected with intravenous lefamulin. 
['@@Monitor:Procedures##']


In [133]:
import pandas as pd
import json

input_txt = fil_sent      
output = fil_symp           
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Identify all the procedures from the given text",
        "input":f"{text}",
        "output":f"These are the identified procedures from the text {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 33.json", "w") as f:     
    f.write(output_json)

In [134]:
#template 34 - specialty 

In [135]:
#Specialty 

filtered_specialty = []

# Iterate through both lists
for sentence, entity in zip(sentences_sub, entities_sub):
    spe_tags = [entity for entity in entity if "Specialty" in entity]  # Filter "Drugs" tags
    if spe_tags:
        filtered_specialty.append(spe_tags)
    else:
        filtered_specialty.append(["There are none"])  # Add a placeholder if no "Drugs" tag is found

print(len(filtered_specialty))
print(len(sentences_sub))
print(len(entities_sub))

10696
10696
10696


In [136]:
# Initialize the lists and indices
fil_symp = []
indices_to_remove = []
fil_sent = []

# Counters for the desired lists
symptoms_count = 0
none_count = 0

# Iterate over the filtered_symptoms_list
for i, sublist in enumerate(filtered_specialty):           ##change##
    if 'There are none' in sublist and none_count < 2:
        fil_symp.append(sublist)
        none_count += 1
        indices_to_remove.append(i)
        #print(i)
    elif any('Specialty' in tag for tag in sublist) and symptoms_count < 8:        ##change##
        fil_symp.append(sublist)
        symptoms_count += 1
        indices_to_remove.append(i)
        #print(i)
        
# Get 10 sentences using the remaining indices
for index in indices_to_remove[:10]:
    fil_sent.append(sentences_sub[index])        

# Remove the extracted lists from filtered_symptoms_list
for index in sorted(indices_to_remove, reverse=True):
    del filtered_specialty[index]              ##change##

# Remove elements from 'sentences' list
for index in sorted(indices_to_remove, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(indices_to_remove, reverse=True):
    del entities_sub[index]
    
print(len(fil_symp))
print(len(filtered_specialty))       ##change##
print(len(sentences_sub))
print(len(entities_sub))
print(len(fil_sent))
print(fil_sent[3])
print(fil_symp[3])

10
10686
10686
10686
10
Renal biopsy is the gold standard for confirming diagnosis of nephritic syndrome and plays an important role in guiding treatment. 
['@@guiding:Specialty##']


In [137]:
import pandas as pd
import json

input_txt = fil_sent      
output = fil_symp           
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Go through the given sentence and identify all specialty terms",
        "input":f"{text}",
        "output":f"These are the identified specialties from the text: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 34.json", "w") as f:     
    f.write(output_json)

In [138]:
#template 35 - environment ##not possible to do 

In [139]:
#template 35

In [140]:
filtered_socialcontext = []

# Iterate through both lists
for sentence, entity in zip(sentences_sub, entities_sub):
    soc_tags = [entity for entity in entity if "Socialcontext" in entity]  # Filter "Drugs" tags
    if soc_tags:
        filtered_socialcontext.append(soc_tags)
    else:
        filtered_socialcontext.append(["There are none"])  # Add a placeholder if no "Drugs" tag is found

print(len(filtered_socialcontext))
print(len(sentences_sub))
print(len(entities_sub))

10686
10686
10686


In [141]:
# Initialize the lists and indices
fil_symp = []
indices_to_remove = []
fil_sent = []

# Counters for the desired lists
symptoms_count = 0
none_count = 0

# Iterate over the filtered_symptoms_list
for i, sublist in enumerate(filtered_socialcontext):           ##change##
    if 'There are none' in sublist and none_count < 2:
        fil_symp.append(sublist)
        none_count += 1
        indices_to_remove.append(i)
        #print(i)
    elif any('Socialcontext' in tag for tag in sublist) and symptoms_count < 8:        ##change##
        fil_symp.append(sublist)
        symptoms_count += 1
        indices_to_remove.append(i)
        #print(i)
        
# Get 10 sentences using the remaining indices
for index in indices_to_remove[:10]:
    fil_sent.append(sentences_sub[index])        

# Remove the extracted lists from filtered_symptoms_list
for index in sorted(indices_to_remove, reverse=True):
    del filtered_socialcontext[index]              ##change##

# Remove elements from 'sentences' list
for index in sorted(indices_to_remove, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(indices_to_remove, reverse=True):
    del entities_sub[index]
    
print(len(fil_symp))
print(len(filtered_socialcontext))       ##change##
print(len(sentences_sub))
print(len(entities_sub))
print(len(fil_sent))
print(fil_sent[3])
print(fil_symp[3])

10
10676
10676
10676
10
  Magnesium Sulfate; Potassium Sulfate; Sodium Sulfate: (Major) Administer tetracyclines at least 2 hours before or 6 hours after administration of magnesium sulfate; potassium sulfate; sodium sulfate. 
['@@administration:Socialcontext##']


In [142]:
import pandas as pd
import json

input_txt = fil_sent      
output = fil_symp           
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Identify all the Socialcontexts from the text given below",
        "input":f"{text}",
        "output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 35.json", "w") as f:     
    f.write(output_json)

# All entities / all entity

In [143]:
#template 36-42 (template 16-21 in excel) ----done after 2 entity combination templates

# 2 entity combination templates (10 * 3)

In [144]:
#template 43-73

In [145]:
sent_sub1 = sentences_sub
ent_sub1 = entities_sub

In [146]:
#print(len(filtered_dipr))
print(len(sentences_sub))
print(len(entities_sub))
print(len(sent_sub1))
print(len(ent_sub1))
print(len(all_entities))
print(len(all_sentences))

10676
10676
10676
10676
11026
11026


In [147]:
len(all_entities)
len(all_sentences)

11026

In [148]:
# Find sentences with both "Drugs" and "Symptoms" tags
selected_sentences = []
selected_annotations = []
indices = []

for i, sentence in enumerate(sentences_sub):
    annotations = entities_sub[i]
    
    # Check if "Drugs" and "Symptoms" tags are both present in annotations
    if any("Drugs" in tag for tag in annotations) and any("Symptoms" in tag for tag in annotations):
        selected_sentences.append(sentence)
        
        # Filter annotations to include only "Drugs" and "Symptoms" tags
        filtered_annotations = [tag for tag in annotations if "Drugs" in tag or "Symptoms" in tag]
        selected_annotations.append(filtered_annotations)
        indices.append(i)

# Print the selected sentences and their corresponding filtered annotations
for sentence, annotations in zip(selected_sentences, selected_annotations):
    print("Sentence:", sentence)
    print("Annotations:", annotations)
    print("-" * 30)



Sentence: Coadministration may impair absorption of sarecycline which may decrease its efficacy. 
Annotations: ['@@sarecycline:Drugs##', '@@impair:Symptoms##']
------------------------------
Sentence:  Photosensitizing agents (topical): (Moderate) Tetracyclines cause photosensitivity and may increase the photosensitizing effects photosensitizing agents used in photodynamic therapy. 
Annotations: ['@@photosensitivity:Symptoms##', '@@Photosensitizing:Drugs##', '@@Photosensitizing agents:Drugs##', '@@photosensitizing:Drugs##', '@@photosensitizing:Drugs##', '@@photosensitizing agents:Drugs##']
------------------------------
Sentence: Prevention of photosensitivity includes adequate protection from sources of UV radiation and the use of protective clothing and sunscreens on exposed skin. 
Annotations: ['@@photosensitivity:Symptoms##', '@@protection:Symptoms##', '@@sources:Symptoms##', '@@protective:Symptoms##', '@@sunscreens:Drugs##']
------------------------------
Sentence: Concomitant use

Sentence: Ponatinib is a CYP3A4 substrate and rifapentine is a strong CYP3A4 inducer. 
Annotations: ['@@Ponatinib:Drugs##', '@@rifapentine:Drugs##', '@@CYP3A4 inducer:Symptoms##']
------------------------------
Sentence: Coadministration with another strong CYP3A4 inducer decreased ponatinib exposure by 62%. 
Annotations: ['@@CYP3A4 inducer:Symptoms##', '@@ponatinib:Drugs##', '@@exposure:Symptoms##']
------------------------------
Sentence:  Ritonavir: (Major) Avoid coadministration of ponatinib and ritonavir due to the potential for increased ponatinib exposure. 
Annotations: ['@@Ritonavir:Drugs##', '@@ponatinib:Drugs##', '@@ritonavir:Drugs##', '@@ponatinib:Drugs##', '@@exposure:Symptoms##']
------------------------------
Sentence: After ritonavir has been discontinued for 3 to 5 half-lives, resume the dose of ponatinib that was tolerated prior to starting ritonavir. 
Annotations: ['@@ritonavir:Drugs##', '@@discontinued:Symptoms##', '@@ponatinib:Drugs##', '@@ritonavir:Drugs##']
------

------------------------------
Sentence: However, iron deficiency may develop, especially in children and menstruating or pregnant women, or as a result of the low copper diet recommended for Wilson&apos;s disease. 
Annotations: ['@@iron:Drugs##', '@@deficiency:Symptoms##', '@@diet:Symptoms##']
------------------------------
Sentence:   Phosphorated Carbohydrate Solution: (Moderate) It has been reported that high intakes of phosphates, such as are found in dietary supplements or food additives, can interfere with absorption of trace nutrients such as iron, copper, and zinc. 
Annotations: ['@@Phosphorated Carbohydrate Solution:Drugs##', '@@dietary:Symptoms##', '@@iron:Drugs##']
------------------------------
Sentence:  Phosphorus: (Moderate) It has been reported that high intakes of phosphates, such as are found in dietary supplements or food additives, can interfere with absorption of trace nutrients such as iron, copper, and zinc. 
Annotations: ['@@dietary:Symptoms##', '@@iron:Drugs##

Sentence: Make review of immunization status and administration of indicated vaccines a routine part of clinical practice in ambulatory and hospitalized patients. 
Annotations: ['@@immunization status:Symptoms##', '@@vaccines:Drugs##']
------------------------------
Sentence: Passive immunization involves transfer of immunoglobulin derived from human or animal sources. 
Annotations: ['@@immunoglobulin:Drugs##', '@@sources:Symptoms##']
------------------------------
Sentence: Ascertain whether the patient has behavioral, occupational, or other exposures that may indicate the need for certain vaccines (eg, hepatitis B vaccine for people who engage in risky sexual behaviors; rabies vaccine for veterinary personnel). 
Annotations: ['@@exposures:Symptoms##', '@@vaccines:Drugs##', '@@hepatitis B vaccine:Drugs##', '@@vaccine:Drugs##', '@@behaviors:Symptoms##', '@@rabies vaccine:Drugs##', '@@vaccine:Drugs##']
------------------------------
Sentence: Review patient history about adverse reactio

Annotations: ['@@Amoxicillin:Drugs##', '@@Clarithromycin:Drugs##', '@@Omeprazole:Drugs##', '@@Contraindicated:Symptoms##', '@@ubrogepant:Drugs##', '@@clarithromycin:Drugs##', '@@contraindicated:Symptoms##', '@@ubrogepant:Drugs##', '@@exposure:Symptoms##', '@@adverse effects:Symptoms##']
------------------------------
Sentence: Coadministration with another strong CYP3A4 inhibitor resulted in a 9.7-fold increase in the exposure of ubrogepant. 
Annotations: ['@@exposure:Symptoms##', '@@ubrogepant:Drugs##']
------------------------------
Sentence: Apalutamide: (Major) Avoid the coadministration of ubrogepant and apalutamide as concurrent use may decrease ubrogepant exposure and reduce the efficacy. 
Annotations: ['@@Apalutamide:Drugs##', '@@ubrogepant:Drugs##', '@@apalutamide:Drugs##', '@@ubrogepant:Drugs##', '@@exposure:Symptoms##']
------------------------------
Sentence: Ubrogepant is a CYP3A4 substrate; apalutamide is a strong CYP3A4 inducer. 
Annotations: ['@@Ubrogepant:Drugs##', '@@

...

Annotations: ['@@exposed to:Symptoms##', '@@valproate:Drugs##']
------------------------------
Sentence: Transient hepatic dysfunction may occur in neonates and infants exposed to carbamazepine. 
Annotations: ['@@exposed to:Symptoms##', '@@carbamazepine:Drugs##']
------------------------------
Sentence: Conditions predisposing to lithium toxicity include preeclampsia and hyperemesis gravidarum; use of diuretics also increases likelihood of lithium toxicity. 
Annotations: ['@@lithium:Drugs##', '@@hyperemesis gravidarum:Symptoms##', '@@diuretics:Drugs##', '@@lithium:Drugs##']
------------------------------
Sentence: Discontinue lithium at onset of labor or 24 to 48 hours before induction or elective cesarean to avoid lithium toxicity in the neonate. 
Annotations: ['@@lithium:Drugs##', '@@onset of labor:Symptoms##', '@@lithium:Drugs##']
------------------------------
Sentence: Close clinical monitoring for toxicity is indicated for any neonate/infant exposed to medications, particularly m

Annotations: ['@@mitapivat:Drugs##', '@@discontinued:Symptoms##', '@@signs:Symptoms##']
------------------------------
Sentence: Hydrocodone is a CYP3A substrate and mitapivat is a weak CYP3A inducer.
Annotations: ['@@mitapivat:Drugs##', '@@weak:Symptoms##']
------------------------------
Sentence:  Ciprofloxacin: (Moderate) Do not exceed mitapivat 20 mg PO twice daily during coadministration with ciprofloxacin and monitor hemoglobin and for adverse reactions from mitapivat. 
Annotations: ['@@mitapivat:Drugs##', '@@mitapivat:Drugs##', '@@adverse reactions:Symptoms##']
------------------------------
Sentence:  Clarithromycin: (Major) Avoid coadministration of mitapivat with clarithromycin due to increased risk of adverse reactions from mitapivat. 
Annotations: ['@@mitapivat:Drugs##', '@@increased risk:Symptoms##', '@@mitapivat:Drugs##', '@@adverse reactions:Symptoms##']
------------------------------
Sentence: When mitapivat is discontinued, reduce the clozapine dose based on clinical r

Annotations: ['@@Guaiacolsulfonate:Drugs##', '@@signs:Symptoms##', '@@mitapivat:Drugs##']
------------------------------
Sentence: If mitapivat is discontinued, consider a dose reduction of hydrocodone and frequently monitor for signs of respiratory depression and sedation. 
Annotations: ['@@mitapivat:Drugs##', '@@discontinued:Symptoms##', '@@signs:Symptoms##']
------------------------------
Sentence: Hydrocodone is a CYP3A substrate and mitapivat is a weak CYP3A inducer. 
Annotations: ['@@mitapivat:Drugs##', '@@weak:Symptoms##']
------------------------------
Sentence:  Hydrocodone; Potassium Guaiacolsulfonate; Pseudoephedrine: (Moderate) Monitor for reduced efficacy of hydrocodone and signs of opioid withdrawal if coadministration with mitapivat is necessary; consider increasing the dose of hydrocodone as needed. 
Annotations: ['@@Guaiacolsulfonate:Drugs##', '@@signs:Symptoms##', '@@mitapivat:Drugs##']
------------------------------
Sentence: If mitapivat is discontinued, consider a 

Sentence:  Tenofovir, PMPA: (Moderate) Coadministration of tenofovir disoproxil fumarate with mitapivat may result in increased plasma concentrations of tenofovir, leading to an increase in tenofovir-related adverse effects. 
Annotations: ['@@mitapivat:Drugs##', '@@adverse effects:Symptoms##']
------------------------------
Sentence:  Tipranavir: (Major) Avoid coadministration of mitapivat with tipranavir due to increased risk of adverse reactions. 
Annotations: ['@@mitapivat:Drugs##', '@@increased risk:Symptoms##', '@@adverse reactions:Symptoms##']
------------------------------
Sentence:  Tramadol: (Moderate) Monitor for reduced efficacy of tramadol and signs of opioid withdrawal if coadministration with mitapivat is necessary; consider increasing the dose of tramadol as needed. 
Annotations: ['@@signs:Symptoms##', '@@mitapivat:Drugs##']
------------------------------
Sentence: If mitapivat is discontinued, consider a dose reduction of tramadol and frequently monitor for seizures, se

Sentence:  Potassium Phosphate; Sodium Phosphate: (Moderate) It has been reported that high intakes of phosphates, such as are found in dietary supplements or food additives, can interfere with absorption of trace nutrients such as iron, copper, and zinc. 
Annotations: ['@@Potassium Phosphate:Drugs##', '@@Sodium Phosphate:Drugs##', '@@dietary:Symptoms##', '@@iron:Drugs##']
------------------------------
Sentence: However, iron deficiency may develop, especially in children and menstruating or pregnant women, or as a result of the low copper diet recommended for Wilson&apos;s disease. 
Annotations: ['@@iron:Drugs##', '@@deficiency:Symptoms##', '@@diet:Symptoms##']
------------------------------
Sentence: Polysaccharide-iron complex elixirs can produce tooth discoloration, a superficial and temporary staining of tooth enamel.
Annotations: ['@@iron:Drugs##', '@@tooth discoloration:Symptoms##', '@@discoloration:Symptoms##', '@@staining of tooth:Symptoms##']
------------------------------
S

In [149]:
print(len(selected_annotations))
print(len(selected_sentences))
entities_sub[49]
sentences_sub[49]

1695
1695


'The clinical relevance of this interaction is poorly defined and for many infections the benefits of combination therapy are likely to outweigh the potential risks. '

In [150]:
sentences_dummy = sentences_sub
entities_dummy = entities_sub

In [151]:
print(len(sentences_dummy))
print(len(entities_dummy))

10676
10676


In [152]:
#template 43 

In [153]:
import pandas as pd
import json

input_txt = selected_sentences[0:10]           ####change####  
output = selected_annotations[0:10]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Give me all the Drugs and symptoms from the text given below",
        "input":f"{text}",
        "output":f"Here are all the Drugs and Symptoms {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 43.json", "w") as f:     ####change####
    f.write(output_json)

In [154]:
#template 44

In [155]:
import pandas as pd
import json

input_txt = selected_sentences[10:20]           ####change####  
output = selected_annotations[10:20]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Provide me with the list of all drugs and symptoms from the text",
        "input":f"{text}",
        "output":f"These are the list of all the drugs and symptoms in the text{entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 44.json", "w") as f:     ####change####
    f.write(output_json)

In [156]:
#template 45

In [157]:
import pandas as pd
import json

input_txt = selected_sentences[20:30]           ####change####  
output = selected_annotations[20:30]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Examine the text and give me with the list of all drugs and symptoms from the text",
        "input":f"{text}",
        "output":f"After examining the text, the list of entities identified are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 45.json", "w") as f:     ####change####
    f.write(output_json)

In [158]:
#template 46

In [159]:
import pandas as pd
import json

input_txt = selected_sentences[30:40]           ####change####  
output = selected_annotations[30:40]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Recognize the drugs and symptoms in the following text",
        "input":f"{text}",
        "output":f"These are the recognized drugs and symptoms in the text: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 46.json", "w") as f:     ####change####
    f.write(output_json)

In [160]:
#template 47

In [161]:
import pandas as pd
import json

input_txt = selected_sentences[40:50]           ####change####  
output = selected_annotations[40:50]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Extract the drugs and symptoms from the following text",
        "input":f"{text}",
        "output":f"The extracted drugs and symptoms are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 47.json", "w") as f:     ####change####
    f.write(output_json)

In [162]:
# Remove elements from 'sentences' list
idx = indices[0:50]
for index in sorted(idx, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(idx, reverse=True):
    del entities_sub[index]
    
print(len(sentences_sub))
print(len(entities_sub))

10626
10626


In [163]:
#template 48-52 diseases and procedures 

In [164]:
print(len(all_entities))
print(len(all_sentences))

11026
11026


In [165]:
# Find sentences with both "Drugs" and "Symptoms" tags
selected_sentences = []
selected_annotations = []
indices = []

for i, sentence in enumerate(sentences_sub):
    annotations = entities_sub[i]
    
    # Check if "Drugs" and "Symptoms" tags are both present in annotations
    if any("Diseases" in tag for tag in annotations) and any("Procedures" in tag for tag in annotations):
        selected_sentences.append(sentence)
        
        # Filter annotations to include only "Drugs" and "Symptoms" tags
        filtered_annotations = [tag for tag in annotations if "Diseases" in tag or "Procedures" in tag]
        selected_annotations.append(filtered_annotations)
        indices.append(i)

# Print the selected sentences and their corresponding filtered annotations
for sentence, annotations in zip(selected_sentences, selected_annotations):
    print("Sentence:", sentence)
    print("Annotations:", annotations)
    print("-" * 30)


Sentence: The clinical relevance of this interaction is poorly defined and for many infections the benefits of combination therapy are likely to outweigh the potential risks. 
Annotations: ['@@infections:Diseases##', '@@combination therapy:Procedures##']
------------------------------
Sentence:  Omeprazole; Amoxicillin; Rifabutin: (Minor) Consider additional monitoring or alternative antimicrobial therapy for patients with infections in which clinical response is highly dependent upon the rapid, bactericidal activity of penicillins. 
Annotations: ['@@monitoring:Procedures##', '@@antimicrobial therapy:Procedures##', '@@infections:Diseases##']
------------------------------
Sentence: The clinical relevance of this interaction is poorly defined and for many infections the benefits of combination therapy are likely to outweigh the potential risks. 
Annotations: ['@@infections:Diseases##', '@@combination therapy:Procedures##']
------------------------------
Sentence: Oxacillin: (Minor) Cons

------------------------------
Sentence: Affected cytochrome P450 isoenzymes and drug transporters: none •Route-Specific Pharmacokinetics Intravenous Route Sodium ferric gluconate complex: Multiple, sequential, single-dose, intravenous pharmacokinetic studies were performed on 14 healthy iron-deficient patients. 
Annotations: ['@@pharmacokinetic studies:Procedures##', '@@iron-deficient:Diseases##']
------------------------------
Sentence: For the treatment of iron-deficiency anemia For the treatment of iron-deficiency anemia in patients undergoing chronic hemodialysis who are receiving supplemental epoetin alfa therapy NOTE: In patients with iron-deficiency anemia receiving hemodialysis and supplemental epoetin alfa therapy, sufficient intravenous iron should be administered to maintain a serum ferritin of greater than 200 ng/mL and transferrin saturation (TSAT) greater than 20%. 
Annotations: ['@@treatment:Procedures##', '@@iron-deficiency anemia:Diseases##', '@@deficiency anemia:Dise

Annotations: ['@@preventative treatment:Procedures##', '@@treatment:Procedures##', '@@migraine:Diseases##']
------------------------------
Sentence: Centrally, CGRP is involved in nociceptive transmission through second and third-order neurons and pain modulation in the brainstem. 
Annotations: ['@@transmission:Diseases##', '@@pain modulation:Procedures##']
------------------------------
Sentence: Renal Impairment Renal impairment did not reveal a significant difference in the pharmacokinetics of ubrogepant in patients with mild or moderate renal impairment (CrCl 30 to 89 mL/minute) relative to those with normal renal function (CrCl more than 90 mL/minute). 
Annotations: ['@@Renal Impairment:Diseases##', '@@Renal impairment:Diseases##', '@@renal impairment:Diseases##', '@@CrCl:Procedures##', '@@CrCl:Procedures##']
------------------------------
Sentence: Patients with severe renal impairment or end-stage renal disease (eGFR less than 30 mL/minute) have not been studied.
Annotations: ['

Annotations: ['@@iron replacement:Procedures##', '@@replacement therapy:Procedures##', '@@therapy:Procedures##', '@@iron-deficiency anemia:Diseases##', '@@deficiency anemia:Diseases##', '@@anemia:Diseases##']
------------------------------
Sentence: The safety and efficacy of ferric maltol for the treatment of iron-deficiency anemia in patients with inflammatory bowel disease (IBD) and chronic kidney disease (CKD) was established in 3 clinical studies. 
Annotations: ['@@treatment:Procedures##', '@@iron-deficiency anemia:Diseases##', '@@deficiency anemia:Diseases##', '@@anemia:Diseases##', '@@inflammatory bowel disease:Diseases##', '@@bowel disease:Diseases##', '@@disease:Diseases##', '@@IBD:Diseases##', '@@chronic kidney disease:Diseases##', '@@kidney disease:Diseases##', '@@disease:Diseases##', '@@CKD:Diseases##']
------------------------------
Sentence: Iron deficiency not only causes anemia and decreased oxygen delivery, but it also reduces the metabolism of muscle and decreases mit

Annotations: ['@@Cerebrospinal fluid analysis:Procedures##', '@@meningitis:Diseases##', '@@meningitis:Diseases##', '@@blood cultures:Procedures##']
------------------------------
Sentence: Methods to definitively diagnose meningococcemia include cultures, antigen detection using latex agglutination, and polymerase chain reaction. 
Annotations: ['@@meningococcemia:Diseases##', '@@antigen detection:Procedures##', '@@detection:Procedures##', '@@latex agglutination:Procedures##', '@@polymerase chain reaction:Procedures##', '@@cultures:Procedures##']
------------------------------
Sentence: In toxic shock syndrome, blood cultures may be positive for  Streptococcus pyogenes or  Staphylococcus aureus ; cultures of other clinically relevant sites may isolate the organism as well. 
Annotations: ['@@toxic:Diseases##', '@@toxic shock syndrome:Diseases##', '@@shock:Diseases##', '@@shock syndrome:Diseases##', '@@syndrome:Diseases##', '@@isolate:Procedures##', '@@blood cultures:Procedures##']
------

...

Sentence: Progression of diabetic retinopathy may be slowed with aggressive blood pressure, lipid, and glycemic control. 
Annotations: ['@@diabetic:Diseases##', '@@diabetic retinopathy:Diseases##', '@@retinopathy:Diseases##', '@@aggressive:Diseases##', '@@glycemic control:Procedures##']
------------------------------
Sentence: Begin annual assessment for diabetic nephropathy at time of type 2 diabetes diagnosis; include assessment of urinary albumin-to-creatinine ratio and serum creatinine level for estimated GFR. 
Annotations: ['@@assessment:Procedures##', '@@diabetic:Diseases##', '@@diabetic nephropathy:Diseases##', '@@nephropathy:Diseases##', '@@diabetes:Diseases##', '@@assessment:Procedures##', '@@serum creatinine:Procedures##', '@@serum creatinine level:Procedures##', '@@estimated GFR:Procedures##', '@@GFR:Procedures##', '@@type 2 diabetes:Diseases##']
------------------------------
Sentence: Affects approximately 50% of patients with diabetes; cause of 50% to 75% of all nontrauma

Sentence: The type of anemia and the underlying cause or causes should be determined before starting therapy with iron. 
Annotations: ['@@anemia:Diseases##', '@@determined:Procedures##', '@@before starting therapy:Procedures##', '@@therapy:Procedures##']
------------------------------
Sentence: The type of anemia and the underlying cause or causes should be determined before starting therapy with iron. 
Annotations: ['@@anemia:Diseases##', '@@determined:Procedures##', '@@before starting therapy:Procedures##', '@@therapy:Procedures##']
------------------------------
Sentence: Iron supplementation should be used cautiously in patients receiving blood transfusions because iron overload may occur. 
Annotations: ['@@Iron supplementation:Procedures##', '@@transfusions:Procedures##', '@@iron overload:Diseases##']
------------------------------
Sentence: Those suffering from hereditary/genetic hemochromatosis or hemochromatosis due to secondary iron overload (e.g., as in iron-loading anemias s

------------------------------
Sentence: Initial step is determined by disease severity classification (for newly diagnosed patients not on controller medications) or by disease control classification (for patients currently using controller medications). 
Annotations: ['@@disease:Diseases##', '@@disease:Diseases##', '@@disease control:Procedures##']
------------------------------
Sentence: Once a mainstay of asthma therapy, short-acting β-agonists are no longer recommended because the preferred reliever for symptomatic patients should not be used as monotherapy because of safety concerns and poor outcomes. 
Annotations: ['@@asthma:Diseases##', '@@monotherapy:Procedures##']
------------------------------
Sentence: Referral to an asthma specialist is recommended. 
Annotations: ['@@Referral:Procedures##', '@@Referral to:Procedures##', '@@asthma:Diseases##']
------------------------------
Sentence: Referral to an asthma specialist is recommended. 
Annotations: ['@@Referral:Procedures##', 

------------------------------
Sentence: Self-rated questionnaire; measures intensity, severity, and depth of common depression symptoms. 
Annotations: ['@@measures:Procedures##', '@@depression:Diseases##']
------------------------------
Sentence: Minimize potentially adverse exposures to fetus (eg, polypharmacy, multiple medication trials, untreated maternal bipolar disorder). 
Annotations: ['@@polypharmacy:Procedures##', '@@bipolar:Diseases##', '@@bipolar disorder:Diseases##', '@@disorder:Diseases##']
------------------------------
Sentence: Refer all female patients with suspected bipolar disorder who are pregnant or planning pregnancy—including those presenting with major depression who report a past history of overactivity or disinhibited behavior—to a mental health professional (preferably a mental health specialist in prenatal medicine) for preconception counseling and therapeutic management. 
Annotations: ['@@bipolar:Diseases##', '@@bipolar disorder:Diseases##', '@@disorder:Dis

Annotations: ['@@opioid withdrawal:Diseases##', '@@Monitor:Procedures##']
------------------------------
Sentence: If mitapivat is discontinued, consider a dose reduction of hydrocodone and frequently monitor for signs of respiratory depression and sedation. 
Annotations: ['@@respiratory depression:Diseases##', '@@depression:Diseases##', '@@sedation:Procedures##', '@@monitor:Procedures##']
------------------------------
Sentence:  Carbinoxamine; Hydrocodone; Pseudoephedrine: (Moderate) Monitor for reduced efficacy of hydrocodone and signs of opioid withdrawal if coadministration with mitapivat is necessary; consider increasing the dose of hydrocodone as needed. 
Annotations: ['@@opioid withdrawal:Diseases##', '@@Monitor:Procedures##']
------------------------------
Sentence: If mitapivat is discontinued, consider a dose reduction of hydrocodone and frequently monitor for signs of respiratory depression and sedation. 
Annotations: ['@@respiratory depression:Diseases##', '@@depression:Di

In [166]:
print(len(selected_annotations))
print(len(selected_sentences))
print(sentences_sub[102])
entities_sub[102]

1424
1424
The oral absorption of these antibiotics will be significantly reduced by other orally administered compounds that contain aluminum salts, calcium salts, iron salts, magnesium salts, and/or zinc salts. 


['@@oral:Anatomy##',
 '@@oral absorption:Clinicalfinding##',
 '@@absorption:Event##',
 '@@antibiotics:Substance##',
 '@@significantly:Socialcontext##',
 '@@reduced:Qualifier##',
 '@@orally:Qualifier##',
 '@@administered:Qualifier##',
 '@@compounds:Qualifier##',
 '@@aluminum:Substance##',
 '@@aluminum salts:Substance##',
 '@@salts:Substance##',
 '@@calcium:Substance##',
 '@@calcium salts:Substance##',
 '@@salts:Substance##',
 '@@iron:Substance##',
 '@@iron salts:Drugs##',
 '@@salts:Substance##',
 '@@magnesium:Substance##',
 '@@salts:Substance##',
 '@@zinc:Drugs##',
 '@@salts:Substance##',
 '@@orally administered:Procedures##',
 '@@contain:Qualifier##',
 '@@magnesium salts:Drugs##']

In [167]:
#template 48

In [168]:
import pandas as pd
import json

input_txt = selected_sentences[0:10]           ####change####  
output = selected_annotations[0:10]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Give me all the Diseases and Procedures from the text given below",
        "input":f"{text}",
        "output":f"Here are all the diseases and procedures in the text: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 48.json", "w") as f:     ####change####
    f.write(output_json)

In [169]:
#template 49

In [170]:
import pandas as pd
import json

input_txt = selected_sentences[10:20]           ####change####  
output = selected_annotations[10:20]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Provide me with the list of all the diseases and procedures from the text",
        "input":f"{text}",
        "output":f"The list of all diseases and procedures in the text are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 49.json", "w") as f:     ####change####
    f.write(output_json)

In [171]:
#template 50

In [172]:
import pandas as pd
import json

input_txt = selected_sentences[20:30]           ####change####  
output = selected_annotations[20:30]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Analyze the text given and provide me all the diseases and procedures.",
        "input":f"{text}",
        "output":f"After analysing the text, the identified diseases and procedures are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 50.json", "w") as f:     ####change####
    f.write(output_json)

In [173]:
#template 51

In [174]:
import pandas as pd
import json

input_txt = selected_sentences[30:40]           ####change####  
output = selected_annotations[30:40]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Examine the text and give me with all the diseases and procedures from the text",
        "input":f"{text}",
        "output":f"After examining the text, the identified diseases and procedures are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 51.json", "w") as f:     ####change####
    f.write(output_json)

In [175]:
#template 52

In [176]:
import pandas as pd
import json

input_txt = selected_sentences[40:50]           ####change####  
output = selected_annotations[40:50]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Extract the diseases and procedures from the following text",
        "input":f"{text}",
        "output":f"Extracted diseases and procedures: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 52.json", "w") as f:     ####change####
    f.write(output_json)

In [177]:
# Remove elements from 'sentences' list
idx = indices[0:50]
for index in sorted(idx, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(idx, reverse=True):
    del entities_sub[index]
    
print(len(sentences_sub))
print(len(entities_sub))

10576
10576


In [178]:
#template 53-57 (disease+symptoms)

In [179]:
# Find sentences with both "Drugs" and "Symptoms" tags
selected_sentences = []
selected_annotations = []
indices = []

for i, sentence in enumerate(sentences_sub):
    annotations = entities_sub[i]
    
    # Check if "Drugs" and "Symptoms" tags are both present in annotations
    if any("Diseases" in tag for tag in annotations) and any("Symptoms" in tag for tag in annotations):
        selected_sentences.append(sentence)
        
        # Filter annotations to include only "Drugs" and "Symptoms" tags
        filtered_annotations = [tag for tag in annotations if "Diseases" in tag or "Symptoms" in tag]
        selected_annotations.append(filtered_annotations)
        indices.append(i)

# Print the selected sentences and their corresponding filtered annotations
for sentence, annotations in zip(selected_sentences, selected_annotations):
    print("Sentence:", sentence)
    print("Annotations:", annotations)
    print("-" * 30)


Sentence:  Methoxsalen: (Moderate) Use methoxsalen and tetracyclines together with caution; the risk of severe burns/photosensitivity may be additive. 
Annotations: ['@@burns:Diseases##', '@@photosensitivity:Symptoms##']
------------------------------
Sentence: In patients with hepatic impairment, a potential additive effect of reduced metabolism may further increase systemic rifaximin exposure. 
Annotations: ['@@hepatic impairment:Diseases##', '@@exposure:Symptoms##']
------------------------------
Sentence: The concomitant use of systemic tretinoin, ATRA and systemic tetracyclines should be avoided due to the potential for increased intracranial pressure and an increased risk of pseudotumor cerebri (benign intracranial hypertension). 
Annotations: ['@@increased intracranial pressure:Diseases##', '@@increased risk:Symptoms##', '@@pseudotumor:Diseases##', '@@pseudotumor cerebri:Diseases##', '@@benign intracranial hypertension:Diseases##', '@@intracranial hypertension:Diseases##', '@@hy

Annotations: ['@@arthralgia:Symptoms##', '@@arthritis:Diseases##', '@@back pain:Symptoms##', '@@pain:Symptoms##', '@@intervertebral disc degeneration:Diseases##', '@@degeneration:Diseases##', '@@osteoarthritis:Diseases##', '@@pain:Symptoms##', '@@neck pain:Symptoms##', '@@pain:Symptoms##', '@@extremity pain:Symptoms##', '@@pain:Symptoms##', '@@skin pain:Symptoms##', '@@pain:Symptoms##', '@@sciatica:Symptoms##', '@@pain:Symptoms##', '@@tendonitis:Diseases##', '@@tenosynovitis:Diseases##']
------------------------------
Sentence: Arthralgia (41% to 61%; grade 3 or 4, 9% or less), myalgia (6% to 24%; grade 3 or 4, 1.1% or less), muscle cramps/spasms (4.8% to 14%), bone pain (9% to 14%; grade 3 or 4, 0.4% to 3%), and musculoskeletal pain (6% to 11%; grade 3 or 4, 3% or less) were reported in patients with CP (n = 270), accelerated phase (n = 85), and blast phase (n = 62) CML and acute lymphoblastic leukemia (n = 32) who received ponatinib in another clinical trial. Fatigue or asthenia occu

Sentence: In the United States, CDC recommends a 2-dose series of recombinant zoster vaccine (Shingrix) for people aged 50 years and older, regardless of history of varicella or herpes zoster infection or immunization with live zoster vaccine. 
Annotations: ['@@zoster:Diseases##', '@@history of:Symptoms##', '@@varicella:Diseases##', '@@herpes:Diseases##', '@@herpes zoster:Diseases##', '@@herpes zoster infection:Diseases##', '@@infection:Diseases##', '@@zoster:Diseases##']
------------------------------
Sentence: Immunogenicity and protection against nonbacteremic pneumococcal pneumonia may be greater with the conjugate vaccine, but significant adverse events  are also more common. 
Annotations: ['@@protection:Symptoms##', '@@pneumococcal pneumonia:Diseases##', '@@pneumonia:Diseases##', '@@adverse events:Symptoms##']
------------------------------
Sentence: In the United States, the conjugate vaccine is no longer routinely recommended for healthy immunocompetent adults aged 65 years and

Sentence: Elevated pressure caused by trauma or rhabdomyolysis in an enclosed space bounded by fascia, especially in leg or forearm. 
Annotations: ['@@pressure:Symptoms##', '@@trauma:Diseases##', '@@rhabdomyolysis:Diseases##']
------------------------------
Sentence: As compartment pressure increases above mean arterial pressure, tissue ischemia and nerve injury develops. 
Annotations: ['@@mean arterial pressure:Symptoms##', '@@ischemia:Diseases##', '@@nerve injury:Diseases##', '@@injury:Diseases##']
------------------------------
Sentence: Long-term sequelae with permanent disability occurs in majority of survivors (rates as high as 76% have been reported). 
Annotations: ['@@permanent disability:Symptoms##', '@@disability:Symptoms##', '@@sequelae:Diseases##']
------------------------------
Sentence: Long-term sequelae often include subtle neuropsychiatric changes (eg, issues with short-term memory and concentration). 
Annotations: ['@@issues:Symptoms##', '@@sequelae:Diseases##']
-----

Sentence: Focal neurologic deficits, including cranial or peripheral motor nerve paralysis. 
Annotations: ['@@nerve paralysis:Diseases##', '@@paralysis:Symptoms##', '@@Focal neurologic deficits:Symptoms##']
------------------------------
Sentence: Related to acute respiratory distress or septic shock. 
Annotations: ['@@Related:Symptoms##', '@@acute respiratory distress:Diseases##', '@@respiratory distress:Symptoms##', '@@septic shock:Diseases##', '@@shock:Diseases##']
------------------------------
Sentence: Pathophysiologically, pathogen-mediated injury to the vascular endothelium results in increased capillary permeability, microhemorrhage, and platelet consumption. 
Annotations: ['@@injury:Diseases##', '@@increased capillary permeability:Symptoms##']
------------------------------
Sentence: In later stages of untreated disease, microvascular leakage can lead to manifestations such as noncardiogenic pulmonary edema and cerebral edema. 
Annotations: ['@@disease:Diseases##', '@@leakage

...

Annotations: ['@@hemorrhage:Symptoms##', '@@sepsis:Diseases##']
------------------------------
Sentence: Admission is required for patients with hemorrhage (eg, dissecting aortic aneurysm, ruptured ectopic pregnancy), sepsis, indication for urgent surgery (eg, perforated viscus, intestinal obstruction), likelihood of progression (eg, pancreatitis), high risk of adverse outcome for missed diagnosis (eg, frail, older, immunocompromised). 
Annotations: ['@@hemorrhage:Symptoms##', '@@dissecting aortic aneurysm:Diseases##', '@@aortic aneurysm:Diseases##', '@@aortic aneurysm, ruptured:Diseases##', '@@aneurysm:Diseases##', '@@ruptured ectopic pregnancy:Diseases##', '@@ectopic pregnancy:Diseases##', '@@sepsis:Diseases##', '@@perforated:Symptoms##', '@@perforated viscus:Diseases##', '@@intestinal obstruction:Diseases##', '@@obstruction:Diseases##', '@@pancreatitis:Diseases##', '@@high risk:Symptoms##', '@@high risk of:Symptoms##', '@@adverse outcome:Symptoms##', '@@diagnosis:Symptoms##', '@@fra

Annotations: ['@@atopic:Diseases##', '@@atopic asthma:Diseases##', '@@asthma:Diseases##', '@@obstruction:Diseases##', '@@exacerbation:Symptoms##']
------------------------------
Sentence: No history of atopic dermatitis, intermediate prevalence of hay fever, and lower IgE levels. 
Annotations: ['@@No history of:Symptoms##', '@@history of:Symptoms##', '@@history of atopic dermatitis:Symptoms##', '@@atopic:Diseases##', '@@atopic dermatitis:Diseases##', '@@dermatitis:Diseases##', '@@hay fever:Diseases##', '@@fever:Symptoms##']
------------------------------
Sentence: Highly atopic asthma with high levels of obstruction and high exacerbation rates. 
Annotations: ['@@atopic:Diseases##', '@@atopic asthma:Diseases##', '@@asthma:Diseases##', '@@obstruction:Diseases##', '@@exacerbation:Symptoms##']
------------------------------
Sentence: History of atopic dermatitis with highest prevalence of skin test reactivity, highest IgE levels, highest eosinophilia, and intermediate prevalence of allergi

Annotations: ['@@severe asthma:Symptoms##', '@@asthma:Diseases##', '@@asthma exacerbation:Symptoms##', '@@exacerbation:Symptoms##']
------------------------------
Sentence: Ipratropium Bromide Nebulizer solution; Adolescents: 500 mcg via nebulizer every 20 minutes for 3 doses, then as needed (for up to 3 hours) has been recommended for severe asthma exacerbation in the emergency care setting. 
Annotations: ['@@severe asthma:Symptoms##', '@@asthma:Diseases##', '@@asthma exacerbation:Symptoms##', '@@exacerbation:Symptoms##']
------------------------------
Sentence: Those with more severe asthma may achieve a better initial response with the 1.25 mg dose. 
Annotations: ['@@severe asthma:Symptoms##', '@@asthma:Diseases##']
------------------------------
Sentence: Those with more severe asthma, weight more than 40 kg, or patients 11 to 12 years of age may achieve a better initial response with the 1.25 mg dose. 
Annotations: ['@@severe asthma:Symptoms##', '@@asthma:Diseases##']
------------

Annotations: ['@@Placental abruption:Diseases##', '@@abruption:Diseases##', '@@abnormalities:Symptoms##']
------------------------------
Sentence: Transient syndrome reported in newborns exposed to antidepressants, antipsychotics, or lithium. 
Annotations: ['@@syndrome:Diseases##', '@@exposed to:Symptoms##']
------------------------------
Sentence: Associated with tremor, muscle twitching, hypotonicity, irritability, feeding difficulties, poor suck, and lethargy; severe cases may lead to dyspnea, respiratory distress, arrhythmias, cyanosis, and seizures. 
Annotations: ['@@tremor:Symptoms##', '@@muscle twitching:Symptoms##', '@@twitching:Symptoms##', '@@hypotonicity:Symptoms##', '@@irritability:Symptoms##', '@@difficulties:Symptoms##', '@@poor suck:Symptoms##', '@@lethargy:Symptoms##', '@@dyspnea:Symptoms##', '@@respiratory distress:Symptoms##', '@@cyanosis:Symptoms##', '@@seizures:Symptoms##', '@@arrhythmias:Diseases##']
------------------------------
Sentence: Most common defect is Eb

Sentence:  Hydrocodone; Pseudoephedrine: (Moderate) Monitor for reduced efficacy of hydrocodone and signs of opioid withdrawal if coadministration with mitapivat is necessary; consider increasing the dose of hydrocodone as needed. 
Annotations: ['@@signs:Symptoms##', '@@opioid withdrawal:Diseases##']
------------------------------
Sentence: If mitapivat is discontinued, consider a dose reduction of hydrocodone and frequently monitor for signs of respiratory depression and sedation. 
Annotations: ['@@discontinued:Symptoms##', '@@signs:Symptoms##', '@@respiratory depression:Diseases##', '@@depression:Diseases##']
------------------------------
Sentence:  Ibuprofen; Oxycodone: (Moderate) Monitor for reduced efficacy of oxycodone and signs of opioid withdrawal if coadministration with mitapivat is necessary; consider increasing the dose of oxycodone as needed. 
Annotations: ['@@signs:Symptoms##', '@@opioid withdrawal:Diseases##']
------------------------------
Sentence: If mitapivat is dis

In [180]:
print(len(selected_annotations))
print(len(selected_sentences))
#print(sentences_sub[102])
#entities_sub[102]

1702
1702


In [181]:
#template 53

In [182]:
import pandas as pd
import json

input_txt = selected_sentences[0:10]           ####change####  
output = selected_annotations[0:10]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Extract the diseases and symptoms from the following text",
        "input":f"{text}",
        "output":f"Here are the extracted diseases and symptoms: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 53.json", "w") as f:     ####change####
    f.write(output_json)

In [183]:
#template 54

In [184]:
import pandas as pd
import json

input_txt = selected_sentences[10:20]           ####change####  
output = selected_annotations[10:20]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":f"Analyze the provided text and identify all the diseases and symptoms mentioned. Record your findings below.",
        "input":f"{text}",
        "output":f"After analyzing the text, the diseases and symptoms are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 54.json", "w") as f:     ####change####
    f.write(output_json)

In [185]:
#template 55

In [186]:
import pandas as pd
import json

input_txt = selected_sentences[20:30]           ####change####  
output = selected_annotations[20:30]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Please document the identified diseases and symptoms from the given text.", 
        "input":f"{text}",
        "output":f"Here are the documented diseases and symptoms: {entities_str}."
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 55.json", "w") as f:     ####change####
    f.write(output_json)

In [187]:
#template 56

In [188]:
import pandas as pd
import json

input_txt = selected_sentences[30:40]           ####change####  
output = selected_annotations[30:40]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Give me all the diseases and symptoms from the text given below",
        "input":f"{text}",
        "output":f"Here are all the diseases and symptoms in the text: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 56.json", "w") as f:     ####change####
    f.write(output_json)

In [189]:
#template 57

In [190]:
import pandas as pd
import json

input_txt = selected_sentences[40:50]           ####change####  
output = selected_annotations[40:50]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"List all the diseases and symptoms in the given text",
        "input":f"{text}",
        "output":f"These are the list of diseases and symptoms: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 57.json", "w") as f:     ####change####
    f.write(output_json)

In [191]:
# Remove elements from 'sentences' list
idx = indices[0:50]
for index in sorted(idx, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(idx, reverse=True):
    del entities_sub[index]
    
print(len(sentences_sub))
print(len(entities_sub))

10526
10526


In [192]:
#template 58-62 (diseases + clinicalfinding)

In [193]:
# Find sentences with both "Drugs" and "Symptoms" tags
selected_sentences = []
selected_annotations = []
indices = []

for i, sentence in enumerate(sentences_sub):
    annotations = entities_sub[i]
    
    # Check if "Drugs" and "Symptoms" tags are both present in annotations
    if any("Diseases" in tag for tag in annotations) and any("Clinicalfinding" in tag for tag in annotations):
        selected_sentences.append(sentence)
        
        # Filter annotations to include only "Drugs" and "Symptoms" tags
        filtered_annotations = [tag for tag in annotations if "Diseases" in tag or "Clinicalfinding" in tag]
        selected_annotations.append(filtered_annotations)
        indices.append(i)

# Print the selected sentences and their corresponding filtered annotations
for sentence, annotations in zip(selected_sentences, selected_annotations):
    print("Sentence:", sentence)
    print("Annotations:", annotations)
    print("-" * 30)


Sentence:  Nanoparticle Albumin-Bound Sirolimus: (Major) Avoid coadministration of sirolimus with sarecycline as concurrent use may increase sirolimus exposure and risk of toxicity. 
Annotations: ['@@exposure:Clinicalfinding##', '@@toxicity:Diseases##']
------------------------------
Sentence: Often associated with development of secondary hyperparathyroidism, normochromic normocytic anemia, and mild metabolic acidosis. 
Annotations: ['@@development:Clinicalfinding##', '@@secondary hyperparathyroidism:Diseases##', '@@hyperparathyroidism:Diseases##', '@@normocytic anemia:Diseases##', '@@anemia:Diseases##', '@@metabolic:Clinicalfinding##', '@@metabolic acidosis:Diseases##', '@@acidosis:Diseases##', '@@normochromic normocytic anemia:Diseases##']
------------------------------
Sentence: Some medications (eg, propylthiouracil, allopurinol, hydralazine) have been implicated as triggers of autoimmune vasculitis and glomerulonephritis with a nephritic presentation. 
Annotations: ['@@triggers:C

Annotations: ['@@muscle strength:Clinicalfinding##', '@@strength:Clinicalfinding##', '@@skin disease:Diseases##', '@@disease:Diseases##', '@@enzyme levels:Clinicalfinding##']
------------------------------
Sentence: Evaluate for interstitial lung disease with pulmonary function tests and chest radiography or high-resolution CT at baseline and thereafter as necessary. 
Annotations: ['@@interstitial lung disease:Diseases##', '@@lung disease:Diseases##', '@@disease:Diseases##', '@@pulmonary function:Clinicalfinding##']
------------------------------
Sentence: Affects approximately 30% of patients with dermatomyositis and polymyositis. 
Annotations: ['@@Affects:Clinicalfinding##', '@@dermatomyositis:Diseases##', '@@polymyositis:Diseases##']
------------------------------
Sentence: Risk factors for interstitial lung disease, which may help guide screening processes, include older age at diagnosis, presence of anti–Jo-1 antibodies, elevated erythrocyte sedimentation rate, presence of anti-MD

Annotations: ['@@thought:Clinicalfinding##', '@@transmitted:Diseases##', '@@disease:Diseases##']
------------------------------
Sentence: In symptomatic patients, illness may evolve over the course of a week or longer, beginning with mild symptoms that progress in some cases to the point of respiratory distress and shock. 
Annotations: ['@@distress:Clinicalfinding##', '@@shock:Diseases##']
------------------------------
Sentence: When COVID-19 is acquired after vaccination, a shift in the most common symptoms has been reported: headache, rhinorrhea, sneezing, sore throat, and loss of smell are most prominent, whereas cough and fever are less common than in unvaccinated people. 
Annotations: ['@@COVID-19:Diseases##', '@@smell:Clinicalfinding##']
------------------------------
Sentence: Physical findings may include systemic, neurologic, dermatologic, gastrointestinal, or more, but clinicians should be particularly attuned to pulmonary and hemodynamic indicators of critical illness. 
Ann

Sentence: NIH guidelines recommend use of baricitinib (or tocilizumab) with dexamethasone, or with remdesivir and dexamethasone, in recently hospitalized patients on high-flow oxygen or noninvasive ventilation who have clinical or laboratory evidence of progressive disease (eg, increasing oxygen needs, increasing inflammatory markers). 
Annotations: ['@@ventilation:Clinicalfinding##', '@@disease:Diseases##']
------------------------------
Sentence: NIH guideline recommends use of tofacitinib when baricitinib and tocilizumab are unavailable for recently hospitalized patients on high-flow oxygen or noninvasive ventilation who have clinical or laboratory evidence of progressive disease (eg, increasing oxygen needs, increasing inflammatory markers), along with dexamethasone or dexamethasone plus remdesivir. 
Annotations: ['@@ventilation:Clinicalfinding##', '@@disease:Diseases##']
------------------------------
Sentence: Infectious Diseases Society of America guideline suggests use of tofac

Annotations: ['@@cardiac output:Clinicalfinding##', '@@atherosclerosis:Diseases##']
------------------------------
Sentence: Rupture of ectopic pregnancy. 
Annotations: ['@@Rupture:Diseases##', '@@ectopic pregnancy:Diseases##', '@@pregnancy:Clinicalfinding##']
------------------------------
Sentence: Ovarian torsion, sometimes associated with a cyst or other ovarian mass. 
Annotations: ['@@Ovarian torsion:Diseases##', '@@torsion:Clinicalfinding##', '@@cyst:Diseases##']
------------------------------
Sentence: Pelvic inflammatory disease due to sexually transmitted infection (eg, gonorrhea, chlamydia). 
Annotations: ['@@Pelvic inflammatory disease:Diseases##', '@@inflammatory disease:Diseases##', '@@disease:Diseases##', '@@sexually:Clinicalfinding##', '@@sexually transmitted infection:Diseases##', '@@transmitted:Diseases##', '@@infection:Diseases##', '@@gonorrhea:Diseases##']
------------------------------
Sentence: Centrally mediated abdominal pain syndrome (functional abdominal pain s

Sentence: Patient is not hypoxic; pulse oximetry measurement is higher than 92% to 94% just before discharge home. 
Annotations: ['@@hypoxic:Diseases##', '@@pulse:Clinicalfinding##']
------------------------------
Sentence: For patients with moderate or severe persistent asthma, peak flow monitoring is preferred. 
Annotations: ['@@severe persistent asthma:Diseases##', '@@persistent:Clinicalfinding##', '@@persistent asthma:Diseases##', '@@asthma:Diseases##']
------------------------------
Sentence: Assess asthma control, medication technique, asthma action plan, adherence, and patient concerns at every patient visit. 
Annotations: ['@@asthma:Diseases##', '@@asthma:Diseases##', '@@adherence:Clinicalfinding##']
------------------------------
Sentence: Use of inhaled short-acting β₂-agonist more than 2 days per week for symptom relief (not for prevention of exercise-induced bronchospasm) indicates inadequate control and need for treatment step-up. 
Annotations: ['@@exercise-induced broncho

Sentence: Monotherapy risks triggering manic symptoms, rapid cycling, and psychotic symptoms; therefore, use only in conjunction with mood stabilizers (eg, lithium, second-generation antipsychotic). 
Annotations: ['@@triggering:Clinicalfinding##', '@@manic:Diseases##', '@@mood:Clinicalfinding##']
------------------------------
Sentence: Maternal exposure to lithium during pregnancy carries a significant risk of adverse pregnancy outcomes and neonatal complications, many of which are evident at time of labor and delivery. 
Annotations: ['@@Maternal:Clinicalfinding##', '@@Maternal exposure:Diseases##', '@@pregnancy:Clinicalfinding##', '@@pregnancy:Clinicalfinding##', '@@complications:Diseases##', '@@labor:Clinicalfinding##', '@@labor and delivery:Clinicalfinding##']
------------------------------
Sentence: If lithium treatment is continued during pregnancy, use fetal echocardiography to test for potential cardiac malformations and maternal serum α-fetoprotein screen for neural tube defec

In [194]:
print(len(selected_annotations))
print(len(selected_sentences))
#print(sentences_sub[102])
#entities_sub[102]

1131
1131


In [195]:
#template 58

In [196]:
import pandas as pd
import json

input_txt = selected_sentences[0:10]           ####change####  
output = selected_annotations[0:10]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"List all the diseases and clinical findings in the given text",
        "input":f"{text}",
        "output":f"These are the diseases and clinical findings in the text given: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 58.json", "w") as f:     ####change####
    f.write(output_json)

In [197]:
#template 59

In [198]:
import pandas as pd
import json

input_txt = selected_sentences[10:20]           ####change####  
output = selected_annotations[10:20]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Give me all the diseases and clinical findings from the text given below",
        "input":f"{text}",
        "output":f"These are the diseases and clinical findings in the text given: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 59.json", "w") as f:     ####change####
    f.write(output_json)

In [199]:
#template 60

In [200]:
import pandas as pd
import json

input_txt = selected_sentences[20:30]           ####change####  
output = selected_annotations[20:30]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Please document the identified diseases and clinical findings from the following text.", 
"input":f"{text}",
"output": f"The documented diseases and clinical findings are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 60.json", "w") as f:     ####change####
    f.write(output_json)

In [201]:
#template 61

In [202]:
import pandas as pd
import json

input_txt = selected_sentences[30:40]           ####change####  
output = selected_annotations[30:40]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Analyze the provided text and identify all the diseases and clinical findings.",
"input":f"{text}",
"output":f"After analysing the text, the identified diseases and clinical findings are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 61.json", "w") as f:     ####change####
    f.write(output_json)

In [203]:
#template 62

In [204]:
import pandas as pd
import json

input_txt = selected_sentences[40:50]           ####change####  
output = selected_annotations[40:50]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Extract the diseases and clinical findings from the following text",
"input":f"{text}",
"output":f"Extracted diseases and clinical findings are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 62.json", "w") as f:     ####change####
    f.write(output_json)

In [205]:
# Remove elements from 'sentences' list
idx = indices[0:50]
for index in sorted(idx, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(idx, reverse=True):
    del entities_sub[index]
    
print(len(sentences_sub))
print(len(entities_sub))

10476
10476


In [206]:
#template 63-67 (Diseases + Drugs)

In [207]:
# Find sentences with both "Drugs" and "Symptoms" tags
selected_sentences = []
selected_annotations = []
indices = []

for i, sentence in enumerate(sentences_sub):
    annotations = entities_sub[i]
    
    # Check if "Drugs" and "Symptoms" tags are both present in annotations
    if any("Diseases" in tag for tag in annotations) and any("Drugs" in tag for tag in annotations):
        selected_sentences.append(sentence)
        
        # Filter annotations to include only "Drugs" and "Symptoms" tags
        filtered_annotations = [tag for tag in annotations if "Diseases" in tag or "Drugs" in tag]
        selected_annotations.append(filtered_annotations)
        indices.append(i)

# Print the selected sentences and their corresponding filtered annotations
for sentence, annotations in zip(selected_sentences, selected_annotations):
    print("Sentence:", sentence)
    print("Annotations:", annotations)
    print("-" * 30)


Sentence:  Mipomersen: (Moderate) Caution should be exercised when mipomersen is used with other medications known to have potential for hepatotoxicity, such as tetracyclines. 
Annotations: ['@@Mipomersen:Drugs##', '@@mipomersen:Drugs##', '@@hepatotoxicity:Diseases##', '@@tetracyclines:Drugs##']
------------------------------
Sentence:  Pyridoxine, Vitamin B6: (Moderate) Divalent or trivalent cations readily chelate with tetracycline antibiotics, forming insoluble compounds. 
Annotations: ['@@chelate:Diseases##', '@@tetracycline antibiotics:Drugs##']
------------------------------
Sentence: C. difficile-associated diarrhea (CDAD) or pseudomembranous colitis has been reported with sarecycline. 
Annotations: ['@@C. difficile-associated diarrhea:Diseases##', '@@diarrhea:Diseases##', '@@CDAD:Diseases##', '@@pseudomembranous colitis:Diseases##', '@@colitis:Diseases##', '@@sarecycline:Drugs##']
------------------------------
Sentence: Use an ACE inhibitor or an angiotensin receptor blocker f

Annotations: ['@@iron:Drugs##', '@@iron deficiency:Diseases##', '@@iron deficiency anemia:Diseases##', '@@deficiency anemia:Diseases##', '@@anemia:Diseases##', '@@preterm delivery:Diseases##', '@@sodium ferric gluconate:Drugs##', '@@sodium ferric gluconate complex:Drugs##', '@@ferric gluconate:Drugs##', '@@ferric gluconate complex:Drugs##', '@@ferric:Drugs##']
------------------------------
Sentence: However, adverse reactions have occurred in premature neonates and low birth weight infants who received intravenously administered benzyl alcohol-containing drugs. 
Annotations: ['@@premature neonates:Diseases##', '@@benzyl alcohol:Drugs##']
------------------------------
Sentence:  Aspirin, ASA; Citric Acid; Sodium Bicarbonate: (Moderate) Doses of antacids and iron should be taken as far apart as possible to minimize the potential for interaction. 
Annotations: ['@@Aspirin:Drugs##', '@@ASA:Diseases##', '@@Citric Acid:Drugs##', '@@Sodium Bicarbonate:Drugs##', '@@antacids:Drugs##', '@@iron

Annotations: ['@@naloxone:Drugs##', '@@opiates:Drugs##', '@@respiratory depression:Diseases##', '@@depression:Diseases##']
------------------------------
Sentence: Naloxone should not be used for drowsiness unless opiate-induced respiratory depression coexists. 
Annotations: ['@@Naloxone:Drugs##', '@@opiate:Drugs##', '@@respiratory depression:Diseases##', '@@depression:Diseases##']
------------------------------
Sentence: Finally, because endorphins and enkephalins (endogenous substances with opiate-like activity) are known to exist in higher concentrations in certain disease states, naloxone has been considered a therapeutic agent for conditions other than opiate overdose. 
Annotations: ['@@opiate:Drugs##', '@@disease:Diseases##', '@@naloxone:Drugs##', '@@opiate:Drugs##', '@@opiate overdose:Diseases##', '@@overdose:Diseases##']
------------------------------
Sentence: Various respiratory diseases have been associated with elevated circulating concentrations of endorphins, and naloxone

Sentence: However, iron deficiency may develop, especially in children and menstruating or pregnant women, or as a result of the low copper diet recommended for Wilson&apos;s disease. 
Annotations: ['@@iron:Drugs##', '@@iron deficiency:Diseases##', '@@Wilson:Diseases##', '@@disease:Diseases##']
------------------------------
Sentence: Abdominal pain was reported in 5% of those receiving ferric citrate for the treatment of iron-deficiency anemia. 
Annotations: ['@@iron:Drugs##', '@@iron-deficiency anemia:Diseases##', '@@deficiency anemia:Diseases##', '@@anemia:Diseases##']
------------------------------
Sentence: Ferric citrate is also associated with stool discoloration (19% to 22%) related to the iron content. Cough was reported in 6% of patients receiving ferric citrate for the management of hyperphosphatemia.
Annotations: ['@@iron:Drugs##', '@@hyperphosphatemia:Diseases##']
------------------------------
Sentence: Hyperkalemia was reported in 5% of patients receiving ferric citrate 

Sentence: If used with sulfonylurea or insulin, a lower sulfonylurea or insulin dose may be needed to decrease risk for hypoglycemia..
Annotations: ['@@sulfonylurea:Drugs##', '@@insulin:Drugs##', '@@sulfonylurea:Drugs##', '@@insulin:Drugs##', '@@hypoglycemia:Diseases##']
------------------------------
Sentence: When used with a sulfonylurea or insulin, a lower dose of the sulfonylurea or insulin may be necessary to minimize the risk of hypoglycemia..
Annotations: ['@@sulfonylurea:Drugs##', '@@insulin:Drugs##', '@@sulfonylurea:Drugs##', '@@insulin:Drugs##', '@@hypoglycemia:Diseases##']
------------------------------
Sentence: If used with sulfonylurea or insulin, a lower sulfonylurea or insulin dose may be needed to decrease hypoglycemia..
Annotations: ['@@sulfonylurea:Drugs##', '@@insulin:Drugs##', '@@sulfonylurea:Drugs##', '@@insulin:Drugs##', '@@hypoglycemia:Diseases##']
------------------------------
Sentence: If used with sulfonylurea or insulin, lower doses of these agents may be 

Sentence: Diabetes medication classes that promote modest weight loss are metformin, glucagon-like peptide 1 receptor agonists, sodium-glucose cotransporter 2 inhibitors, and amylin mimetics. 
Annotations: ['@@Diabetes:Diseases##', '@@metformin:Drugs##', '@@glucagon:Drugs##', '@@mimetics:Diseases##', '@@glucagon-like peptide 1 receptor agonists:Drugs##', '@@sodium-glucose cotransporter 2 inhibitors:Drugs##', '@@amylin mimetics:Drugs##']
------------------------------
Sentence: Bariatric surgery is a recommended option to treat type 2 diabetes in patients with:. 
Annotations: ['@@diabetes:Diseases##', '@@type 2 diabetes:Drugs##']
------------------------------
Sentence: Increases risk for heart disease owing to increased insulin resistance, hyperglycemia, hypertension, dyslipidemia, and inflammation. 
Annotations: ['@@heart disease:Diseases##', '@@disease:Diseases##', '@@insulin:Drugs##', '@@insulin resistance:Diseases##', '@@hyperglycemia:Diseases##', '@@hypertension:Diseases##', '@@dy

------------------------------
Sentence:   Digoxin: (Moderate) Increase monitoring of serum digoxin concentrations and watch for potential signs and symptoms of clinical toxicity when starting, adjusting, or discontinuing mitapivat. 
Annotations: ['@@toxicity:Diseases##', '@@mitapivat:Drugs##']
------------------------------
Sentence:  Diphenhydramine; Hydrocodone; Phenylephrine: (Moderate) Monitor for reduced efficacy of hydrocodone and signs of opioid withdrawal if coadministration with mitapivat is necessary; consider increasing the dose of hydrocodone as needed. 
Annotations: ['@@opioid withdrawal:Diseases##', '@@mitapivat:Drugs##']
------------------------------
Sentence: If mitapivat is discontinued, consider a dose reduction of hydrocodone and frequently monitor for signs of respiratory depression and sedation. 
Annotations: ['@@mitapivat:Drugs##', '@@respiratory depression:Diseases##', '@@depression:Diseases##']
------------------------------
Sentence: Dolutegravir: (Moderate) 

In [208]:
print(len(selected_annotations))
print(len(selected_sentences))
#print(sentences_sub[102])
#entities_sub[102]

1129
1129


In [209]:
#template 63

In [210]:
import pandas as pd
import json

input_txt = selected_sentences[0:10]           ####change####  
output = selected_annotations[0:10]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Extract the diseases and drugs from the following text",
"input":f"{text}",
"output":f"Extracted disases and drugs from the given text are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 63.json", "w") as f:     ####change####
    f.write(output_json)

In [211]:
#template 64

In [212]:
import pandas as pd
import json

input_txt = selected_sentences[10:20]           ####change####  
output = selected_annotations[10:20]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Analyze the provided text and identify all the diseases and durgs.",
"input":f"{text}",
"output":f"After analyzing the text, the identified diseases and drugs are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 64.json", "w") as f:     ####change####
    f.write(output_json)

In [213]:
#template 65

In [214]:
import pandas as pd
import json

input_txt = selected_sentences[20:30]           ####change####  
output = selected_annotations[20:30]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Please document the identified diseases and drugs from the following text.", 
"input":f"{text}",
"output": f"The documented diseases and drugs are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 65.json", "w") as f:     ####change####
    f.write(output_json)

In [215]:
#template 66

In [216]:
import pandas as pd
import json

input_txt = selected_sentences[30:40]           ####change####  
output = selected_annotations[30:40]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"List all the diseases and drugs in the sentence given below",
"input":f"{text}",
"output":f"List of diseases and drugs are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 66.json", "w") as f:     ####change####
    f.write(output_json)

In [217]:
#template 67

In [218]:
import pandas as pd
import json

input_txt = selected_sentences[40:50]           ####change####  
output = selected_annotations[40:50]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"In the given text, find and record all instances of diseases and drugs.",
"input":f"{text}",
"output": f"These are the recorded disases and drugs {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 67.json", "w") as f:     ####change####
    f.write(output_json)

In [219]:
# Remove elements from 'sentences' list
idx = indices[0:50]
for index in sorted(idx, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(idx, reverse=True):
    del entities_sub[index]
    
print(len(sentences_sub))
print(len(entities_sub))

10426
10426


In [220]:
#template 68-72 (clinical findings + symptoms)

In [221]:
# Find sentences with both "Drugs" and "Symptoms" tags
selected_sentences = []
selected_annotations = []
indices = []

for i, sentence in enumerate(sentences_sub):
    annotations = entities_sub[i]
    
    # Check if "Drugs" and "Symptoms" tags are both present in annotations
    if any("Clinicalfinding" in tag for tag in annotations) and any("Symptoms" in tag for tag in annotations):
        selected_sentences.append(sentence)
        
        # Filter annotations to include only "Drugs" and "Symptoms" tags
        filtered_annotations = [tag for tag in annotations if "Clinicalfinding" in tag or "Symptoms" in tag]
        selected_annotations.append(filtered_annotations)
        indices.append(i)

# Print the selected sentences and their corresponding filtered annotations
for sentence, annotations in zip(selected_sentences, selected_annotations):
    print("Sentence:", sentence)
    print("Annotations:", annotations)
    print("-" * 30)


Sentence: Rales, decreased breath sounds, and dullness to percussion of chest. 
Annotations: ['@@Rales:Symptoms##', '@@decreased breath sounds:Symptoms##', '@@breath sounds:Clinicalfinding##']
------------------------------
Sentence: Initial laboratory tests should include electrolytes, complement levels (CH50, C3, C4), CBC, and liver function tests. 
Annotations: ['@@CH50:Clinicalfinding##', '@@C3:Symptoms##', '@@C4:Symptoms##', '@@liver function:Clinicalfinding##']
------------------------------
Sentence: Findings are nonspecific; kidneys may be enlarged with increased echogenicity. 
Annotations: ['@@Findings:Symptoms##', '@@echogenicity:Clinicalfinding##']
------------------------------
Sentence: In many cases, an identifiable precipitating event (eg, interventional vascular procedure or imaging) or evidence of emboli elsewhere (eg, skin, digits) provides a clue to diagnosis. 
Annotations: ['@@emboli:Symptoms##', '@@diagnosis:Symptoms##', '@@precipitating:Clinicalfinding##']
-------

------------------------------
Sentence: In the event that an accidental needlestick occurs, medical attention should be sought. 
Annotations: ['@@medical:Symptoms##', '@@attention:Clinicalfinding##']
------------------------------
Sentence: Although there are risks to the fetus of an opioid-dependent mother with use of naloxone, an opioid overdose is a medical emergency and can be fatal for the pregnant woman and fetus if left untreated. 
Annotations: ['@@medical:Symptoms##', '@@pregnant:Clinicalfinding##']
------------------------------
Sentence: In 1 study evaluating the effects of naloxone on fetal behavior, 54 pregnant women near term received either 0.4 mg of naloxone or placebo. 
Annotations: ['@@behavior:Symptoms##', '@@pregnant:Clinicalfinding##', '@@near:Symptoms##']
------------------------------
Sentence: Significant increases were observed in the number, duration, and amplitude of fetal heart rate accelerations, number of fetal body movements, and percentage of time spent 

Sentence:  Ibritumomab Tiuxetan: (Moderate) It has been reported that high intakes of phosphates, such as are found in dietary supplements or food additives, can interfere with absorption of trace nutrients such as iron, copper, and zinc. 
Annotations: ['@@dietary:Symptoms##', '@@absorption:Clinicalfinding##']
------------------------------
Sentence: Due to the discrepant findings and study differences, additional data are needed to clarify the potential interaction between iron salts and MMF. 
Annotations: ['@@findings:Symptoms##', '@@interaction:Clinicalfinding##']
------------------------------
Sentence: However, iron deficiency may develop, especially in children and menstruating or pregnant women, or as a result of the low copper diet recommended for Wilson&apos;s disease. 
Annotations: ['@@deficiency:Symptoms##', '@@develop:Clinicalfinding##', '@@pregnant:Clinicalfinding##', '@@diet:Symptoms##', '@@menstruating:Clinicalfinding##']
------------------------------
Sentence:   Phosph

Sentence: Contraindication: physical or cognitive impairment precluding ability to effectively use the technology. 
Annotations: ['@@cognitive:Clinicalfinding##', '@@cognitive impairment:Symptoms##', '@@impairment:Symptoms##', '@@ability:Clinicalfinding##']
------------------------------
Sentence: Small crossover trial conducted in patients with type 2 diabetes showed significant reduction in hemoglobin A1C level for patients using a continuous glucose monitoring device versus self-monitoring of blood glucose level. 
Annotations: ['@@conducted:Symptoms##', '@@hemoglobin A1C level:Clinicalfinding##', '@@blood glucose level:Clinicalfinding##', '@@glucose level:Clinicalfinding##']
------------------------------
Sentence: Physical or cognitive impairment precluding the rigors of insulin pump therapy during initiation and maintenance. 
Annotations: ['@@cognitive:Clinicalfinding##', '@@cognitive impairment:Symptoms##', '@@impairment:Symptoms##', '@@rigors:Symptoms##', '@@initiation:Clinicalf

Sentence: Perforated viscus (stomach, small bowel, colon) due to obstruction and over-distention, ischemia, ulceration, ingested foreign body (eg, fish bone, toothpick). 
Annotations: ['@@Perforated:Symptoms##', '@@ingested:Clinicalfinding##']
------------------------------
Sentence: Chronic (intestinal angina) due to poor cardiac output or atherosclerosis. 
Annotations: ['@@intestinal angina:Symptoms##', '@@angina:Symptoms##', '@@cardiac output:Clinicalfinding##']
------------------------------
Sentence: Ovarian torsion, sometimes associated with a cyst or other ovarian mass. 
Annotations: ['@@torsion:Clinicalfinding##', '@@ovarian mass:Symptoms##', '@@mass:Symptoms##']
------------------------------
Sentence: Centrally mediated abdominal pain syndrome (functional abdominal pain syndrome) characterized by chronic, even constant pain; not well understood, may be due to altered pain modulation systems resulting in magnified perception of sensory stimuli. 
Annotations: ['@@abdominal pain

------------------------------
Sentence: High-dose inhaled corticosteroid plus inhaled long-acting β₂-agonist with as-needed inhaled short-acting β₂-agonist to alleviate symptoms. 
Annotations: ['@@symptoms:Symptoms##', '@@inhaled:Clinicalfinding##', '@@inhaled:Clinicalfinding##', '@@inhaled:Clinicalfinding##']
------------------------------
Sentence: High-dose inhaled corticosteroid plus inhaled long-acting β₂-agonist with as-needed inhaled short-acting β₂-agonist to alleviate symptoms. 
Annotations: ['@@symptoms:Symptoms##', '@@inhaled:Clinicalfinding##', '@@inhaled:Clinicalfinding##', '@@inhaled:Clinicalfinding##']
------------------------------
Sentence: Medium-/high-dose corticosteroid plus inhaled long-acting β₂-agonist plus tiotropium bromide, a long-acting muscarinic antagonist with as-required inhaled short-acting β₂-agonist to alleviate symptoms. 
Annotations: ['@@symptoms:Symptoms##', '@@inhaled:Clinicalfinding##', '@@inhaled:Clinicalfinding##']
-----------------------------

------------------------------
Sentence: Increased risk for alcohol, tobacco, and substance use and high-risk behaviors (eg, sexual indiscretion). 
Annotations: ['@@Increased risk:Symptoms##', '@@risk behaviors:Clinicalfinding##', '@@behaviors:Symptoms##', '@@sexual:Clinicalfinding##']
------------------------------
Sentence: Poor nutrition, weight gain, and decreased adherence to prenatal care. 
Annotations: ['@@nutrition:Clinicalfinding##', '@@weight gain:Symptoms##', '@@adherence:Clinicalfinding##']
------------------------------
Sentence: Impaired functional capacity with social and vocational difficulties (eg, loss of job, difficulties with health care navigation, lack of social support). 
Annotations: ['@@Impaired:Symptoms##', '@@functional capacity:Symptoms##', '@@capacity:Symptoms##', '@@difficulties:Symptoms##', '@@loss of job:Symptoms##', '@@difficulties:Symptoms##', '@@lack of social support:Symptoms##', '@@social support:Clinicalfinding##']
------------------------------
Se

Annotations: ['@@exposure:Clinicalfinding##', '@@adverse reactions:Symptoms##']
------------------------------
Sentence: Description: Polysaccharide-iron complex is an oral iron preparation used in the treatment and prevention of iron-deficiency anemia and for nutritional supplementation when iron intake in the diet is inadequate to meet body needs. 
Annotations: ['@@deficiency:Symptoms##', '@@nutritional:Clinicalfinding##', '@@iron intake:Symptoms##', '@@diet:Symptoms##']
------------------------------
Sentence: The anemia of iron deficiency may result in fatigue, exertional shortness of breath, tachycardia, pallor, headache, glossitis, koilonychia (spoon nails), and decreased cognitive functioning. 
Annotations: ['@@deficiency:Symptoms##', '@@fatigue:Symptoms##', '@@shortness of breath:Symptoms##', '@@pallor:Symptoms##', '@@headache:Symptoms##', '@@koilonychia:Symptoms##', '@@spoon nails:Symptoms##', '@@cognitive:Clinicalfinding##', '@@cognitive functioning:Clinicalfinding##', '@@exe

In [222]:
print(len(selected_annotations))
print(len(selected_sentences))
#print(sentences_sub[102])
#entities_sub[102]

1149
1149


In [223]:
#template 68

In [224]:
import pandas as pd
import json

input_txt = selected_sentences[0:10]           ####change####  
output = selected_annotations[0:10]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"In the given text, find and record all instances of clinical findings and symptoms.",
"input":f"{text}",
"output": f"Recorded instances of clinical findings and symptoms are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 68.json", "w") as f:     ####change####
    f.write(output_json)

In [225]:
#template 69

In [226]:
import pandas as pd
import json

input_txt = selected_sentences[10:20]           ####change####  
output = selected_annotations[10:20]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"List all the symptoms and clinical findings in the sentence given below",
"input":f"{text}",
"output":f"List of clinical findings and symptoms are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 69.json", "w") as f:     ####change####
    f.write(output_json)

In [227]:
#template 70

In [228]:
import pandas as pd
import json

input_txt = selected_sentences[20:30]           ####change####  
output = selected_annotations[20:30]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Please document the identified clinical findings and symptoms from the given text.", 
"input":f"{text}",
"output": f"Documented clinical findings and symptoms are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 70.json", "w") as f:     ####change####
    f.write(output_json)

In [229]:
#template 71

In [230]:
import pandas as pd
import json

input_txt = selected_sentences[30:40]           ####change####  
output = selected_annotations[30:40]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Analyze the provided text and identify all the clinical findings and symptoms.",
"input":f"{text}",
"output":f"After analyzing the text, the identified clinical findings and symptoms are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 71.json", "w") as f:     ####change####
    f.write(output_json)

In [231]:
#template 72

In [232]:
import pandas as pd
import json

input_txt = selected_sentences[40:50]           ####change####  
output = selected_annotations[40:50]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Extract the symptoms and clinical findings from the following text",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 72.json", "w") as f:     ####change####
    f.write(output_json)

In [233]:
# Remove elements from 'sentences' list
idx = indices[0:50]
for index in sorted(idx, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(idx, reverse=True):
    del entities_sub[index]
    
print(len(sentences_sub))
print(len(entities_sub))

10376
10376


In [234]:
#template 73-77 (Organism + specialty)

In [235]:
# Find sentences with both "Drugs" and "Symptoms" tags
selected_sentences = []
selected_annotations = []
indices = []

for i, sentence in enumerate(sentences_sub):
    annotations = entities_sub[i]
    
    # Check if "Drugs" and "Symptoms" tags are both present in annotations
    if any("Organism" in tag for tag in annotations) and any("Specialty" in tag for tag in annotations):
        selected_sentences.append(sentence)
        
        # Filter annotations to include only "Drugs" and "Symptoms" tags
        filtered_annotations = [tag for tag in annotations if "Organism" in tag or "Specialty" in tag]
        selected_annotations.append(filtered_annotations)
        indices.append(i)

# Print the selected sentences and their corresponding filtered annotations
for sentence, annotations in zip(selected_sentences, selected_annotations):
    print("Sentence:", sentence)
    print("Annotations:", annotations)
    print("-" * 30)


Sentence: Counsel patients receiving immunosuppressant medications about the possibility of a diminished vaccine response and to continue to follow precautions to avoid exposure to SARS-CoV-2 virus after receiving the vaccine. 
Annotations: ['@@Counsel:Specialty##', '@@SARS-CoV:Organism##', '@@SARS-CoV-2:Organism##', '@@CoV:Organism##', '@@virus:Organism##']
------------------------------
Sentence: In vitro experiments with both diluted and undiluted sodium ferric gluconate complex demonstrate that less than 1% of the iron species within the compound is dialyzable. Pediatrics Sodium ferric gluconate complex: Single intravenous dose pharmacokinetics have been performed in 48 iron-deficient children aged 6 to 15 years. 
Annotations: ['@@species:Organism##', '@@Pediatrics:Specialty##']
------------------------------
Sentence: Residents and staff of facilities for developmentally disabled people. 
Annotations: ['@@staff:Specialty##', '@@Residents:Organism##']
------------------------------

In [236]:
print(len(selected_annotations))
print(len(selected_sentences))
#print(sentences_sub[102])
#entities_sub[102]

19
19


In [237]:
#template 73

In [238]:
import pandas as pd
import json

input_txt = selected_sentences[0:10]           ####change####  
output = selected_annotations[0:10]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
        "task":"Named Entity Recognition",
        "instruction":"Extract the organisms and specialty from the following text",
        "input":f"{text}",
        "output":f"Extracted organisms and specialities are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 73.json", "w") as f:     ####change####
    f.write(output_json)

In [239]:
#template 74

In [240]:
import pandas as pd
import json

input_txt = selected_sentences[10:20]           ####change####  
output = selected_annotations[10:20]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Analyze the provided text and identify all the organism and specialty.",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 74.json", "w") as f:     ####change####
    f.write(output_json)

In [241]:
# Remove elements from 'sentences' list
idx = indices[0:20]
for index in sorted(idx, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(idx, reverse=True):
    del entities_sub[index]
    
print(len(sentences_sub))
print(len(entities_sub))

10357
10357


In [242]:
#template 75-79 (specialty + procedures)

In [243]:
# Find sentences with both "Drugs" and "Symptoms" tags
selected_sentences = []
selected_annotations = []
indices = []

for i, sentence in enumerate(sentences_sub):
    annotations = entities_sub[i]
    
    # Check if "Drugs" and "Symptoms" tags are both present in annotations
    if any("Procedures" in tag for tag in annotations) and any("Specialty" in tag for tag in annotations):
        selected_sentences.append(sentence)
        
        # Filter annotations to include only "Drugs" and "Symptoms" tags
        filtered_annotations = [tag for tag in annotations if "Procedures" in tag or "Specialty" in tag]
        selected_annotations.append(filtered_annotations)
        indices.append(i)

# Print the selected sentences and their corresponding filtered annotations
for sentence, annotations in zip(selected_sentences, selected_annotations):
    print("Sentence:", sentence)
    print("Annotations:", annotations)
    print("-" * 30)


Sentence: Consult a nephrologist to aid in diagnosis and management; rapidly progressive glomerulonephritis requires urgent management. 
Annotations: ['@@nephrologist:Specialty##', '@@management:Procedures##', '@@management:Procedures##', '@@Consult a nephrologist:Procedures##']
------------------------------
Sentence: Consult appropriate specialist for treatment of condition (eg, rheumatologist, infectious disease specialist, hepatologist) for patients in whom an underlying or precipitating disorder is identified. 
Annotations: ['@@specialist:Specialty##', '@@treatment:Procedures##', '@@rheumatologist:Specialty##', '@@infectious disease specialist:Specialty##', '@@specialist:Specialty##', '@@hepatologist:Specialty##']
------------------------------
Sentence: Prompt diagnosis and treatment are essential, as patients who have extensive crescentic pathology are less likely to respond. 
Annotations: ['@@treatment:Procedures##', '@@pathology:Specialty##']
------------------------------
Sen

Sentence: Recommendations for specialist referral. 
Annotations: ['@@specialist:Specialty##', '@@referral:Procedures##']
------------------------------
Sentence: Registered dietitian for medical nutrition therapy. 
Annotations: ['@@dietitian:Specialty##', '@@medical nutrition therapy:Procedures##', '@@nutrition therapy:Procedures##', '@@therapy:Procedures##', '@@Registered dietitian:Specialty##']
------------------------------
Sentence: Ophthalmologist for dilated eye examination. 
Annotations: ['@@Ophthalmologist:Specialty##', '@@eye examination:Procedures##', '@@examination:Procedures##']
------------------------------
Sentence: Endocrinologist for uncertain diagnosis, teaching and supervising insulin therapy, treatment of labile glycemia (eg, recurrent hypoglycemia, persistent hyperglycemia, ketoacidosis), or when the complexity of care exceeds the capacity of the primary care setting. 
Annotations: ['@@Endocrinologist:Specialty##', '@@insulin therapy:Procedures##', '@@therapy:Proce

Sentence: Porphyria cutanea tarda (PCT) is sometimes associated with parenchymal iron deposits; patients with PCT should avoid iron supplements unless prescribed by a physician. 
Annotations: ['@@avoid iron:Procedures##', '@@supplements:Procedures##', '@@prescribed:Procedures##', '@@physician:Specialty##']
------------------------------


In [244]:
print(len(selected_annotations))
print(len(selected_sentences))
#print(sentences_sub[102])
#entities_sub[102]

218
218


In [245]:
#template 75

In [246]:
import pandas as pd
import json

input_txt = selected_sentences[0:10]           ####change####  
output = selected_annotations[0:10]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Extract the specialties and procedures from the following text",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 75.json", "w") as f:     ####change####
    f.write(output_json)

In [247]:
#template 76

In [248]:
import pandas as pd
import json

input_txt = selected_sentences[10:20]           ####change####  
output = selected_annotations[10:20]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Analyze the provided text and identify all the procedures and specialty.",
"input":f"{text}",
"output":f"After analysing the text, the identitfied procedures and specialties are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 76.json", "w") as f:     ####change####
    f.write(output_json)

In [249]:
#template 77

In [250]:
import pandas as pd
import json

input_txt = selected_sentences[20:30]           ####change####  
output = selected_annotations[20:30]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Please document the identified procedures and specialties from the given text.", 
"input":f"{text}",
"output": f"Documented procedures and specialties are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 77.json", "w") as f:     ####change####
    f.write(output_json)

In [251]:
#template 78

In [252]:
import pandas as pd
import json

input_txt = selected_sentences[30:40]           ####change####  
output = selected_annotations[30:40]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Your task is to read the following text and note down all the words that are of the category 'specialty' and 'procedures'", 
"input":f"{text}",
"output": entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 78.json", "w") as f:     ####change####
    f.write(output_json)

In [253]:
#template 79

In [254]:
import pandas as pd
import json

input_txt = selected_sentences[40:50]           ####change####  
output = selected_annotations[40:50]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"As a medical professional look at the following text and identify all the specialties and procedures", 
"input":f"{text}",
"output": entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 79.json", "w") as f:     ####change####
    f.write(output_json)

In [255]:
# Remove elements from 'sentences' list
idx = indices[0:50]
for index in sorted(idx, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(idx, reverse=True):
    del entities_sub[index]
    
print(len(sentences_sub))
print(len(entities_sub))

10307
10307


In [256]:
#template 80-84 (anatomy + clinicalfinding)

In [257]:
# Find sentences with both "Drugs" and "Symptoms" tags
selected_sentences = []
selected_annotations = []
indices = []

for i, sentence in enumerate(sentences_sub):
    annotations = entities_sub[i]
    
    # Check if "Drugs" and "Symptoms" tags are both present in annotations
    if any("Anatomy" in tag for tag in annotations) and any("Clinicalfinding" in tag for tag in annotations):
        selected_sentences.append(sentence)
        
        # Filter annotations to include only "Drugs" and "Symptoms" tags
        filtered_annotations = [tag for tag in annotations if "Anatomy" in tag or "Clinicalfinding" in tag]
        selected_annotations.append(filtered_annotations)
        indices.append(i)

# Print the selected sentences and their corresponding filtered annotations
for sentence, annotations in zip(selected_sentences, selected_annotations):
    print("Sentence:", sentence)
    print("Annotations:", annotations)
    print("-" * 30)


Sentence: Omeprazole; Sodium Bicarbonate: (Major) Early reports noted an increase in the excretion of tetracyclines during coadministration with sodium bicarbonate, and that the oral absorption of tetracyclines is reduced by sodium bicarbonate via increased gastric pH. However, conflicting data have been reported, and further study is needed. 
Annotations: ['@@excretion:Clinicalfinding##', '@@oral absorption:Clinicalfinding##', '@@gastric:Anatomy##', '@@pH:Clinicalfinding##', '@@conflicting:Clinicalfinding##']
------------------------------
Sentence: The oral absorption of these antibiotics will be significantly reduced by other orally administered compounds that contain calcium salts, particularly if the time of administration is within 60 minutes of each other. 
Annotations: ['@@oral:Anatomy##', '@@oral absorption:Clinicalfinding##']
------------------------------
Sentence:  Sodium Bicarbonate: (Major) Early reports noted an increase in the excretion of tetracyclines during coadminis

Sentence: Temporary cardiopulmonary standstill secondary to interruption of cardiac automaticity with spontaneous recovery of pulses. 
Annotations: ['@@cardiopulmonary:Anatomy##', '@@cardiac:Anatomy##', '@@spontaneous recovery:Clinicalfinding##', '@@recovery:Clinicalfinding##', '@@pulses:Clinicalfinding##']
------------------------------
Sentence: Diminished or absent pulses, usually of the lower extremities. 
Annotations: ['@@pulses:Clinicalfinding##', '@@lower extremities:Anatomy##', '@@extremities:Anatomy##']
------------------------------
Sentence: Various cardiac rhythms can occur (eg, asystole, pulseless electrical activity, ventricular tachycardia, ventricular fibrillation, idioventricular rhythm, atrial fibrillation). 
Annotations: ['@@cardiac:Anatomy##', '@@rhythms:Clinicalfinding##', '@@ventricular:Anatomy##', '@@ventricular:Anatomy##', '@@rhythm:Clinicalfinding##', '@@atrial:Anatomy##', '@@cardiac rhythms:Clinicalfinding##', '@@electrical activity:Clinicalfinding##']
-------

Sentence: Precise mechanisms are unknown, but disorders are thought to be mediated by cytotoxic T cells (polymyositis) and complement-mediated microangiopathy (dermatomyositis). 
Annotations: ['@@thought:Clinicalfinding##', '@@cells:Anatomy##', '@@cytotoxic T cells:Anatomy##']
------------------------------
Sentence: Muscle enzyme levels (primarily creatine kinase level) are indicated for all patients presenting with signs and symptoms of inflammatory myopathy. 
Annotations: ['@@Muscle:Anatomy##', '@@enzyme levels:Clinicalfinding##']
------------------------------
Sentence: MRI may be used to help confirm diagnosis and identify a muscle site for biopsy. 
Annotations: ['@@muscle:Anatomy##', '@@site for biopsy:Clinicalfinding##']
------------------------------
Sentence: CBC, erythrocyte sedimentation rate, and C-reactive protein and electrolyte levels are routinely obtained but are not required to establish diagnosis. 
Annotations: ['@@erythrocyte:Anatomy##', '@@electrolyte levels:Clinic

Sentence: American Association of Clinical Endocrinologists recommends an individualized target but states that blood pressure should be approximately 130/80 mm
Annotations: ['@@blood:Anatomy##', '@@blood pressure:Clinicalfinding##']
------------------------------
Sentence: Uncertainty exists regarding optimal blood pressure targets for patients with hypertension and type 2 diabetes. 
Annotations: ['@@blood:Anatomy##', '@@blood pressure:Clinicalfinding##']
------------------------------
Sentence: Some evidence suggests that tight blood pressure control may be favorable for reducing cardiovascular events and stroke. 
Annotations: ['@@blood:Anatomy##', '@@blood pressure:Clinicalfinding##', '@@cardiovascular:Anatomy##']
------------------------------
Sentence: Other evidence suggests that the benefits of blood pressure reduction in decreasing cardiovascular events plateau after attainment of a lower systolic blood pressure of 140 mm
Annotations: ['@@blood:Anatomy##', '@@blood pressure:Cli

Sentence: Multidrug therapy (ie, thiazide diuretic and ACE inhibitor/angiotensin receptor blocker at maximal doses) is often required to achieve blood pressure targets. 
Annotations: ['@@blood:Anatomy##', '@@blood pressure:Clinicalfinding##']
------------------------------
Sentence: If blood pressure is 160/100 mm Hg or more, start pharmacotherapy with 2 agents. 
Annotations: ['@@blood:Anatomy##', '@@blood pressure:Clinicalfinding##']
------------------------------
Sentence: Statin therapy is first line drug therapy for dyslipidemia; type of therapy is adjusted based on assessment of cardiovascular risk and age. 
Annotations: ['@@cardiovascular:Anatomy##', '@@age:Clinicalfinding##']
------------------------------
Sentence: Moderate-intensity statin therapy is indicated for adults aged 40 to 75 years with diabetes mellitus, regardless of estimated 10-year risk of atherosclerotic cardiovascular disease. 
Annotations: ['@@aged:Clinicalfinding##', '@@cardiovascular:Anatomy##']
------------

Annotations: ['@@Gender:Clinicalfinding##', '@@body:Anatomy##']
------------------------------
Sentence: An adequate intake is 0.27 mg per day PO and is based on the average iron intake of breast-fed infants. 
Annotations: ['@@breast:Anatomy##', '@@breast-fed infants:Clinicalfinding##']
------------------------------
Sentence: Serum iron, hemoglobin and hematocrit should be evaluated prior to iron therapy and at regular intervals during therapy. 
Annotations: ['@@Serum:Anatomy##', '@@hematocrit:Clinicalfinding##']
------------------------------
Sentence: If such a response is not seen, assessment for nonadherence (due to side effects or other reasons), malabsorption, or ongoing blood loss exceeding iron intake is needed. Maximum Dosage Limits: Dosage with iron must be individualized according to the patients age, dietary intake requirements, and the degree of the iron-deficiency anemia. 
Annotations: ['@@blood:Anatomy##', '@@according:Clinicalfinding##', '@@age:Clinicalfinding##', '@@d

Annotations: ['@@skin:Anatomy##', '@@breakdown:Clinicalfinding##']
------------------------------
Sentence: Wheezing apart from upper respiratory infection at young age. 
Annotations: ['@@upper respiratory:Anatomy##', '@@age:Clinicalfinding##']
------------------------------
Sentence: Abnormal pulmonary function in early childhood. 
Annotations: ['@@pulmonary:Anatomy##', '@@pulmonary function:Clinicalfinding##']
------------------------------
Sentence: History and physical examination consistent with asthma (ie, episodic airflow obstruction and airway hyperresponsiveness) and documentation of reversible airway obstruction support the diagnosis. 
Annotations: ['@@airflow:Clinicalfinding##', '@@airway:Anatomy##', '@@airway:Anatomy##']
------------------------------
Sentence: Diagnosis is challenging in this age group because objective measurements of lung function are difficult to obtain. 
Annotations: ['@@age:Clinicalfinding##', '@@lung:Anatomy##', '@@lung function:Clinicalfinding##']
-

In [258]:
print(len(selected_annotations))
print(len(selected_sentences))
#print(sentences_sub[102])
#entities_sub[102]

1042
1042


In [259]:
#template 80

In [260]:
import pandas as pd
import json

input_txt = selected_sentences[0:10]           ####change####  
output = selected_annotations[0:10]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"As a medical professional look at the following text and identify all the clinical findings and anatomy related terms", 
"input":f"{text}",
"output": f"Identified clinical findings and anatomies are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 80.json", "w") as f:     ####change####
    f.write(output_json)

In [261]:
#template 81

In [262]:
import pandas as pd
import json

input_txt = selected_sentences[10:20]           ####change####  
output = selected_annotations[10:20]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Your task is to read the following text and note down all the words that are of the category 'clinical findings' and 'anatomy'", 
"input":f"{text}",
"output": entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 81.json", "w") as f:     ####change####
    f.write(output_json)

In [263]:
#template 82

In [264]:
import pandas as pd
import json

input_txt = selected_sentences[20:30]           ####change####  
output = selected_annotations[20:30]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Please document the identified anatomies and clinical findings from the given text.", 
"input":f"{text}",
"output": f"Here are the documented anatomies and clinical findings {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 82.json", "w") as f:     ####change####
    f.write(output_json)

In [265]:
#template 83

In [266]:
import pandas as pd
import json

input_txt = selected_sentences[30:40]           ####change####  
output = selected_annotations[30:40]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Analyze the provided text and identify all the anatomies and clinical findings.",
"input":f"{text}",
"output":f"After analysing the text, the identified anatomies and clinical findings are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 83.json", "w") as f:     ####change####
    f.write(output_json)

In [267]:
#template 84

In [268]:
import pandas as pd
import json

input_txt = selected_sentences[40:50]           ####change####  
output = selected_annotations[40:50]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Extract the clinical findings and anatomies from the following text",
"input":f"{text}",
"output":f"Extracted clinical findings and anatomies in the text are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 84.json", "w") as f:     ####change####
    f.write(output_json)

In [269]:
# Remove elements from 'sentences' list
idx = indices[0:50]
for index in sorted(idx, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(idx, reverse=True):
    del entities_sub[index]
    
print(len(sentences_sub))
print(len(entities_sub))

10257
10257


In [270]:
#template 85-89 (Anatomy + disease)

In [271]:
# Find sentences with both "Drugs" and "Symptoms" tags
selected_sentences = []
selected_annotations = []
indices = []

for i, sentence in enumerate(sentences_sub):
    annotations = entities_sub[i]
    
    # Check if "Drugs" and "Symptoms" tags are both present in annotations
    if any("Anatomy" in tag for tag in annotations) and any("Diseases" in tag for tag in annotations):
        selected_sentences.append(sentence)
        
        # Filter annotations to include only "Drugs" and "Symptoms" tags
        filtered_annotations = [tag for tag in annotations if "Anatomy" in tag or "Diseases" in tag]
        selected_annotations.append(filtered_annotations)
        indices.append(i)

# Print the selected sentences and their corresponding filtered annotations
for sentence, annotations in zip(selected_sentences, selected_annotations):
    print("Sentence:", sentence)
    print("Annotations:", annotations)
    print("-" * 30)


Sentence: Enamel hypoplasia can result. 
Annotations: ['@@Enamel:Anatomy##', '@@Enamel hypoplasia:Diseases##', '@@hypoplasia:Diseases##']
------------------------------
Sentence: Complications include rapidly progressive glomerulonephritis, acute and chronic renal failure, pulmonary edema, and hypertensive encephalopathy. 
Annotations: ['@@rapidly progressive glomerulonephritis:Diseases##', '@@glomerulonephritis:Diseases##', '@@chronic renal failure:Diseases##', '@@renal:Anatomy##', '@@renal failure:Diseases##', '@@pulmonary:Anatomy##', '@@pulmonary edema:Diseases##', '@@edema:Diseases##', '@@hypertensive:Diseases##', '@@hypertensive encephalopathy:Diseases##', '@@encephalopathy:Diseases##', '@@Complications:Diseases##']
------------------------------
Sentence: Occurs as a result of glomerular injury secondary to an inflammatory response within glomeruli. 
Annotations: ['@@glomerular:Anatomy##', '@@injury:Diseases##', '@@inflammatory response:Diseases##', '@@glomeruli:Anatomy##']
-----

------------------------------
Sentence: People with chronic liver disease and people who have received liver transplants (increased risk of fulminant hepatitis A if infected). 
Annotations: ['@@chronic liver disease:Diseases##', '@@liver:Anatomy##', '@@liver disease:Diseases##', '@@disease:Diseases##', '@@liver:Anatomy##', '@@fulminant hepatitis:Diseases##', '@@hepatitis:Diseases##', '@@hepatitis A:Diseases##']
------------------------------
Sentence: People with end-stage renal disease. 
Annotations: ['@@renal:Anatomy##', '@@renal disease:Diseases##', '@@disease:Diseases##']
------------------------------
Sentence: People with hepatitis C infection or chronic liver disease. 
Annotations: ['@@hepatitis:Diseases##', '@@hepatitis C:Diseases##', '@@infection:Diseases##', '@@chronic liver disease:Diseases##', '@@liver:Anatomy##', '@@liver disease:Diseases##', '@@disease:Diseases##']
------------------------------
Sentence: Administering live virus vaccine to household contacts (eg, childr

------------------------------
Sentence: Begins as macular or maculopapular eruption of small (1-5 mm), flat, pink, and nonpruritic areas on wrists, forearms, and ankles. 
Annotations: ['@@eruption:Diseases##', '@@wrists:Anatomy##', '@@forearms:Anatomy##', '@@ankles:Anatomy##']
------------------------------
Sentence: Present in most patients (90%) during disease course; however, rash can present late or appear atypical, localized, faint, evanescent, and difficult to recognize in those with darker skin. 
Annotations: ['@@disease:Diseases##', '@@disease course:Diseases##', '@@skin:Anatomy##']
------------------------------
Sentence: Periorbital and peripheral edema. 
Annotations: ['@@Periorbital:Anatomy##', '@@peripheral edema:Diseases##', '@@edema:Diseases##', '@@Periorbital and peripheral edema:Diseases##']
------------------------------
Sentence: Altered mental status due to intracerebral hemorrhage, cerebral edema, or vascular occlusion. 
Annotations: ['@@Altered mental status:Disea

------------------------------
Sentence: Patients with Renal Impairment Dosing Specific guidelines for dosage adjustments in renal impairment are not available; it appears that no dosage adjustments are needed..
Annotations: ['@@Renal:Anatomy##', '@@Renal Impairment:Diseases##', '@@renal:Anatomy##', '@@renal impairment:Diseases##']
------------------------------
Sentence: Skeletal and encephalic malformation was observed in neonatal mice when ferric gluconate was given intraperitoneally to gravid dams on gestation days 7 to 9. 
Annotations: ['@@Skeletal:Anatomy##', '@@encephalic:Anatomy##', '@@malformation:Diseases##']
------------------------------
Sentence: However, oral administration of other ferric or ferrous compounds to gravid mice or rats caused no fetal malformation. 
Annotations: ['@@fetal:Anatomy##', '@@fetal malformation:Diseases##', '@@malformation:Diseases##']
------------------------------
Sentence: An overdose of iron in pregnant women may carry a risk for spontaneous a

Annotations: ['@@diabetes:Diseases##', '@@diabetes mellitus:Diseases##', '@@cardiovascular:Anatomy##', '@@cardiovascular disease:Diseases##', '@@disease:Diseases##', '@@macrovascular complications:Diseases##', '@@complications:Diseases##']
------------------------------
Sentence: No significant cardiovascular disease. 
Annotations: ['@@cardiovascular:Anatomy##', '@@cardiovascular disease:Diseases##', '@@disease:Diseases##']
------------------------------
Sentence: Extensive comorbid conditions (including renal and liver failure). 
Annotations: ['@@renal:Anatomy##', '@@liver:Anatomy##', '@@liver failure:Diseases##', '@@renal and liver failure:Diseases##']
------------------------------
Sentence: Fasting plasma glucose target of 80 to 130 mg/dL (American Diabetes Association) or less than 110 mg/dL (American Association of Clinical Endocrinologists). 
Annotations: ['@@plasma:Anatomy##', '@@Diabetes:Diseases##']
------------------------------
Sentence: Glucose target between 110 and 140 m

Annotations: ['@@hypertension:Diseases##', '@@cardiovascular:Anatomy##', '@@cardiovascular disease:Diseases##', '@@disease:Diseases##']
------------------------------
Sentence: Routine screening for coronary artery disease is not recommended in asymptomatic patients. 
Annotations: ['@@coronary:Anatomy##', '@@coronary artery:Anatomy##', '@@coronary artery disease:Diseases##', '@@artery:Anatomy##', '@@disease:Diseases##']
------------------------------
Sentence: Sodium-glucose cotransporter 2 inhibitors are recommended for patients with clinical heart failure. 
Annotations: ['@@heart:Anatomy##', '@@heart failure:Diseases##']
------------------------------
Sentence: Canagliflozin, dapagliflozin, empagliflozin, and ertugliflozin have been shown to reduce the risk of heart failure hospitalizations in patients:
Annotations: ['@@heart:Anatomy##', '@@heart failure:Diseases##']
------------------------------
Sentence: Who have type 2 diabetes mellitus and established cardiovascular disease. 
An

Annotations: ['@@asthma:Diseases##', '@@Eosinophilic:Anatomy##']
------------------------------
Sentence: Oral corticosteroid–dependent moderate to severe asthma. 
Annotations: ['@@Oral:Anatomy##', '@@asthma:Diseases##']
------------------------------
Sentence: Consider subcutaneous allergen immunotherapy for patients with persistent asthma when (1) there is a clear evidence of a relationship between symptoms and exposure to an allergen to which the patient is sensitive and (2) exposure reduction measures have failed. 
Annotations: ['@@subcutaneous:Anatomy##', '@@persistent asthma:Diseases##', '@@asthma:Diseases##']
------------------------------
Sentence: Common, but may be unrecognized; prevalence of gastroesophageal reflux disease among patients with asthma is between 34% and 89%. 
Annotations: ['@@gastroesophageal:Anatomy##', '@@gastroesophageal reflux:Diseases##', '@@gastroesophageal reflux disease:Diseases##', '@@reflux:Diseases##', '@@reflux disease:Diseases##', '@@disease:Disea

Sentence:  Edoxaban: (Major) Consider an edoxaban dosage reduction for patients being treated for deep venous thrombosis (DVT) or pulmonary embolism (PE) if concomitant use of mitapivat is necessary. 
Annotations: ['@@deep venous thrombosis:Diseases##', '@@venous thrombosis:Diseases##', '@@thrombosis:Diseases##', '@@DVT:Diseases##', '@@pulmonary:Anatomy##', '@@pulmonary embolism:Diseases##', '@@embolism:Diseases##', '@@PE:Diseases##']
------------------------------
Sentence: Based on clinical experience in patients with non-valvular atrial fibrillation no dose reduction is recommended for concomitant use of mitapivat. 
Annotations: ['@@atrial:Anatomy##', '@@atrial fibrillation:Diseases##', '@@fibrillation:Diseases##']
------------------------------
Sentence: Fentanyl plasma concentrations will increase once the inducer is stopped, which may increase or prolong the therapeutic and adverse effects, including serious respiratory depression. 
Annotations: ['@@plasma:Anatomy##', '@@respirat

Annotations: ['@@blood:Anatomy##', '@@iron overload:Diseases##']
------------------------------
Sentence: Administration of iron to premature neonates can increase the risk of developing hemolytic anemia because these neonates may have a low vitamin E serum concentration. 
Annotations: ['@@premature neonates:Diseases##', '@@hemolytic anemia:Diseases##', '@@anemia:Diseases##', '@@serum:Anatomy##']
------------------------------
Sentence: Hemochromatosis causes the body to lose its ability to regulate the amount of iron that is absorbed, leading to excess iron absorption and tissue storage. 
Annotations: ['@@Hemochromatosis:Diseases##', '@@body:Anatomy##', '@@tissue:Anatomy##']
------------------------------
Sentence: Massive deposition of iron ( hemosiderosis ) in parenchymal tissues in these conditions may damage the liver, heart, pancreas and other tissues. 
Annotations: ['@@hemosiderosis:Diseases##', '@@parenchymal:Anatomy##', '@@tissues:Anatomy##', '@@liver:Anatomy##', '@@heart:Anat

In [272]:
print(len(selected_annotations))
print(len(selected_sentences))
#print(sentences_sub[102])
#entities_sub[102]

1180
1180


In [273]:
#template 85

In [274]:
import pandas as pd
import json

input_txt = selected_sentences[0:10]           ####change####  
output = selected_annotations[0:10]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Read the following text and identify all the diseases and anatomy related terms",
"input":f"{text}",
"output":f"Here are all the diseases and anatomy related terms: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 85.json", "w") as f:     ####change####
    f.write(output_json)

In [275]:
#template 86

In [276]:
import pandas as pd
import json

input_txt = selected_sentences[10:20]           ####change####  
output = selected_annotations[10:20]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"What are the diseases and anatomy related terms in the sentence given below?",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 86.json", "w") as f:     ####change####
    f.write(output_json)

In [277]:
#template 87

In [278]:
import pandas as pd
import json

input_txt = selected_sentences[20:30]           ####change####  
output = selected_annotations[20:30]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"In the given text, find and record all instances of anatomies and diseases.",
"input":f"{text}",
"output": entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 87.json", "w") as f:     ####change####
    f.write(output_json)

In [279]:
#template 88

In [280]:
import pandas as pd
import json

input_txt = selected_sentences[30:40]           ####change####  
output = selected_annotations[30:40]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"As a medical professional look at the following text and identify all the diseases and anatomy related terms", 
"input":f"{text}",
"output": entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 88.json", "w") as f:     ####change####
    f.write(output_json)

In [281]:
#template 89

In [282]:
import pandas as pd
import json

input_txt = selected_sentences[40:50]           ####change####  
output = selected_annotations[40:50]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Your task is to read the following text and note down all the words that are of the category 'anatomy' and 'disease'", 
"input":f"{text}",
"output": f"Here are all the words of the category 'anatomy' and 'disease'{entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 89.json", "w") as f:     ####change####
    f.write(output_json)

In [283]:
# Remove elements from 'sentences' list
idx = indices[0:50]
for index in sorted(idx, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(idx, reverse=True):
    del entities_sub[index]
    
print(len(sentences_sub))
print(len(entities_sub))

10207
10207


In [284]:
#template 90-94 (diseases+specialty)

In [285]:
# Find sentences with both "Drugs" and "Symptoms" tags
selected_sentences = []
selected_annotations = []
indices = []

for i, sentence in enumerate(sentences_sub):
    annotations = entities_sub[i]
    
    # Check if "Drugs" and "Symptoms" tags are both present in annotations
    if any("Specialty" in tag for tag in annotations) and any("Diseases" in tag for tag in annotations):
        selected_sentences.append(sentence)
        
        # Filter annotations to include only "Drugs" and "Symptoms" tags
        filtered_annotations = [tag for tag in annotations if "Specialty" in tag or "Diseases" in tag]
        selected_annotations.append(filtered_annotations)
        indices.append(i)

# Print the selected sentences and their corresponding filtered annotations
for sentence, annotations in zip(selected_sentences, selected_annotations):
    print("Sentence:", sentence)
    print("Annotations:", annotations)
    print("-" * 30)


Sentence: Consider a dosage reduction for patients with CML in accelerated phase who have achieved a major cytogenetic response. 
Annotations: ['@@CML:Diseases##', '@@cytogenetic:Specialty##']
------------------------------
Sentence: Consider a dosage reduction for patients with CML in accelerated phase who have achieved a major cytogenetic response. 
Annotations: ['@@CML:Diseases##', '@@cytogenetic:Specialty##']
------------------------------
Sentence:  During clinical trials with sodium ferric gluconate complex, cardiovascular adverse events reported in both adult and pediatric trials included hypotension (29% adults, 28% to 41% pediatrics), hypertension (13% adults, 23% pediatrics), and sinus tachycardia (5% adults, 13% to 21% pediatrics). 
Annotations: ['@@pediatrics:Specialty##', '@@hypertension:Diseases##', '@@pediatrics:Specialty##', '@@sinus tachycardia:Diseases##', '@@tachycardia:Diseases##', '@@pediatrics:Specialty##']
------------------------------
Sentence:  Hematologic adv

In [286]:
print(len(selected_annotations))
print(len(selected_sentences))
print(len(sentences_sub))
print(len(entities_sub))
#print(sentences_sub[102])
#entities_sub[102]

130
130
10207
10207


In [287]:
print(len(sentences_sub))
print(len(entities_sub))

10207
10207


In [288]:
#template 90

In [289]:
import pandas as pd
import json

input_txt = selected_sentences[0:10]           ####change####  
output = selected_annotations[0:10]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"As a clinical specialist look at the following text and identify all the diseases and specialty related terms", 
"input":f"{text}",
"output": f"As a clinical specialist, these are the diseases and specialties that I have identified in this text: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 90.json", "w") as f:     ####change####
    f.write(output_json)

In [290]:
#template 91

In [291]:
import pandas as pd
import json

input_txt = selected_sentences[10:20]           ####change####  
output = selected_annotations[10:20]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"As a medical professional look at the following text and identify all the diseases and specialty related terms", 
"input":f"{text}",
"output": f"As a medical professional, these are the diseases and specialties that I have identified in this text: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 91.json", "w") as f:     ####change####
    f.write(output_json)

In [292]:
#template 92

In [293]:
import pandas as pd
import json

input_txt = selected_sentences[20:30]           ####change####  
output = selected_annotations[20:30]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"In the given text, find and record all instances of specialties and diseases.",
"input":f"{text}",
"output": f"Recorded instances of specialties and diseases are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 92.json", "w") as f:     ####change####
    f.write(output_json)

In [294]:
#template 93

In [295]:
import pandas as pd
import json

input_txt = selected_sentences[30:40]           ####change####  
output = selected_annotations[30:40]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"What are the diseases and specialties in the sentence given below?",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 93.json", "w") as f:     ####change####
    f.write(output_json)

In [296]:
#template 94

In [297]:
import pandas as pd
import json

input_txt = selected_sentences[40:50]           ####change####  
output = selected_annotations[40:50]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Your task is to read the following text and note down all the words that are of the category 'anatomy' and 'disease'", 
"input":f"{text}",
"output": f"Here are all the words of the category 'anatomy' and 'disease'{entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 94.json", "w") as f:     ####change####
    f.write(output_json)

In [298]:
# Remove elements from 'sentences' list
idx = indices[0:50]
for index in sorted(idx, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(idx, reverse=True):
    del entities_sub[index]
    
print(len(sentences_sub))
print(len(entities_sub))

10157
10157


In [299]:
#all entity templates that we had skipped earlier (template 36-41 i.e 16-21 in excel) we dont have 42

In [300]:
#creation of 8_entities list 

# Annotations to remove
annotations_to_remove = ['Socialcontext', 'Substance', 'Environmentgeographicallocation', 'Qualifier', 'Event', 'Physicalobjects']

# Remove unwanted annotations from each list in entities_sub
updated_entities = []

for annotations_list in entities_sub:
    updated_annotations = [annotation for annotation in annotations_list if all(tag not in annotation for tag in annotations_to_remove)]
    updated_entities.append(updated_annotations)
    
replacement_string = "There are none"

for i, sublist in enumerate(updated_entities):
    if not sublist:  # Check if the sublist is empty
        updated_entities[i] = [replacement_string]

In [301]:
entities_sub = updated_entities

In [302]:
#template 36

In [303]:
import pandas as pd
import json

input_txt = sentences_sub[0:10]       
output = entities_sub[0:10]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Anatomies, Specialties, Clinical findings, Drugs"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"As  a medical professional, identify all the {list_of_entities} from the text given to you", 
"input":f"{text}",
"output":f"List of entities in the text are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 36.json", "w") as f:     
    f.write(output_json)

In [304]:
#template 37

In [305]:
import pandas as pd
import json

input_txt = sentences_sub[10:20]       
output = entities_sub[10:20]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Anatomies, Specialties, Clinical findings, Drugs"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"As a Clinical specialist, identify all the {list_of_entities} from the text given to you", 
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 37.json", "w") as f:     
    f.write(output_json)

In [306]:
#template 38

In [307]:
import pandas as pd
import json

input_txt = sentences_sub[20:30]       
output = entities_sub[20:30]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Anatomies, Specialties, Clinical findings, Drugs"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Extract all the terms and their respective category that would be important to any medical professional", 
"input":f"{text}",
"output":f"These are the extracted terms that would be important to a medical professional: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 38.json", "w") as f:     
    f.write(output_json)

In [308]:
#template 39

In [309]:
import pandas as pd
import json

input_txt = sentences_sub[30:40]       
output = entities_sub[30:40]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Anatomies, Specialties, Clinical findings, Drugs"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"From the text below,Provide me all the medical terms and the categories they belong to", 
"input":f"{text}",
"output":f"All the medical terms along with their respective categories are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 39.json", "w") as f:     
    f.write(output_json)

In [310]:
#template 40

In [311]:
import pandas as pd
import json

input_txt = sentences_sub[40:50]       
output = entities_sub[40:50]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Anatomies, Specialties, Clinical findings, Drugs"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"The following text consists of various medical terms. Can you identify these terms and the categories they belong to?", 
"input":f"{text}",
"output": f"Here are all the medical terms and their respective categories{entities_str}. @@ indicates the start of a new medical term and its category while ## indicates the end of it"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 40.json", "w") as f:     
    f.write(output_json)

In [312]:
#template 41

In [313]:
import pandas as pd
import json

input_txt = sentences_sub[50:60]       
output = entities_sub[50:60]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Anatomies, Specialties, Clinical findings, Drugs"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"instruction":"Identify and classify all the concepts that would be important to a clinician using the sentence given below", 
"input":f"{text}",
"output": f"categories{entities_str}. @@ indicates the start of a new medical concept that would be important to a clinician followed by its classification. ## indicates the end of it"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 41.json", "w") as f:     
    f.write(output_json)

In [314]:
# Remove elements from 'sentences' list
idx = indices[0:60]
for index in sorted(idx, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(idx, reverse=True):
    del entities_sub[index]
    
print(len(sentences_sub))
print(len(entities_sub))

10097
10097


# 3 entity combination templates

In [315]:
#template 95-99 (Disease+symptoms+clinical findings)

In [316]:

selected_sentences = []
selected_annotations = []
indices = []

for i, sentence in enumerate(sentences_sub):
    annotations = entities_sub[i]
    
    # Check if "Drugs" and "Symptoms" tags are both present in annotations
    if any("Symptoms" in tag for tag in annotations) and any("Diseases" in tag for tag in annotations) and any("Clinicalfinding" in tag for tag in annotations):
        selected_sentences.append(sentence)
        
        # Filter annotations to include only "Drugs" and "Symptoms" tags
        filtered_annotations = [tag for tag in annotations if "Symptoms" in tag or "Diseases" in tag or "Clinicalfinding" in tag]
        selected_annotations.append(filtered_annotations)
        indices.append(i)

# Print the selected sentences and their corresponding filtered annotations
for sentence, annotations in zip(selected_sentences, selected_annotations):
    print("Sentence:", sentence)
    print("Annotations:", annotations)
    print("-" * 30)


Sentence: Monitor patients for signs and symptoms of fluid retention and manage as clinically indicated. 
Annotations: ['@@signs:Symptoms##', '@@signs and symptoms:Symptoms##', '@@symptoms:Symptoms##', '@@fluid retention:Diseases##', '@@retention:Clinicalfinding##']
------------------------------
Sentence: Permanently discontinue ponatinib in patients who develop a GI perforation. 
Annotations: ['@@develop:Clinicalfinding##', '@@GI perforation:Diseases##', '@@perforation:Symptoms##']
------------------------------
Sentence: Insomnia (11% to 13%) and anxiety (4.8% to 18%) were reported in patients with chronic phase (n = 270), accelerated phase (n = 85), and blast phase (n = 62) chronic myelogenous leukemia and acute lymphoblastic leukemia (n = 32) who received ponatinib in a clinical trial.
Annotations: ['@@Insomnia:Symptoms##', '@@anxiety:Clinicalfinding##', '@@blast phase:Diseases##', '@@chronic myelogenous leukemia:Diseases##', '@@myelogenous leukemia:Diseases##', '@@leukemia:Diseas

Sentence: Nervous system disorders (eg, sleep disturbance, irritability, paresthesia, generalized weakness, posttraumatic stress disorder). 
Annotations: ['@@Nervous:Symptoms##', '@@disorders:Diseases##', '@@sleep:Clinicalfinding##', '@@sleep disturbance:Diseases##', '@@irritability:Diseases##', '@@paresthesia:Symptoms##', '@@generalized weakness:Symptoms##', '@@weakness:Symptoms##', '@@posttraumatic:Symptoms##', '@@posttraumatic stress disorder:Diseases##', '@@stress:Symptoms##', '@@disorder:Diseases##', '@@Nervous system disorders:Diseases##']
------------------------------
Sentence: Diagnosis is based on presence of proximal muscle weakness (with or without pathognomonic cutaneous features of dermatomyositis), elevated skeletal muscle enzyme levels, abnormal EMG results, and inflammation on muscle biopsy. 
Annotations: ['@@proximal muscle weakness:Symptoms##', '@@muscle weakness:Symptoms##', '@@weakness:Symptoms##', '@@dermatomyositis:Diseases##', '@@enzyme levels:Clinicalfinding##'

------------------------------
Sentence: Infectious Diseases Society of America guideline suggests use of tofacitinib in hospitalized patients with severe COVID-19 who do not require mechanical ventilation (noninvasive or invasive), along with remdesivir and corticosteroids (unless contraindicated). 
Annotations: ['@@severe COVID-19:Diseases##', '@@COVID-19:Diseases##', '@@ventilation:Clinicalfinding##', '@@contraindicated:Symptoms##']
------------------------------
Sentence: WHO guideline summarizes evidence for use of interleukin-6 inhibitors (tocilizumab or sarilumab) from up to 27 studies for 6 outcomes; overall, interleukin-6 inhibitors reduce mortality, decrease need for mechanical ventilation, and may decrease duration of mechanical ventilation and hospitalization, with little evidence for adverse events leading to discontinuation of drug, including secondary bacterial infections. 
Annotations: ['@@ventilation:Clinicalfinding##', '@@ventilation:Clinicalfinding##', '@@infections:

------------------------------
Sentence: Assess sleep pattern and duration in all patients with type 2 diabetes. 
Annotations: ['@@sleep:Clinicalfinding##', '@@sleep pattern:Symptoms##', '@@diabetes:Diseases##', '@@sleep pattern and duration:Symptoms##', '@@type 2 diabetes:Diseases##']
------------------------------
Sentence: Treatment of sleep apnea improves quality of life and positively affects blood pressure. 
Annotations: ['@@sleep:Clinicalfinding##', '@@sleep apnea:Diseases##', '@@apnea:Diseases##', '@@quality of life:Symptoms##', '@@affects:Clinicalfinding##', '@@blood pressure:Clinicalfinding##', '@@pressure:Symptoms##']
------------------------------
Sentence: Excess of fat in the liver (steatosis) that is not a result of excessive alcohol consumption or other secondary causes. 
Annotations: ['@@steatosis:Diseases##', '@@excessive alcohol consumption:Symptoms##', '@@alcohol consumption:Clinicalfinding##']
------------------------------
Sentence: Depression and diabetes-related

Sentence:  Diphenhydramine; Hydrocodone; Phenylephrine: (Moderate) Monitor for reduced efficacy of hydrocodone and signs of opioid withdrawal if coadministration with mitapivat is necessary; consider increasing the dose of hydrocodone as needed. 
Annotations: ['@@signs:Symptoms##', '@@opioid withdrawal:Diseases##', '@@withdrawal:Clinicalfinding##']
------------------------------
Sentence: Coadministration of a CYP3A inducer like mitapivat with fentanyl, a CYP3A substrate, may decrease exposure to fentanyl resulting in decreased efficacy or onset of withdrawal symptoms in a patient who has developed physical dependence to fentanyl. 
Annotations: ['@@exposure:Clinicalfinding##', '@@exposure to:Clinicalfinding##', '@@withdrawal:Clinicalfinding##', '@@withdrawal symptoms:Symptoms##', '@@symptoms:Symptoms##', '@@developed:Clinicalfinding##', '@@physical dependence:Diseases##', '@@dependence:Diseases##']
------------------------------
Sentence: Fentanyl plasma concentrations will increase on

In [317]:
print(len(selected_annotations))
print(len(selected_sentences))
print(len(sentences_sub))
print(len(entities_sub))
#print(sentences_sub[102])
#entities_sub[102]

576
576
10097
10097


In [318]:
#template 95

In [319]:
import pandas as pd
import json

input_txt = selected_sentences[0:10]           ####change####  
output = selected_annotations[0:10]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Read the following text and identify all the diseases, symptoms and clinical findings",
"input":f"{text}",
"output":f"After reading the text, the identified diseases, symptoms and clinical findings are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 95.json", "w") as f:     ####change####
    f.write(output_json)

In [320]:
#template 96

In [321]:
import pandas as pd
import json

input_txt = selected_sentences[10:20]           ####change####  
output = selected_annotations[10:20]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"What are the diseases, symptoms and clinical findings in the sentence given below?",
"input":f"{text}",
"output":f"The identified diseases, symptoms and clinical findings are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 96.json", "w") as f:     ####change####
    f.write(output_json)

In [322]:
#template 97

In [323]:
import pandas as pd
import json

input_txt = selected_sentences[20:30]           ####change####  
output = selected_annotations[20:30]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"In the given text, find and record all instances of symptoms, clinical findings and diseases.",
"input":f"{text}",
"output": entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 97.json", "w") as f:     ####change####
    f.write(output_json)

In [324]:
#template 98

In [325]:
import pandas as pd
import json

input_txt = selected_sentences[30:40]           ####change####  
output = selected_annotations[30:40]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"As a medical professional look at the following text and identify all the diseases, symptoms and clinical findings", 
"input":f"{text}",
"output": f"As a medical professional, I have identified the following diseases, symptoms and clinical findings: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 98.json", "w") as f:     ####change####
    f.write(output_json)

In [326]:
#template 99

In [327]:
import pandas as pd
import json

input_txt = selected_sentences[40:50]           ####change####  
output = selected_annotations[40:50]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"As a clinical specialist look at the following text and identify all the diseases, symptoms and clinical findings", 
"input":f"{text}",
"output": f"As a clinical specialist, I have identified the following diseases, symptoms and clinical findings: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 99.json", "w") as f:     ####change####
    f.write(output_json)

In [328]:
# Remove elements from 'sentences' list
idx = indices[0:50]
for index in sorted(idx, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(idx, reverse=True):
    del entities_sub[index]
    
print(len(sentences_sub))
print(len(entities_sub))

10047
10047


In [329]:
#template 100-104 (diseases + clinical findings + procedures)

In [330]:
selected_sentences = []
selected_annotations = []
indices = []

for i, sentence in enumerate(sentences_sub):
    annotations = entities_sub[i]
    
    # Check if "Drugs" and "Symptoms" tags are both present in annotations
    if any("Procedures" in tag for tag in annotations) and any("Diseases" in tag for tag in annotations) and any("Clinicalfinding" in tag for tag in annotations):
        selected_sentences.append(sentence)
        
        # Filter annotations to include only "Drugs" and "Symptoms" tags
        filtered_annotations = [tag for tag in annotations if "Procedures" in tag or "Diseases" in tag or "Clinicalfinding" in tag]
        selected_annotations.append(filtered_annotations)
        indices.append(i)

# Print the selected sentences and their corresponding filtered annotations
for sentence, annotations in zip(selected_sentences, selected_annotations):
    print("Sentence:", sentence)
    print("Annotations:", annotations)
    print("-" * 30)


Sentence: Therapy interruption and a dose reduction may be necessary in patients who develop severe myelosuppression. 
Annotations: ['@@Therapy:Procedures##', '@@develop:Clinicalfinding##', '@@myelosuppression:Diseases##']
------------------------------
Sentence: Do not start or resume ponatinib until at least 2 weeks after major surgery and until adequate wound healing has occurred. 
Annotations: ['@@major surgery:Procedures##', '@@surgery:Procedures##', '@@wound:Diseases##', '@@wound healing:Clinicalfinding##']
------------------------------
Sentence: The safety of resuming ponatinib therapy after wound healing complications have resolved has not been established.
Annotations: ['@@therapy:Procedures##', '@@wound:Diseases##', '@@wound healing:Clinicalfinding##', '@@complications:Diseases##']
------------------------------
Sentence: Available data from postmarketing reports with sodium ferric gluconate complex injection use in pregnancy are insufficient to assess the risk of major birt

Sentence: IF on supplemental oxygen, including noninvasive ventilation or high-flow oxygen, AND there is evidence of systemic inflammation and rapidly increasing oxygen needs while on dexamethasone..
Annotations: ['@@supplemental oxygen:Procedures##', '@@noninvasive ventilation:Procedures##', '@@ventilation:Clinicalfinding##', '@@systemic inflammation:Diseases##', '@@inflammation:Diseases##', '@@high-flow oxygen:Procedures##']
------------------------------
Sentence: The NIH COVID-19 treatment guidelines recommend a single 8 mg/kg (actual body weight, up to 800 mg) IV dose given with dexamethasone (with or without remdesivir) for hospitalized patients on supplemental oxygen, including high-flow oxygen and noninvasive ventilation, IF exhibiting signs of systemic inflammation and rapidly increasing oxygen needs. 
Annotations: ['@@COVID-19:Diseases##', '@@treatment:Procedures##', '@@body weight:Clinicalfinding##', '@@hospitalized:Procedures##', '@@supplemental oxygen:Procedures##', '@@non

Annotations: ['@@Assessing:Procedures##', '@@suicide:Diseases##', '@@violence:Clinicalfinding##']
------------------------------
Sentence: Several augmentation strategies validated for use in nonpregnant bipolar patients for managing depression and relapse prevention may be used; however, data for pregnant bipolar patients is scarce. 
Annotations: ['@@augmentation:Procedures##', '@@strategies:Clinicalfinding##', '@@bipolar:Diseases##', '@@depression:Diseases##', '@@relapse prevention:Procedures##', '@@prevention:Procedures##', '@@pregnant:Clinicalfinding##', '@@bipolar:Diseases##']
------------------------------
Sentence: Psychotherapy techniques include bipolar-specific cognitive behavioral therapy, family-focused therapy, interpersonal and social rhythm therapy, group psychoeducation, and systemic care management. 
Annotations: ['@@Psychotherapy:Procedures##', '@@bipolar:Diseases##', '@@cognitive:Clinicalfinding##', '@@cognitive behavioral therapy:Procedures##', '@@behavioral therapy

------------------------------
Sentence:  Codeine; Promethazine: (Moderate) Monitor for reduced efficacy of codeine and signs of opioid withdrawal in patients who have developed physical dependence if coadministration with mitapivat is necessary; consider increasing the dose of codeine as needed. 
Annotations: ['@@opioid withdrawal:Diseases##', '@@withdrawal:Clinicalfinding##', '@@developed:Clinicalfinding##', '@@physical dependence:Diseases##', '@@dependence:Diseases##', '@@Monitor:Procedures##']
------------------------------
Sentence:  Colchicine: (Major) Due to the risk for serious colchicine toxicity including multi-organ failure and death, avoid coadministration of colchicine and mitapivat in patients with normal renal and hepatic function unless the use of both agents is imperative. 
Annotations: ['@@colchicine toxicity:Diseases##', '@@toxicity:Diseases##', '@@multi-organ failure:Diseases##', '@@organ failure:Diseases##', '@@death:Clinicalfinding##', '@@hepatic function:Clinical

Sentence:   Norethindrone; Ethinyl Estradiol; Ferrous fumarate: (Major) Women taking both estrogens and mitapivat should report breakthrough bleeding to their prescribers. 
Annotations: ['@@Women:Clinicalfinding##', '@@taking:Procedures##', '@@breakthrough bleeding:Diseases##', '@@bleeding:Diseases##', '@@prescribers:Procedures##']
------------------------------
Sentence:   Norgestimate; Ethinyl Estradiol: (Major) Women taking both estrogens and mitapivat should report breakthrough bleeding to their prescribers. 
Annotations: ['@@Women:Clinicalfinding##', '@@taking:Procedures##', '@@breakthrough bleeding:Diseases##', '@@bleeding:Diseases##', '@@prescribers:Procedures##']
------------------------------
Sentence:  Oxycodone: (Moderate) Monitor for reduced efficacy of oxycodone and signs of opioid withdrawal if coadministration with mitapivat is necessary; consider increasing the dose of oxycodone as needed. 
Annotations: ['@@opioid withdrawal:Diseases##', '@@withdrawal:Clinicalfinding##'

In [331]:
print(len(selected_annotations))
print(len(selected_sentences))
print(len(sentences_sub))
print(len(entities_sub))
#print(sentences_sub[102])
#entities_sub[102]

489
489
10047
10047


In [332]:
#template 100

In [333]:
import pandas as pd
import json

input_txt = selected_sentences[0:10]           ####change####  
output = selected_annotations[0:10]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"What are the different diseases, procedures and clinical findings in the sentence given below?",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 100.json", "w") as f:     ####change####
    f.write(output_json)

In [334]:
#template 101

In [335]:
import pandas as pd
import json

input_txt = selected_sentences[10:20]           ####change####  
output = selected_annotations[10:20]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"In the given text, find and record all the diseases, clinical findings and procedures.",
"input":f"{text}",
"output": f"Recorded diseases, clinical findings and procedures are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 101.json", "w") as f:     ####change####
    f.write(output_json)

In [336]:
#template 102

In [337]:
import pandas as pd
import json

input_txt = selected_sentences[20:30]           ####change####  
output = selected_annotations[20:30]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Identify all the diseases, procedures and clinical findings that would be important to any medical professional", 
"input":f"{text}",
"output": f"These are the diseases, procedures and clinical findings that would be important to any medical professional: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 102.json", "w") as f:     ####change####
    f.write(output_json)

In [338]:
#template 103

In [339]:
import pandas as pd
import json

input_txt = selected_sentences[30:40]           ####change####  
output = selected_annotations[30:40]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"As a clinical specialist look at the following text and identify all the diseases, procedures and clinical findings", 
"input":f"{text}",
"output": entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 103.json", "w") as f:     ####change####
    f.write(output_json)

In [340]:
#template 104

In [341]:
import pandas as pd
import json

input_txt = selected_sentences[40:50]           ####change####  
output = selected_annotations[40:50]            ####change####
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Read the following text and identify all the diseases, procedures and clinical findings",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 104.json", "w") as f:     ####change####
    f.write(output_json)

In [342]:
# Remove elements from 'sentences' list
idx = indices[0:50]
for index in sorted(idx, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(idx, reverse=True):
    del entities_sub[index]
    
print(len(sentences_sub))
print(len(entities_sub))

9997
9997


# saving our progress 

In [343]:
#saving 
import pickle
with open('Remaining data.pkl', 'wb') as f:
    pickle.dump((entities_sub, sentences_sub), f)

In [344]:
import pickle
with open('Remaining data.pkl', 'rb') as f:
    loaded_data = pickle.load(f)
loaded_annotations, loaded_sentences = loaded_data

In [345]:
print(len(loaded_annotations))
print(len(loaded_sentences))

9997
9997


In [346]:
loaded_annotations[1]

['@@tetracycline antibiotics:Drugs##', '@@chelate:Drugs##']

In [347]:
loaded_sentences[1]

'Tetracycline absorption may be reduced as tetracycline antibiotics can chelate with divalent or trivalent cations. '

In [348]:
#Multi turn templates 

In [349]:
entities_sub = loaded_annotations
sentences_sub = loaded_sentences

In [350]:
#creation of 8_entities list 

# Annotations to remove
annotations_to_remove = ['Socialcontext', 'Substance', 'Environmentgeographicallocation', 'Qualifier', 'Event', 'Physicalobjects']

# Remove unwanted annotations from each list in entities_sub
updated_entities = []

for annotations_list in entities_sub:
    updated_annotations = [annotation for annotation in annotations_list if all(tag not in annotation for tag in annotations_to_remove)]
    updated_entities.append(updated_annotations)
    
replacement_string = "There are none"

for i, sublist in enumerate(updated_entities):
    if not sublist:  # Check if the sublist is empty
        updated_entities[i] = [replacement_string]

In [351]:
len(updated_entities)

9997

In [352]:
entities_sub = updated_entities

In [353]:
#template 105

In [354]:
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Anatomies, Specialties, Clinical findings, Drugs"

In [355]:
# Find sentences with both "Drugs" and "Symptoms" tags
selected_sentences = []
selected_annotations = []
indices = []

 

for i, sentence in enumerate(sentences_sub):
    annotations = entities_sub[i]

    # Check if "Drugs" and "Symptoms" tags are both present in annotations
    if any("Drugs" in tag for tag in annotations) and any("Clinicalfinding" in tag for tag in annotations):
        selected_sentences.append(sentence)

        # Filter annotations to include only "Drugs" and "Symptoms" tags
        filtered_annotations = [tag for tag in annotations if "Drugs" in tag or "Clinicalfinding" in tag]
        selected_annotations.append(filtered_annotations)
        indices.append(i)

 

# print the selected sentences and their corresponding filtered annotations
for sentence, annotations in zip(selected_sentences, selected_annotations):
    print("Sentence:", sentence)
    print("Annotations:", annotations)
    print("-" * 30)

Sentence: Tetracyclines may displace methotrexate from protein binding sites leading to increased methotrexate levels. 
Annotations: ['@@methotrexate:Drugs##', '@@protein binding:Clinicalfinding##', '@@binding:Clinicalfinding##', '@@methotrexate:Drugs##', '@@Tetracyclines:Drugs##']
------------------------------
Sentence: Bacterostatic antibacterials like tetracyclines may antagonize the bactericidal effects of penicillins which may reduce their efficacy. 
Annotations: ['@@antibacterials:Drugs##', '@@penicillins:Drugs##', '@@Bacterostatic:Clinicalfinding##', '@@bactericidal:Clinicalfinding##']
------------------------------
Sentence: Bacterostatic antibacterials like tetracyclines may antagonize the bactericidal effects of penicillins which may reduce their efficacy. 
Annotations: ['@@antibacterials:Drugs##', '@@Bacterostatic:Clinicalfinding##', '@@bactericidal:Clinicalfinding##']
------------------------------
Sentence: Bacterostatic antibacterials like tetracyclines may antagonize th

------------------------------
Sentence:  Mycophenolate: (Major) Conflicting information has been reported regarding coadministration of mycophenolate and iron salts. 
Annotations: ['@@Mycophenolate:Drugs##', '@@Conflicting:Clinicalfinding##', '@@mycophenolate:Drugs##', '@@iron:Drugs##', '@@iron salts:Drugs##', '@@salts:Drugs##']
------------------------------
Sentence: Due to the discrepant findings and study differences, additional data are needed to clarify the potential interaction between iron salts and MMF. 
Annotations: ['@@interaction:Clinicalfinding##', '@@iron:Drugs##', '@@iron salts:Drugs##', '@@salts:Drugs##']
------------------------------
Sentence:  Naproxen; Esomeprazole: (Moderate) The bioavailability of oral iron salts is influenced by gastric pH, and the concomitant administration of proton pump inhibitors can decrease iron absorption. 
Annotations: ['@@Naproxen:Drugs##', '@@Esomeprazole:Drugs##', '@@iron:Drugs##', '@@iron salts:Drugs##', '@@salts:Drugs##', '@@pH:Clin

------------------------------
Sentence: CDC suggests that vaccine administration may be considered beyond the usual age limit (26 years) up to age 45 years for people at risk of acquiring HPV (eg, people who are sexually active but not in a long-term monogamous relationship). 
Annotations: ['@@vaccine:Drugs##', '@@age:Clinicalfinding##', '@@age:Clinicalfinding##', '@@sexually:Clinicalfinding##', '@@monogamous:Clinicalfinding##']
------------------------------
Sentence: Note that there are several formulations of mRNA vaccines available, and they vary in terms of storage and reconstitution requirements as well as age appropriateness. 
Annotations: ['@@vaccines:Drugs##', '@@age:Clinicalfinding##', '@@mRNA vaccines:Drugs##']
------------------------------
Sentence: Cocooning— providing booster doses (before the birth) to family members who will be in close contact with the infant—is an additional strategy to protect the infant during vulnerable period before third dose in infant DTaP ser

------------------------------
Sentence: The non-heme ferric form of iron needs an acidic intragastric pH to be reduced to ferrous and to be absorbed. 
Annotations: ['@@iron:Drugs##', '@@pH:Clinicalfinding##', '@@ferrous:Drugs##', '@@absorbed:Clinicalfinding##']
------------------------------
Sentence: Proton pump inhibitors have long-lasting effects on the secretion of gastric acid and thus, increase the pH of the stomach. 
Annotations: ['@@pH:Clinicalfinding##', '@@Proton pump inhibitors:Drugs##']
------------------------------
Sentence: The increase in intragastric pH can interfere with the absorption of iron salts. 
Annotations: ['@@pH:Clinicalfinding##', '@@absorption:Clinicalfinding##', '@@iron:Drugs##', '@@iron salts:Drugs##', '@@salts:Drugs##']
------------------------------
Sentence: Oral absorption of iron supplements is reduced if given with antacids; the buffering agents contained in didanosine tablets and powder likewise reduce iron salt absorption. 
Annotations: ['@@Oral 

Annotations: ['@@iron:Drugs##', '@@iron salts:Drugs##', '@@salts:Drugs##', '@@pH:Clinicalfinding##', '@@iron:Drugs##', '@@absorption:Clinicalfinding##', '@@Proton pump inhibitors:Drugs##', '@@proton pump inhibitors:Drugs##']
------------------------------
Sentence: The non-heme ferric form of iron needs an acidic intragastric pH to be reduced to ferrous and to be absorbed. 
Annotations: ['@@iron:Drugs##', '@@pH:Clinicalfinding##', '@@ferrous:Drugs##', '@@absorbed:Clinicalfinding##']
------------------------------
Sentence: The increase in intragastric pH can interfere with the absorption of iron salts. 
Annotations: ['@@pH:Clinicalfinding##', '@@absorption:Clinicalfinding##', '@@iron:Drugs##', '@@iron salts:Drugs##', '@@salts:Drugs##']
------------------------------
Sentence:  Rabeprazole: (Moderate) The bioavailability of oral iron salts is influenced by gastric pH, and the concomitant administration of proton pump inhibitors can decrease iron absorption. 
Annotations: ['@@Rabeprazole

...

Sentence: Concomitant use with other strong CYP3A inhibitors increased mitapivat overall exposure by 3.6 to 4.9-fold. 
Annotations: ['@@mitapivat:Drugs##', '@@exposure:Clinicalfinding##']
------------------------------
Sentence: Although the potential effect of CYP inducers on the pharmacokinetics of avanafil has not been evaluated, plasma concentrations may decrease. 
Annotations: ['@@pharmacokinetics:Clinicalfinding##', '@@avanafil:Drugs##']
------------------------------
Sentence: Avatrombopag is a CYP2C9 and CYP3A substrate, and dual moderate or strong inducers such as mitapivat decrease avatrombopag exposure, which may reduce efficacy. 
Annotations: ['@@Avatrombopag:Drugs##', '@@mitapivat:Drugs##', '@@avatrombopag:Drugs##', '@@exposure:Clinicalfinding##']
------------------------------
Sentence: Coadministration with another strong CYP3A inducer decreased mitapivat overall exposure by 91% to 95%. 
Annotations: ['@@mitapivat:Drugs##', '@@exposure:Clinicalfinding##']
---------------

------------------------------
Sentence: Efavirenz decreased mitapivat overall and peak exposure by approximately 60% and 30%, respectively, after mitapivat 5 or 20 mg twice daily. 
Annotations: ['@@mitapivat:Drugs##', '@@exposure:Clinicalfinding##', '@@mitapivat:Drugs##']
------------------------------
Sentence: Efavirenz decreased mitapivat overall and peak exposure by 55% and 24%, respectively, after mitapivat 50 mg twice daily. 
Annotations: ['@@mitapivat:Drugs##', '@@exposure:Clinicalfinding##', '@@mitapivat:Drugs##']
------------------------------
Sentence: Monitor hemoglobin and titrate the mitapivat dose based on response; do not exceed 100 mg PO twice daily. 
Annotations: ['@@mitapivat:Drugs##', '@@response:Clinicalfinding##']
------------------------------
Sentence: Efavirenz decreased mitapivat overall and peak exposure by approximately 60% and 30%, respectively, after mitapivat 5 or 20 mg twice daily. 
Annotations: ['@@mitapivat:Drugs##', '@@exposure:Clinicalfinding##', '@@

------------------------------
Sentence: Coadministration with another moderate CYP3A inhibitor increased mitapivat overall exposure by 2.6-fold. 
Annotations: ['@@mitapivat:Drugs##', '@@exposure:Clinicalfinding##']
------------------------------
Sentence: Monitor hemoglobin and titrate the mitapivat dose based on response; do not exceed 100 mg PO twice daily. 
Annotations: ['@@mitapivat:Drugs##', '@@response:Clinicalfinding##']
------------------------------
Sentence: Coadministration with another moderate CYP3A inducer decreased mitapivat overall exposure by 55% to 60%. 
Annotations: ['@@mitapivat:Drugs##', '@@exposure:Clinicalfinding##']
------------------------------
Sentence: Coadministration with another moderate CYP3A inhibitor increased mitapivat overall exposure by 2.6-fold. 
Annotations: ['@@mitapivat:Drugs##', '@@exposure:Clinicalfinding##']
------------------------------
Sentence: Coadministration increases mitapivat concentrations and may decrease ritonavir concentrations 

Annotations: ['@@Pharmacokinetics:Clinicalfinding##', '@@iron:Drugs##', '@@iron:Drugs##', '@@ferrous:Drugs##', '@@absorbed:Clinicalfinding##']
------------------------------
Sentence: Polysaccharide-iron complex is absorbed intact through the duodenum and upper small intestines. 
Annotations: ['@@iron:Drugs##', '@@absorbed:Clinicalfinding##']
------------------------------
Sentence: Although orally administered iron is absorbed in the duodenum, iron directly instilled into the duodenum is poorly absorbed.
Annotations: ['@@iron:Drugs##', '@@absorbed:Clinicalfinding##', '@@iron:Drugs##', '@@absorbed:Clinicalfinding##']
------------------------------
Sentence: Both ascorbic acid and meat (heme iron) will increase the absorption of non-heme iron. 
Annotations: ['@@ascorbic acid:Drugs##', '@@iron:Drugs##', '@@absorption:Clinicalfinding##', '@@iron:Drugs##']
------------------------------
Sentence: A hematopoetic transcription factor, known as NF-E 2 , regulates the absorption of iron by the

Annotations: ['@@Sodium Bicarbonate:Drugs##', '@@antacids:Drugs##', '@@iron:Drugs##', '@@interaction:Clinicalfinding##']
------------------------------
Sentence: Antacids may decrease the absorption of oral iron preparations. 
Annotations: ['@@Antacids:Drugs##', '@@absorption:Clinicalfinding##', '@@iron:Drugs##']
------------------------------
Sentence: At higher pH values, iron is more readily ionized to its ferric state and is more poorly absorbed. 
Annotations: ['@@pH:Clinicalfinding##', '@@values:Clinicalfinding##', '@@iron:Drugs##', '@@absorbed:Clinicalfinding##', '@@ferric:Drugs##']
------------------------------
Sentence:  Thyroid hormones: (Moderate) Oral thyroid hormones should be administered at least 4 hours before or after the ingestion of iron supplements. 
Annotations: ['@@hormones:Drugs##', '@@hormones:Drugs##', '@@ingestion:Clinicalfinding##', '@@iron:Drugs##']
------------------------------
Sentence: Oral iron salts have been reported to chelate oral thyroid hormones w

In [356]:
indices = indices[0:10]
indices 

[4, 7, 16, 21, 22, 23, 24, 25, 26, 27]

In [357]:
temp_entities = []
for i in indices: 
    temp_entities.append(entities_sub[i])

In [358]:
#checking if above code worked correctly 

print(selected_sentences[0])
print(temp_entities[0])
print(selected_annotations[0])

Tetracyclines may displace methotrexate from protein binding sites leading to increased methotrexate levels. 
['@@methotrexate:Drugs##', '@@protein binding:Clinicalfinding##', '@@binding:Clinicalfinding##', '@@methotrexate:Drugs##', '@@Tetracyclines:Drugs##']
['@@methotrexate:Drugs##', '@@protein binding:Clinicalfinding##', '@@binding:Clinicalfinding##', '@@methotrexate:Drugs##', '@@Tetracyclines:Drugs##']


In [359]:
import pandas as pd
import json

input_txt = selected_sentences[0:10]                    ####change####  
output1 = temp_entities                                ####change####
output2 = selected_annotations[0:10]                  ####change####
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities1, entities2 in zip(input_txt, output1, output2):
    # Join the output list elements into a single string
    entities_str1 = ' '.join(entities1)
    entities_str2 = ' '.join(entities2)
    
    example = {
"task":"Named Entity Recognition",
"instruction1":f"Examine below text and identify {list_of_entities}.",
"input":f"{text}",
"output1":f"After examining the text, these are the identified entities: {entities_str1}",
"instruction2":f"From above text identify the clinical findings and drugs.",
"output2": f"Here are the clinical findings and drugs identified in the text: {entities_str2}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 105.json", "w") as f:     ####change####
    f.write(output_json)

In [360]:
# Remove elements from 'sentences' list
idx = indices[0:10]
for index in sorted(idx, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(idx, reverse=True):
    del entities_sub[index]
    
print(len(sentences_sub))
print(len(entities_sub))

9987
9987


In [361]:
#template 106

In [362]:
# Find sentences with both "Drugs" and "Symptoms" tags
selected_sentences = []
selected_annotations = []
indices = []

 

for i, sentence in enumerate(sentences_sub):
    annotations = entities_sub[i]

    # Check if "Drugs" and "Symptoms" tags are both present in annotations
    if any("Drugs" in tag for tag in annotations) and any("Symptoms" in tag for tag in annotations):
        selected_sentences.append(sentence)

        # Filter annotations to include only "Drugs" and "Symptoms" tags
        filtered_annotations = [tag for tag in annotations if "Drugs" in tag or "Symptoms" in tag]
        selected_annotations.append(filtered_annotations)
        indices.append(i)

 

# print the selected sentences and their corresponding filtered annotations
for sentence, annotations in zip(selected_sentences, selected_annotations):
    print("Sentence:", sentence)
    print("Annotations:", annotations)
    print("-" * 30)
    
indices = indices[0:20]
temp_entities = []
for i in indices: 
    temp_entities.append(entities_sub[i])

print(selected_sentences[0])
print(temp_entities[0])
print(selected_annotations[0])

Sentence: Subsequent dose reduction: Permanently discontinue ponatinib therapy in patients unable to tolerate a dose of 15 mg once daily.
Annotations: ['@@ponatinib:Drugs##', '@@unable:Symptoms##']
------------------------------
Sentence: Serum lipase 2.1 to 5 times ULN and symptomatic; or serum lipase greater than 5 times ULN and asymptomatic: Hold ponatinib therapy.
Annotations: ['@@asymptomatic:Symptoms##', '@@ponatinib:Drugs##']
------------------------------
Sentence: For the first occurrence, resume treatment at the next lower dose upon resolution to grade 1 or less and complete resolution of symptoms; discontinue ponatinib for a recurrence. 
Annotations: ['@@symptoms:Symptoms##', '@@ponatinib:Drugs##']
------------------------------
Sentence: Other Nonhematologic Adverse Reactions Grade 1: Hold ponatinib therapy. 
Annotations: ['@@ponatinib:Drugs##', '@@Adverse Reactions:Symptoms##']
------------------------------
Sentence: Cutting, crushing, or otherwise manipulating tablets/ca

------------------------------
Sentence: During adult clinical trials with sodium ferric gluconate complex, hyperkalemia (6%), generalized edema (5%), leg edema, peripheral edema, hypoglycemia, edema, hypervolemia, and hypokalemia were reported. During adult clinical trials with ferric pyrophosphate citrate, peripheral edema was reported in 7% of patients receiving study drug versus 4% of patients receiving placebo.
Annotations: ['@@sodium ferric gluconate:Drugs##', '@@sodium ferric gluconate complex:Drugs##', '@@ferric gluconate:Drugs##', '@@ferric gluconate complex:Drugs##', '@@leg edema:Symptoms##', '@@hypokalemia:Symptoms##', '@@ferric pyrophosphate citrate:Drugs##', '@@pyrophosphate:Drugs##', '@@ferric:Drugs##', '@@ferric:Drugs##']
------------------------------
Sentence: At the initial visit, review immunization history and assess need for catch-up vaccines; at every interim examination, assess need for boosters or new vaccines based on age, interval change (eg, development of a 

------------------------------
Sentence: Butalbital; Acetaminophen; Caffeine: (Major) Increase the initial and second dose of ubrogepant to 100 mg if coadministered with butalbital as concurrent use may decrease ubrogepant exposure and reduce its efficacy. 
Annotations: ['@@Butalbital:Drugs##', '@@Acetaminophen:Drugs##', '@@Caffeine:Drugs##', '@@ubrogepant:Drugs##', '@@butalbital:Drugs##', '@@ubrogepant:Drugs##', '@@exposure:Symptoms##']
------------------------------
Sentence: Ubrogepant is a CYP3A4 substrate; butalbital is a moderate CYP3A4 inducer. 
Annotations: ['@@Ubrogepant:Drugs##', '@@butalbital:Drugs##', '@@CYP3A4 inducer:Symptoms##']
------------------------------
Sentence: Butalbital; Acetaminophen; Caffeine; Codeine: (Major) Increase the initial and second dose of ubrogepant to 100 mg if coadministered with butalbital as concurrent use may decrease ubrogepant exposure and reduce its efficacy. 
Annotations: ['@@Butalbital:Drugs##', '@@Acetaminophen:Drugs##', '@@Caffeine:Drug

Annotations: ['@@Nefazodone:Drugs##', '@@Contraindicated:Symptoms##', '@@ubrogepant:Drugs##', '@@nefazodone:Drugs##', '@@contraindicated:Symptoms##', '@@ubrogepant:Drugs##', '@@exposure:Symptoms##', '@@adverse effects:Symptoms##']
------------------------------
Sentence: Coadministration with another strong CYP3A4 inhibitor resulted in a 9.7-fold increase in the exposure of ubrogepant. 
Annotations: ['@@exposure:Symptoms##', '@@ubrogepant:Drugs##']
------------------------------
Sentence:  Nelfinavir: (Contraindicated) Coadministration of ubrogepant and nelfinavir is contraindicated as concurrent use may increase ubrogepant exposure and the risk of adverse effects. 
Annotations: ['@@Nelfinavir:Drugs##', '@@Contraindicated:Symptoms##', '@@ubrogepant:Drugs##', '@@nelfinavir:Drugs##', '@@contraindicated:Symptoms##', '@@ubrogepant:Drugs##', '@@exposure:Symptoms##', '@@adverse effects:Symptoms##']
------------------------------
Sentence: Coadministration with another strong CYP3A4 inhibitor

Sentence: Concurrent use may increase ubrogepant exposure and the risk of adverse effects. 
Annotations: ['@@ubrogepant:Drugs##', '@@exposure:Symptoms##']
------------------------------
Sentence: Concurrent use may increase ubrogepant exposure and the risk of adverse effects. 
Annotations: ['@@ubrogepant:Drugs##', '@@exposure:Symptoms##', '@@adverse effects:Symptoms##']
------------------------------
Sentence:  Ribociclib: (Contraindicated) Coadministration of ubrogepant and ribociclib is contraindicated as concurrent use may increase ubrogepant exposure and the risk of adverse effects.
Annotations: ['@@Ribociclib:Drugs##', '@@Contraindicated:Symptoms##', '@@ubrogepant:Drugs##', '@@ribociclib:Drugs##', '@@contraindicated:Symptoms##', '@@ubrogepant:Drugs##', '@@exposure:Symptoms##', '@@adverse effects:Symptoms##']
------------------------------
Sentence: Coadministration with another strong CYP3A4 inhibitor resulted in a 9.7-fold increase in the exposure of ubrogepant. 
Annotations: ['@

...

Sentence: Part of medical nutrition involves instruction in how to use carbohydrate, fat, and protein counting for patients who have advanced to flexible insulin therapy. 
Annotations: ['@@medical:Symptoms##', '@@insulin:Drugs##']
------------------------------
Sentence: Monitoring carbohydrate intake, by carbohydrate counting or experience-based estimation, is an especially important strategy for patients who use insulin. 
Annotations: ['@@carbohydrate intake:Symptoms##', '@@insulin:Drugs##']
------------------------------
Sentence: Emphasize consumption of healthy fats (eg, long-chain ω-3 fatty acids, eicosapentaenoic acid, docosahexaenoic acid, α-linolenic acid) from food sources, such as fish, nuts, and avocados. 
Annotations: ['@@healthy:Symptoms##', '@@eicosapentaenoic acid:Drugs##', '@@sources:Symptoms##', '@@docosahexaenoic acid:Drugs##']
------------------------------
Sentence: Rationale for blood glucose monitoring, regardless of insulin use, is to encourage patients to play 

Sentence: Alert an anesthesiologist if the patient has required oral corticosteroids during 6 months before the surgery or if the patient is on high-dose inhaled corticosteroids; consider steroid stress dosing. 
Annotations: ['@@inhaled corticosteroids:Drugs##', '@@stress:Symptoms##']
------------------------------
Sentence: Inadequate inhaled corticosteroid use (eg, inappropriate inhalation technique, noncompliance with treatment). 
Annotations: ['@@inhaled corticosteroid:Drugs##', '@@noncompliance:Symptoms##']
------------------------------
Sentence: Identify and treat maternal vitamin D deficiency prior to conception or during pregnancy. 
Annotations: ['@@vitamin:Drugs##', '@@deficiency:Symptoms##']
------------------------------
Sentence: Annual influenza vaccine to prevent influenza-induced exacerbation. 
Annotations: ['@@influenza vaccine:Drugs##', '@@vaccine:Drugs##', '@@exacerbation:Symptoms##']
------------------------------
Sentence: Accurate diagnosis is key to avoid treatin

------------------------------
Sentence: If mitapivat is discontinued, consider a dose reduction of hydrocodone and frequently monitor for signs of respiratory depression and sedation. 
Annotations: ['@@mitapivat:Drugs##', '@@discontinued:Symptoms##', '@@signs:Symptoms##']
------------------------------
Sentence: Hydrocodone is a CYP3A substrate and mitapivat is a weak CYP3A inducer. 
Annotations: ['@@mitapivat:Drugs##', '@@weak:Symptoms##']
------------------------------
Sentence: If mitapivat is discontinued, consider a buprenorphine dose reduction and monitor for signs of respiratory depression. 
Annotations: ['@@mitapivat:Drugs##', '@@discontinued:Symptoms##', '@@signs:Symptoms##']
------------------------------
Sentence: If mitapivat is discontinued, consider a buprenorphine dose reduction and monitor for signs of respiratory depression. 
Annotations: ['@@mitapivat:Drugs##', '@@discontinued:Symptoms##', '@@signs:Symptoms##']
------------------------------
Sentence:  Bupropion: (Mo

------------------------------
Sentence:  Emtricitabine; Rilpivirine; Tenofovir disoproxil fumarate: (Moderate) Coadministration of tenofovir disoproxil fumarate with mitapivat may result in increased plasma concentrations of tenofovir, leading to an increase in tenofovir-related adverse effects. 
Annotations: ['@@Rilpivirine:Drugs##', '@@tenofovir disoproxil fumarate:Drugs##', '@@mitapivat:Drugs##', '@@adverse effects:Symptoms##']
------------------------------
Sentence:  Emtricitabine; Tenofovir alafenamide: (Moderate) Coadministration of tenofovir alafenamide with mitapivat may result in increased plasma concentrations of tenofovir leading to an increase in tenofovir-related adverse effects. 
Annotations: ['@@Tenofovir alafenamide:Drugs##', '@@tenofovir alafenamide:Drugs##', '@@mitapivat:Drugs##', '@@adverse effects:Symptoms##']
------------------------------
Sentence:  Emtricitabine; Tenofovir disoproxil fumarate: (Moderate) Coadministration of tenofovir disoproxil fumarate with mi

Annotations: ['@@Mitapivat:Drugs##', '@@weak:Symptoms##']
------------------------------
Sentence:  (Moderate) Monitor for an increase in ombitasvir-related adverse reactions if coadministration with mitapivat is necessary. 
Annotations: ['@@mitapivat:Drugs##', '@@adverse reactions:Symptoms##']
------------------------------
Sentence:  (Moderate) Monitor for an increase in paritaprevir-related adverse reactions if coadministration with mitapivat is necessary. 
Annotations: ['@@mitapivat:Drugs##', '@@adverse reactions:Symptoms##']
------------------------------
Sentence:  Oxycodone: (Moderate) Monitor for reduced efficacy of oxycodone and signs of opioid withdrawal if coadministration with mitapivat is necessary; consider increasing the dose of oxycodone as needed. 
Annotations: ['@@signs:Symptoms##', '@@mitapivat:Drugs##']
------------------------------
Sentence: If mitapivat is discontinued, consider a dose reduction of oxycodone and frequently monitor for signs of respiratory depress

In [363]:
print(selected_sentences[0])
print(temp_entities[0])
print(selected_annotations[0])

Subsequent dose reduction: Permanently discontinue ponatinib therapy in patients unable to tolerate a dose of 15 mg once daily.
['@@ponatinib:Drugs##', '@@therapy:Procedures##', '@@unable:Symptoms##']
['@@ponatinib:Drugs##', '@@unable:Symptoms##']


In [364]:
import pandas as pd
import json

input_txt = selected_sentences[0:10]                         ####change####  
output1 = temp_entities[0:10]                                ####change####
output2 = selected_annotations[0:10]                         ####change####
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities1, entities2 in zip(input_txt, output1, output2):
    # Join the output list elements into a single string
    entities_str1 = ' '.join(entities1)
    entities_str2 = ' '.join(entities2)
    
    example = {
"task":"Named Entity Recognition",
"instruction1":"From the input text list all the symptoms and drugs",
"input":f"{text}", 
"output1":f"Identified symptoms and drugs are: {entities_str2}",
"instruction2":"From above text also identify Procedures, Organisms, Diseases, Anatomies, Specialties, Clinical findings",                    
"output2":entities_str1
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 106.json", "w") as f:     ####change####
    f.write(output_json)

In [365]:
import pandas as pd
import json

input_txt = selected_sentences[10:20]                         ####change####  
output1 = temp_entities[10:20]                                ####change####
output2 = selected_annotations[10:20]                         ####change####
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities1, entities2 in zip(input_txt, output1, output2):
    # Join the output list elements into a single string
    entities_str1 = ' '.join(entities1)
    entities_str2 = ' '.join(entities2)
    
    example = {
"task":"Named Entity Recognition",
"instruction1":"Identify drugs and symptoms from input text", 
"input":f"{text}", 
"output1":entities_str2, 
"instruction2":f"Additionally identify {list_of_entities} from above text.",
"output2":entities_str1
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 107.json", "w") as f:     ####change####
    f.write(output_json)

In [366]:
# Remove elements from 'sentences' list
idx = indices[0:20]
for index in sorted(idx, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(idx, reverse=True):
    del entities_sub[index]
    
print(len(sentences_sub))
print(len(entities_sub))

9967
9967


In [367]:
#template 108

In [368]:
# Find sentences with both "Drugs" and "Symptoms" tags
selected_sentences = []
selected_annotations = []
indices = []

 

for i, sentence in enumerate(sentences_sub):
    annotations = entities_sub[i]

    # Check if "Drugs" and "Symptoms" tags are both present in annotations
    if any("Diseases" in tag for tag in annotations) and any("Symptoms" in tag for tag in annotations):
        selected_sentences.append(sentence)

        # Filter annotations to include only "Drugs" and "Symptoms" tags
        filtered_annotations = [tag for tag in annotations if "Diseases" in tag or "Symptoms" in tag]
        selected_annotations.append(filtered_annotations)
        indices.append(i)

 

# print the selected sentences and their corresponding filtered annotations
for sentence, annotations in zip(selected_sentences, selected_annotations):
    print("Sentence:", sentence)
    print("Annotations:", annotations)
    print("-" * 30)
    
indices = indices[0:20]
temp_entities = []
for i in indices: 
    temp_entities.append(entities_sub[i])

print(selected_sentences[0])
print(temp_entities[0])
print(selected_annotations[0])

Sentence: Chronic changes(eg, fibrosis, tubular atrophy, glomerulosclerosis) are apparent in chronic nephritic syndrome. 
Annotations: ['@@fibrosis:Diseases##', '@@tubular atrophy:Symptoms##', '@@atrophy:Diseases##', '@@glomerulosclerosis:Diseases##', '@@chronic nephritic syndrome:Diseases##', '@@nephritic:Diseases##', '@@nephritic syndrome:Diseases##', '@@syndrome:Diseases##']
------------------------------
Sentence: Diagnosis is based on thrombocytopenia and laboratory indicators of microangiopathic hemolytic anemia, often with associated neurologic dysfunction; in thrombocytopenic purpura, ADAMTS13 activity is subnormal. 
Annotations: ['@@Diagnosis:Symptoms##', '@@thrombocytopenia:Diseases##', '@@microangiopathic hemolytic anemia:Diseases##', '@@hemolytic anemia:Diseases##', '@@anemia:Diseases##', '@@neurologic dysfunction:Symptoms##', '@@dysfunction:Diseases##', '@@thrombocytopenic purpura:Diseases##', '@@purpura:Diseases##']
------------------------------
Sentence: Monitor patient

Sentence: Conscious patient presents with severe headache, which also can be a presenting symptom of lightning strike. 
Annotations: ['@@severe headache:Symptoms##', '@@headache:Diseases##', '@@presenting symptom:Symptoms##', '@@symptom:Symptoms##', '@@lightning strike:Diseases##']
------------------------------
Sentence: Seizing or postictal patients present with confusion, amnesia for the event, paresthesia, or unconsciousness. 
Annotations: ['@@postictal:Symptoms##', '@@confusion:Diseases##', '@@amnesia:Diseases##', '@@paresthesia:Symptoms##', '@@unconsciousness:Symptoms##', '@@Seizing:Symptoms##']
------------------------------
Sentence: Severely concussed patients present confused or unconscious. 
Annotations: ['@@confused:Diseases##', '@@unconscious:Symptoms##', '@@concussed:Diseases##']
------------------------------
Sentence: Diagnose specific injuries (eg, subarachnoid hemorrhage, subdural hematoma, diffuse axonal injury) using head CT scan or MRI. 
Annotations: ['@@injuries:D

Sentence: Kappa-receptors are responsible for analgesia, dysphoria, some psychomimetic effects (e.g., disorientation and/or depersonalization), and sedation. 
Annotations: ['@@responsible:Symptoms##', '@@dysphoria:Diseases##', '@@disorientation:Diseases##', '@@depersonalization:Diseases##']
------------------------------
Sentence: Thus, not only are respiratory depression, hypotension, and sedation reversed, but analgesia as well. 
Annotations: ['@@respiratory depression:Diseases##', '@@depression:Diseases##', '@@hypotension:Symptoms##']
------------------------------
Sentence: Clinicians should use discretion when considering administering naloxone to patients who are sedated from opiates but do not exhibit respiratory depression. 
Annotations: ['@@sedated:Symptoms##', '@@respiratory depression:Diseases##', '@@depression:Diseases##']
------------------------------
Sentence: Naloxone should not be used for drowsiness unless opiate-induced respiratory depression coexists. 
Annotations: 

------------------------------
Sentence: Rocky Mountain Spotted Fever. 
Annotations: ['@@Rocky Mountain Spotted Fever:Diseases##', '@@Spotted Fever:Diseases##', '@@Fever:Symptoms##']
------------------------------
Sentence: Rocky Mountain spotted fever is a tick-borne infection caused by the bacterium Rickettsia rickettsii , which is transmitted via the bite of an infected tick. 
Annotations: ['@@Rocky Mountain spotted fever:Diseases##', '@@spotted fever:Diseases##', '@@fever:Symptoms##', '@@tick-borne infection:Diseases##', '@@infection:Diseases##', '@@transmitted:Diseases##', '@@bite:Diseases##', '@@borne:Diseases##']
------------------------------
Sentence: Rocky Mountain spotted fever presents clinically as an undifferentiated febrile illness and is accompanied by rash that eventually develops in 90% of cases. 
Annotations: ['@@Rocky Mountain spotted fever:Diseases##', '@@spotted fever:Diseases##', '@@fever:Symptoms##', '@@febrile:Symptoms##', '@@febrile illness:Diseases##', '@@ras

------------------------------
Sentence: This may be related to the immunologic role in the sepsis seen with COVID-19. 
Annotations: ['@@related:Symptoms##', '@@sepsis:Diseases##', '@@COVID-19:Diseases##']
------------------------------
Sentence: Delta (B.1.617.2 and AY lineages): first detected in India; characterized by increased transmissibility and possibly by reduced neutralization by some monoclonal antibody treatments and postvaccine serum; unclear whether associated with more severe disease. 
Annotations: ['@@detected:Symptoms##', '@@transmissibility:Diseases##', '@@disease:Diseases##', '@@postvaccine:Symptoms##']
------------------------------
Sentence: Gamma (P.1 and descendent lineages): seems to have originated in Brazil; may mitigate protective effect of antibodies to the original strain. 
Annotations: ['@@protective:Symptoms##', '@@strain:Diseases##']
------------------------------
Sentence: Epsilon (B.1.427 and B.1.429): first detected in California; slight increase in t

...

------------------------------
Sentence: Based on phenotypic cluster (ie, atopic burden, lung function and airway lability, exacerbation history). 
Annotations: ['@@atopic:Diseases##', '@@exacerbation:Symptoms##']
------------------------------
Sentence: Mild asthma with low atopy, obstruction, and exacerbation rate. 
Annotations: ['@@Mild asthma:Symptoms##', '@@asthma:Diseases##', '@@atopy:Diseases##', '@@obstruction:Diseases##', '@@exacerbation:Symptoms##']
------------------------------
Sentence: No history of atopic dermatitis, low prevalence of hay fever and skin prick test reactivity, and lowest IgE levels. 
Annotations: ['@@No history of:Symptoms##', '@@history of:Symptoms##', '@@history of atopic dermatitis:Symptoms##', '@@atopic:Diseases##', '@@atopic dermatitis:Diseases##', '@@dermatitis:Diseases##', '@@hay fever:Diseases##', '@@fever:Symptoms##', '@@prick:Symptoms##']
------------------------------
Sentence: Atopic asthma with low levels of obstruction and medium rates of ex

Sentence: Subcutaneous allergen immunotherapy reduces long-term asthma medication use and may also improve asthma-related quality of life and FEV₁.
Annotations: ['@@asthma:Diseases##', '@@quality of life:Symptoms##']
------------------------------
Sentence: Allergen therapy is usually avoided in patients with severe asthma because of concern regarding greater risk for possible severe systemic reactions and lack of evidence supporting efficacy in this subgroup. 
Annotations: ['@@severe asthma:Symptoms##', '@@asthma:Diseases##']
------------------------------
Sentence: For acute asthma exacerbation. 
Annotations: ['@@acute asthma:Diseases##', '@@asthma:Diseases##', '@@asthma exacerbation:Symptoms##', '@@exacerbation:Symptoms##']
------------------------------
Sentence: Ipratropium Bromide Pressurized inhalation, solution; Infants and Children 5 years and younger: 160 mcg (approximately 9 actuations of 17 mcg/actuation) via oral inhalation every 20 minutes for up to 1 hour only, in conjun

Sentence: Usual guidelines for initiation of systemic corticosteroids for asthma exacerbations should be followed. 
Annotations: ['@@asthma:Diseases##', '@@exacerbations:Symptoms##']
------------------------------
Sentence: Avoid spirometry in patients with known or suspected COVID-19 infection; if possible, postpone spirometry and peak frequency ratio measurements while community transmission rates are concerning. 
Annotations: ['@@suspected COVID-19:Symptoms##', '@@suspected COVID-19 infection:Symptoms##', '@@COVID-19:Diseases##', '@@COVID-19 infection:Diseases##', '@@infection:Diseases##', '@@transmission:Diseases##']
------------------------------
Sentence: Signs of severe obstruction include respiratory rate higher than 60 breaths per minute, use of accessory muscles, inspiratory and expiratory wheezing, paradoxical breathing, cyanosis, and SaO₂ less than 90%. 
Annotations: ['@@Signs:Symptoms##', '@@obstruction:Diseases##', '@@expiratory wheezing:Symptoms##', '@@wheezing:Symptoms#

------------------------------
Sentence: Misdiagnosis of bipolar episodes as unipolar depression is not uncommon. 
Annotations: ['@@Misdiagnosis:Symptoms##', '@@bipolar:Diseases##', '@@unipolar depression:Diseases##', '@@depression:Diseases##']
------------------------------
Sentence: Accurate diagnosis is key to avoid treating with antidepressant monotherapy; treatment with antidepressant monotherapy risks triggering manic and psychotic symptoms. 
Annotations: ['@@diagnosis:Symptoms##', '@@manic:Diseases##', '@@psychotic:Symptoms##', '@@symptoms:Symptoms##']
------------------------------
Sentence: Relapse of mood disorder manifestations increases when pharmacotherapy is rapidly discontinued. 
Annotations: ['@@mood disorder:Diseases##', '@@disorder:Diseases##', '@@manifestations:Symptoms##', '@@discontinued:Symptoms##']
------------------------------
Sentence: Discontinue lithium at onset of labor or 24 to 48 hours before induction or elective cesarean to avoid lithium toxicity in neo

------------------------------
Sentence: Benzhydrocodone; Acetaminophen: (Moderate) Monitor for reduced efficacy of benzhydrocodone and signs of opioid withdrawal if coadministration with mitapivat is necessary; consider increasing the dose of benzhydrocodone as needed. 
Annotations: ['@@signs:Symptoms##', '@@opioid withdrawal:Diseases##']
------------------------------
Sentence: If mitapivat is discontinued, consider a dose reduction of benzhydrocodone and frequently monitor for signs of respiratory depression and sedation. 
Annotations: ['@@discontinued:Symptoms##', '@@signs:Symptoms##', '@@respiratory depression:Diseases##', '@@depression:Diseases##']
------------------------------
Sentence:  Brompheniramine; Guaifenesin; Hydrocodone: (Moderate) Monitor for reduced efficacy of hydrocodone and signs of opioid withdrawal if coadministration with mitapivat is necessary; consider increasing the dose of hydrocodone as needed. 
Annotations: ['@@signs:Symptoms##', '@@opioid withdrawal:Dise

In [369]:
import pandas as pd
import json

input_txt = selected_sentences[0:10]                         ####change####  
output1 = temp_entities[0:10]                                ####change####
output2 = selected_annotations[0:10]                         ####change####
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities1, entities2 in zip(input_txt, output1, output2):
    # Join the output list elements into a single string
    entities_str1 = ' '.join(entities1)
    entities_str2 = ' '.join(entities2)
    
    example = {
"task":"Named Entity Recognition", 
"input":f"{text}",
"instruction1":"What are the list of diseases and symptoms from input text",
"output1":entities_str2,
"instruction2":f"Can you also find {list_of_entities}", 
"output2":entities_str1
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 108.json", "w") as f:     ####change####
    f.write(output_json)

In [370]:
#template 109

In [371]:
import pandas as pd
import json

input_txt = selected_sentences[10:20]                         ####change####  
output1 = temp_entities[10:20]                                ####change####
output2 = selected_annotations[10:20]                         ####change####
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities1, entities2 in zip(input_txt, output1, output2):
    # Join the output list elements into a single string
    entities_str1 = ' '.join(entities1)
    entities_str2 = ' '.join(entities2)
    
    example = {
"task":"Named Entity Recognition", 
"input":f"{text}",
"instruction1":"examine the following text and identify diseases and symptoms",
"output1": f"After examining the text, the following diseases and symptoms were identified: {entities_str2}",
"instruction2":f"from the given text also identify {list_of_entities}", 
"output2":f"Here are all the entities and their categories you asked for {entities_str1}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 109.json", "w") as f:     ####change####
    f.write(output_json)

In [372]:
# Remove elements from 'sentences' list
idx = indices[0:20]
for index in sorted(idx, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(idx, reverse=True):
    del entities_sub[index]
    
print(len(sentences_sub))
print(len(entities_sub))

9947
9947


In [373]:
#template 110

In [374]:
# Find sentences with both "Drugs" and "Symptoms" tags
selected_sentences = []
selected_annotations = []
indices = []

 

for i, sentence in enumerate(sentences_sub):
    annotations = entities_sub[i]

    # Check if "Drugs" and "Symptoms" tags are both present in annotations
    if any("Diseases" in tag for tag in annotations) and any("Procedures" in tag for tag in annotations):
        selected_sentences.append(sentence)

        # Filter annotations to include only "Drugs" and "Symptoms" tags
        filtered_annotations = [tag for tag in annotations if "Diseases" in tag or "Procedures" in tag]
        selected_annotations.append(filtered_annotations)
        indices.append(i)

 

# print the selected sentences and their corresponding filtered annotations
for sentence, annotations in zip(selected_sentences, selected_annotations):
    print("Sentence:", sentence)
    print("Annotations:", annotations)
    print("-" * 30)
    
indices = indices[0:20]
temp_entities = []
for i in indices: 
    temp_entities.append(entities_sub[i])

print(selected_sentences[0])
print(temp_entities[0])
print(selected_annotations[0])

Sentence: Volume overload that cannot be controlled by pharmacotherapy. 
Annotations: ['@@Volume overload:Diseases##', '@@pharmacotherapy:Procedures##']
------------------------------
Sentence: Untreated disease is usually fatal, but plasmapheresis and immunosuppression improve outcomes such that most patients survive. 
Annotations: ['@@disease:Diseases##', '@@plasmapheresis:Procedures##', '@@immunosuppression:Diseases##']
------------------------------
Sentence: AST or ALT at least 3 times ULN concurrent with bilirubin greater than 2 times ULN and alkaline phosphatase less than 2 times ULN:
Annotations: ['@@AST:Diseases##', '@@ALT:Procedures##']
------------------------------
Sentence: Treat hypertension as appropriate; patients may require urgent clinical intervention. 
Annotations: ['@@hypertension:Diseases##', '@@intervention:Procedures##']
------------------------------
Sentence: Therapy interruption, a dosage adjustment, or discontinuation may be necessary if hypertension is not 

------------------------------
Sentence: Prednisone Oral tablet; Adults: Initially, use a large dose (e.g., 60 mg PO once daily); once muscle disease is controlled, taper to 5 mg to 10 mg PO every other day..
Annotations: ['@@muscle disease:Diseases##', '@@disease:Diseases##', '@@taper:Procedures##']
------------------------------
Sentence: Methylprednisolone Sodium Succinate Solution for injection; Adults: Initially, 10 to 40 mg IV/IM. 
Annotations: ['@@injection:Procedures##', '@@IM:Diseases##']
------------------------------
Sentence: Immune Globulin (Human) Solution for injection; Adults: Patients with resistant dermatomyositis received IVIG 2 g/kg IV in 2 separate doses every month for 3 months in one study..
Annotations: ['@@injection:Procedures##', '@@dermatomyositis:Diseases##']
------------------------------
Sentence: Ophthalmologic assessment at diagnosis, as well as at follow-up, is recommended owing to possible eye involvement (eg, eyelid abnormalities, retinopathy, visual 

Annotations: ['@@hospitalized:Procedures##', '@@severe COVID-19:Diseases##', '@@COVID-19:Diseases##', '@@mechanical ventilation:Procedures##']
------------------------------
Sentence: WHO guideline summarizes evidence for use of interleukin-6 inhibitors (tocilizumab or sarilumab) from up to 27 studies for 6 outcomes; overall, interleukin-6 inhibitors reduce mortality, decrease need for mechanical ventilation, and may decrease duration of mechanical ventilation and hospitalization, with little evidence for adverse events leading to discontinuation of drug, including secondary bacterial infections. 
Annotations: ['@@mechanical ventilation:Procedures##', '@@mechanical ventilation:Procedures##', '@@hospitalization:Procedures##', '@@discontinuation:Procedures##', '@@infections:Diseases##', '@@bacterial infections:Diseases##']
------------------------------
Sentence: REMAP-CAP and RECOVERY trials both indicate a mortality benefit for tocilizumab among patients who experienced rapid respirato

Annotations: ['@@surgery:Procedures##', '@@pharmacotherapy:Procedures##', '@@diabetes:Diseases##', '@@surgery:Procedures##', '@@therapies:Procedures##', '@@A1C:Procedures##']
------------------------------
Sentence: Major complication rate is approximately 5% and reoperation rate is approximately 8%. 
Annotations: ['@@complication:Diseases##', '@@reoperation:Procedures##']
------------------------------
Sentence: There is strong evidence supporting treatment of patients with diabetes and blood pressure of 140/90 mm
Annotations: ['@@supporting treatment:Procedures##', '@@treatment:Procedures##', '@@diabetes:Diseases##']
------------------------------
Sentence: Hg yield cardiovascular benefits for some populations but increase adverse events (elevations in serum creatinine level and electrolyte disturbances). 
Annotations: ['@@elevations:Procedures##', '@@serum creatinine:Procedures##', '@@serum creatinine level:Procedures##', '@@electrolyte disturbances:Diseases##']
--------------------

Annotations: ['@@examination:Procedures##', '@@infection:Diseases##', '@@strangulated hernia:Diseases##', '@@hernia:Diseases##']
------------------------------
Sentence: Rectal examination is of limited use and not recommended routinely, but it may be helpful in detecting blood (peptic ulcer disease, ischemic bowel), stool impaction, perirectal abscess, or fistulae. 
Annotations: ['@@Rectal examination:Procedures##', '@@examination:Procedures##', '@@peptic ulcer:Diseases##', '@@peptic ulcer disease:Diseases##', '@@ulcer:Diseases##', '@@disease:Diseases##', '@@ischemic bowel:Diseases##', '@@impaction:Diseases##', '@@perirectal abscess:Diseases##', '@@abscess:Diseases##', '@@fistulae:Diseases##']
------------------------------
Sentence: In patients whose abdominal examination is unrevealing, broaden the scope of physical examination, as extra-abdominal disease may present as abdominal pain (eg, myocardial infarction, pneumonia, pulmonary embolism, renal or other retroperitoneal pathology

------------------------------
Sentence: Conventional ultrasonography is 83% to 91%  sensitive and 80%  to 95% specific for cholecystitis and is better than CT in detecting this condition. 
Annotations: ['@@ultrasonography:Procedures##', '@@cholecystitis:Diseases##', '@@CT:Procedures##']
------------------------------
Sentence: Ultrasonography may also detect a variety of intra-abdominal conditions including liver mass, diverticulitis, appendicitis, and small bowel inflammation or obstruction, but in general, sensitivity does not equal that of CT for these conditions. 
Annotations: ['@@Ultrasonography:Procedures##', '@@liver mass:Diseases##', '@@diverticulitis:Diseases##', '@@appendicitis:Diseases##', '@@inflammation:Diseases##', '@@obstruction:Diseases##', '@@CT:Procedures##']
------------------------------
Sentence: Point of care ultrasonographic technique developed for evaluation of trauma, FAST protocol (focused assessment with sonography for trauma) is increasingly used for prelim

Sentence: Consider subcutaneous allergen immunotherapy for patients with persistent asthma when (1) there is a clear evidence of a relationship between symptoms and exposure to an allergen to which the patient is sensitive and (2) exposure reduction measures have failed. 
Annotations: ['@@allergen immunotherapy:Procedures##', '@@immunotherapy:Procedures##', '@@persistent asthma:Diseases##', '@@asthma:Diseases##', '@@measures:Procedures##']
------------------------------
Sentence: Avoid using β-blockers and NSAIDs (including aspirin) in patients with asthma because they have potential to exacerbate symptoms. 
Annotations: ['@@asthma:Diseases##', '@@Avoid:Procedures##']
------------------------------
Sentence: Multidisciplinary case management may be needed for patients with severe, difficult-to-treat disease. 
Annotations: ['@@case management:Procedures##', '@@disease:Diseases##']
------------------------------
Sentence: Consider evaluation for gastroesophageal reflux disease (eg, 24-ho

Sentence:  Dienogest; Estradiol valerate: (Major) Women taking both estrogens and mitapivat should report breakthrough bleeding to their prescribers. 
Annotations: ['@@taking:Procedures##', '@@breakthrough bleeding:Diseases##', '@@bleeding:Diseases##', '@@prescribers:Procedures##']
------------------------------
Sentence:   Diethylstilbestrol, DES: (Major) Women taking both estrogens and mitapivat should report breakthrough bleeding to their prescribers. 
Annotations: ['@@taking:Procedures##', '@@breakthrough bleeding:Diseases##', '@@bleeding:Diseases##', '@@prescribers:Procedures##']
------------------------------
Sentence:   Digoxin: (Moderate) Increase monitoring of serum digoxin concentrations and watch for potential signs and symptoms of clinical toxicity when starting, adjusting, or discontinuing mitapivat. 
Annotations: ['@@monitoring:Procedures##', '@@toxicity:Diseases##', '@@serum digoxin:Procedures##']
------------------------------
Sentence: If mitapivat is discontinued, con

Sentence: Malabsorption states Patients with partial gastrectomy or with malabsorption syndromes will have impaired absorption of iron from food..
Annotations: ['@@Malabsorption:Diseases##', '@@partial gastrectomy:Procedures##', '@@gastrectomy:Procedures##', '@@malabsorption:Diseases##', '@@syndromes:Diseases##', '@@malabsorption syndromes:Diseases##']
------------------------------
Sentence: For the treatment of iron-deficiency anemia NOTE: All dosages are expressed in terms of elemental iron. 
Annotations: ['@@treatment:Procedures##', '@@iron-deficiency anemia:Diseases##', '@@deficiency anemia:Diseases##', '@@anemia:Diseases##']
------------------------------
Sentence: Serum iron levels greater than 300 mcg/dL, elevated ferritin levels, and transferrin oversaturation may indicate iron poisoning (see Adverse reactions).
Annotations: ['@@Serum iron:Procedures##', '@@iron poisoning:Diseases##', '@@poisoning:Diseases##']
------------------------------
Sentence: Patients with Hepatic Impa

In [375]:
import pandas as pd
import json

input_txt = selected_sentences[0:10]                         ####change####  
output1 = temp_entities[0:10]                                ####change####
output2 = selected_annotations[0:10]                         ####change####
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities1, entities2 in zip(input_txt, output1, output2):
    # Join the output list elements into a single string
    entities_str1 = ' '.join(entities1)
    entities_str2 = ' '.join(entities2)
    
    example = {
"task":"Named Entity Recognition", 
"input":f"{text}",
"instruction1":"From the following text identify diseases and procedures and display them in such a way such that the start of every entity @@ and the end is ##",
"output1": f"{entities_str2}",
"instruction2":f"Additionally please identify {list_of_entities}", 
"output2":f"Here is an updated list containing the additional entities {entities_str1}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 110.json", "w") as f:     ####change####
    f.write(output_json)

In [376]:
#template 111

In [377]:
import pandas as pd
import json

input_txt = selected_sentences[10:20]                         ####change####  
output1 = temp_entities[10:20]                                ####change####
output2 = selected_annotations[10:20]                         ####change####
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities1, entities2 in zip(input_txt, output1, output2):
    # Join the output list elements into a single string
    entities_str1 = ' '.join(entities1)
    entities_str2 = ' '.join(entities2)
    
    example = {
"task":"Named Entity Recognition", 
"input":f"{text}",
"instruction1":"Please analyze the text below and identify diseases and procedures",
"output1": f"After analyzing the text, the following diseases and procedures were identified: {entities_str2}",
"instruction2":"Now identify all the entities in the text", 
"output2":f"Here is an updated list containing all the entities {entities_str1}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 111.json", "w") as f:     ####change####
    f.write(output_json)

In [378]:
# Remove elements from 'sentences' list
idx = indices[0:20]
for index in sorted(idx, reverse=True):
    del sentences_sub[index]

# Remove elements from 'sentences' list
for index in sorted(idx, reverse=True):
    del entities_sub[index]
    
print(len(sentences_sub))
print(len(entities_sub))

9927
9927


In [379]:
#saving 
import pickle
with open('Remaining data.pkl', 'wb') as f:
    pickle.dump((entities_sub, sentences_sub), f)

In [380]:
import pickle
with open('Remaining data.pkl', 'rb') as f:
    loaded_data = pickle.load(f)
loaded_annotations, loaded_sentences = loaded_data

In [381]:
len(loaded_annotations)

9927

In [382]:
loaded_annotations

[['@@Simethicone:Drugs##', '@@plasma:Anatomy##', '@@sarecycline:Drugs##'],
 ['@@tetracycline antibiotics:Drugs##', '@@chelate:Drugs##'],
 ['@@tetracycline antibiotics:Drugs##', '@@chelate:Drugs##'],
 ['@@tetracycline antibiotics:Drugs##', '@@chelate:Drugs##'],
 ['@@monitoring:Procedures##'],
 ['@@Molindone:Drugs##', '@@molindone:Drugs##'],
 ['There are none'],
 ['@@sarecycline:Drugs##'],
 ['@@Neuromuscular:Anatomy##',
  '@@Neuromuscular blockers:Drugs##',
  '@@neuromuscular:Anatomy##',
  '@@neuromuscular blockers:Drugs##',
  '@@neuromuscular:Anatomy##',
  '@@neuromuscular blockade:Procedures##',
  '@@tetracyclines:Drugs##'],
 ['@@peripheral nerve:Anatomy##',
  '@@nerve:Anatomy##',
  '@@evaluate:Procedures##',
  '@@neuromuscular:Anatomy##',
  '@@neuromuscular blockade:Procedures##',
  '@@assess:Procedures##',
  '@@neuromuscular:Anatomy##',
  '@@determine:Procedures##',
  '@@neuromuscular blocker:Drugs##'],
 ['@@tetracyclines:Drugs##'],
 ['@@oral:Anatomy##'],
 ['@@tetracyclines:Drugs##']

In [383]:
entities_sub = loaded_annotations
sentences_sub = loaded_sentences 

In [384]:
#template 112

In [385]:
list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Anatomies, Specialties, Clinical findings, Drugs"

In [386]:
import pandas as pd
import json

input_txt = sentences_sub[0:10]       
output = entities_sub[0:10]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"What are the named entities in the text snippet given below? Options: {list_of_entities}",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 112.json", "w") as f:     
    f.write(output_json)

In [387]:
#template 113

In [388]:
import pandas as pd
import json

input_txt = sentences_sub[10:20]       
output = entities_sub[10:20]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Find and identify {list_of_entities}",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 113.json", "w") as f:     
    f.write(output_json)

In [389]:
#template 114

In [390]:
import pandas as pd
import json

input_txt = sentences_sub[20:30]       
output = entities_sub[20:30]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Identify all named entities related to medical domain, and provide their entity types.",
"input":f"{text}",
"output":f"Here are all the named entities related to the medical domain {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 114.json", "w") as f:     
    f.write(output_json)

In [391]:
#template 115

In [392]:
import pandas as pd
import json

input_txt = sentences_sub[30:40]       
output = entities_sub[30:40]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Please list all entities in the text. Options: {list_of_entities}",
"input":f"{text}",
"output":f"Here are all the entities in the text: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 115.json", "w") as f:     
    f.write(output_json)

In [393]:
#template 116

In [394]:
import pandas as pd
import json

input_txt = sentences_sub[40:50]       
output = entities_sub[40:50]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Please list all entities that would be important to a medical professional",
"input":f"{text}",
"output":f"All the entities important to a medical professional are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 116.json", "w") as f:     
    f.write(output_json)

In [395]:
#template 117

In [396]:
import pandas as pd
import json

input_txt = sentences_sub[50:60]       
output = entities_sub[50:60]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Please list all entities that would be important to a clinical specialist",
"input":f"{text}",
"output":f"All the entities important to a clinical specialist are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 117.json", "w") as f:     
    f.write(output_json)

In [397]:
#template 118

In [398]:
import pandas as pd
import json

input_txt = sentences_sub[60:70]       
output = entities_sub[60:70]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"In the provided text, indicate all the {list_of_entities} where every new one starts with @@ and ends with ##",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 118.json", "w") as f:     
    f.write(output_json)

In [399]:
#template 119

In [400]:
import pandas as pd
import json

input_txt = sentences_sub[70:80]       
output = entities_sub[70:80]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Search and identify {list_of_entities}",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 119.json", "w") as f:     
    f.write(output_json)

In [401]:
#template 120

In [402]:
import pandas as pd
import json

input_txt = sentences_sub[80:90]       
output = entities_sub[80:90]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"List all entity words in the text. Options: {list_of_entities}",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 120.json", "w") as f:     
    f.write(output_json)

In [403]:
#templat 121

In [404]:
import pandas as pd
import json

input_txt = sentences_sub[90:100]       
output = entities_sub[90:100]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"What are the named entities in the text extract below?",
"input":f"{text}",
"output":f"These are the named entities in the text extract given: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 121.json", "w") as f:     
    f.write(output_json)

In [405]:
#template 122

In [406]:
import pandas as pd
import json

input_txt = sentences_sub[100:110]       
output = entities_sub[100:110]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Extract all the {list_of_entities} from the following section.",
"input":f"{text}",
"output":f"All the extracted entities are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 122.json", "w") as f:     
    f.write(output_json)

In [407]:
#template 123

In [408]:
import pandas as pd
import json

input_txt = sentences_sub[110:120]       
output = entities_sub[110:120]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Find {list_of_entities} in the following section.",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 123.json", "w") as f:     
    f.write(output_json)

In [409]:
#template 124

In [410]:
import pandas as pd
import json

input_txt = sentences_sub[120:130]       
output = entities_sub[120:130]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"What are the {list_of_entities} in the following text fragment?",
"input":f"{text}",
"output":f"List of entities in the given text fragment are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 124.json", "w") as f:     
    f.write(output_json)

In [411]:
#template 125

In [412]:
import pandas as pd
import json

input_txt = sentences_sub[130:140]       
output = entities_sub[130:140]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Are there any {list_of_entities} in this sentence?  List all those that can be found. If there are none in this sentence, answer: There are none",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 125.json", "w") as f:     
    f.write(output_json)

In [413]:
#template 126

In [414]:
import pandas as pd
import json

input_txt = sentences_sub[140:150]       
output = entities_sub[140:150]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Which entities can you find in the paragraph?",
"input":f"{text}",
"output":f"Entities found in the paragraph are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 126.json", "w") as f:     
    f.write(output_json)

In [415]:
#template 127

In [416]:
import pandas as pd
import json

input_txt = sentences_sub[150:160]       
output = entities_sub[150:160]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Can you please identify all entities in that text?",
"input":f"{text}",
"output":f"All identified entities are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 127.json", "w") as f:     
    f.write(output_json)

In [417]:
#template 128

In [418]:
import pandas as pd
import json

input_txt = sentences_sub[160:170]       
output = entities_sub[160:170]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Are there any {list_of_entities} mentioned in the text?",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 128.json", "w") as f:     
    f.write(output_json)

In [419]:
#template 129

In [420]:
import pandas as pd
import json

input_txt = sentences_sub[170:180]       
output = entities_sub[170:180]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Does this sentence mention any {list_of_entities}?",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 129.json", "w") as f:     
    f.write(output_json)

In [421]:
#template 130

In [422]:
import pandas as pd
import json

input_txt = sentences_sub[180:190]       
output = entities_sub[180:190]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Could you please provide a list of all entities that you can find in this snippet?",
"input":f"{text}",
"output":f"List of all entities found in the given snippet are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 130.json", "w") as f:     
    f.write(output_json)

In [423]:
#template 131

In [424]:
import pandas as pd
import json

input_txt = sentences_sub[190:200]       
output = entities_sub[190:200]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Can you provide a list of all the entities in the sentence? Which entity type do they belong to?",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 131.json", "w") as f:     
    f.write(output_json)

In [425]:
#template 132

In [426]:
import pandas as pd
import json

input_txt = sentences_sub[200:210]       
output = entities_sub[200:210]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Can you list all the entities in the sentence that belong to any of this entity types: {list_of_entities}?",
"input":f"{text}",
"output":f"{entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 132.json", "w") as f:     
    f.write(output_json)

In [427]:
#template 133

In [428]:
import pandas as pd
import json

input_txt = sentences_sub[210:220]       
output = entities_sub[210:220]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"I extracted the following text from an article. Which are the medical concepts you found? Which category do they belong to?",
"input":f"{text}",
"output":f"The following medical concepts along with their respective categories were found: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 133.json", "w") as f:     
    f.write(output_json)

In [429]:
#template 134

In [430]:
import pandas as pd
import json

input_txt = sentences_sub[220:230]       
output = entities_sub[220:230]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Please recognize all entities in the text:",
"input":f"{text}",
"output":f"All the recognized entities in the text are: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 134.json", "w") as f:     
    f.write(output_json)

In [431]:
#template 135

In [432]:
import pandas as pd
import json

input_txt = sentences_sub[230:240]       
output = entities_sub[230:240]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Can you please identify and categorize the key subjects in that piece of text?",
"input":f"{text}",
"output":f"These are the key subjects in the given piece of text: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 135.json", "w") as f:     
    f.write(output_json)

In [433]:
#removing "there are none" annotations and the corresponding sentences 

In [434]:
entities_sub = entities_sub[240:]
sentences_sub = sentences_sub[240:]

In [435]:
print(len(entities_sub))
print(len(sentences_sub))

9687
9687


In [436]:
# Find indices of elements containing "There are none"
indices_to_remove = [i for i, annotations in enumerate(entities_sub) if any("There are none" in tag for tag in annotations)]

# Create a new filtered entities_sub list without elements containing "There are none"
filtered_entities_sub = [annotations for i, annotations in enumerate(entities_sub) if i not in indices_to_remove]

In [437]:
len(indices_to_remove)

559

In [438]:
entities_sub = filtered_entities_sub

In [439]:
# Remove elements from 'sentences' list
for index in sorted(indices_to_remove, reverse=True):
    del sentences_sub[index]

print(len(sentences_sub))
print(len(entities_sub))

9128
9128


In [440]:
print(sentences_sub[2])
entities_sub[2]

Monitor patients for signs and symptoms of bleeding and mange as clinically indicated. 


['@@signs:Symptoms##',
 '@@signs and symptoms:Symptoms##',
 '@@symptoms:Symptoms##',
 '@@bleeding:Symptoms##']

In [441]:
#template 136

In [442]:
import pandas as pd
import json

input_txt = sentences_sub[0:10]       
output = entities_sub[0:10]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"What {list_of_entities} are present in the text?",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 136.json", "w") as f:     
    f.write(output_json)

In [443]:
#template 137

In [444]:
import pandas as pd
import json

input_txt = sentences_sub[10:20]       
output = entities_sub[10:20]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Apply Named Entity Recognition (NER) task to this snippet:",
"input":f"{text}",
"output":f"The following named entities were identified after applying Named Entity Recognition task: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 137.json", "w") as f:     
    f.write(output_json)

In [445]:
#template 138

In [446]:
import pandas as pd
import json

input_txt = sentences_sub[20:30]       
output = entities_sub[20:30]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":"Use Named Entity Recognition task with following fragment:",
"input":f"{text}",
"output":f"The following named entities were identified after applying Named Entity Recognition task on the fragment: {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 138.json", "w") as f:     
    f.write(output_json)

In [447]:
#template 139 

In [448]:
import pandas as pd
import json

input_txt = sentences_sub[30:40]       
output = entities_sub[30:40]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Identify entities of the following types: {list_of_entities}",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 139.json", "w") as f:     
    f.write(output_json)

In [449]:
#template 140

In [450]:
import pandas as pd
import json

input_txt = sentences_sub[40:50]       
output = entities_sub[40:50]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Output the following entity types {list_of_entities} in the text:",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 140.json", "w") as f:     
    f.write(output_json)

In [451]:
#template 141

In [452]:
import pandas as pd
import json

input_txt = sentences_sub[50:60]       
output = entities_sub[50:60]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Output any mentions of {list_of_entities} encountered in the text.",
"input":f"{text}",
"output":f"Here are the entities encountered in the text {entities_str}"
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 141.json", "w") as f:     
    f.write(output_json)

In [453]:
#template 142

In [454]:
import pandas as pd
import json

input_txt = sentences_sub[60:70]       
output = entities_sub[60:70]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Output the following entity types {list_of_entities} if present:",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 142.json", "w") as f:     
    f.write(output_json)

In [455]:
#template 143

In [456]:
import pandas as pd
import json

input_txt = sentences_sub[70:80]       
output = entities_sub[70:80]           
#list_of_entities = "Procedures, Symptoms, Organisms, Diseases, Socialcontext, Anatomy, Specialty, Substance, Environmentgeographicallocation, Qualifier, Clinicalfinding, Event, Drugs, Physicalobjects"

# Create a list to store the generated examples
examples = []

# Generate examples and store them as dictionaries
for text, entities in zip(input_txt, output):
    # Join the output list elements into a single string
    entities_str = ' '.join(entities)
    
    example = {
"task":"Named Entity Recognition",
"instruction":f"Output the following entity types {list_of_entities} if present:",
"input":f"{text}",
"output":entities_str
    }
    examples.append(example)

# Convert the examples to JSON format
output_json = json.dumps(examples, indent=2)

# Save the JSON output to a file
with open("template 143.json", "w") as f:     
    f.write(output_json)

In [457]:
entities_sub = entities_sub[80:]
sentences_sub = sentences_sub[80:]

In [458]:
print(len(entities_sub))
print(len(sentences_sub))

9048
9048


In [459]:
import pickle
with open('Remaining data.pkl', 'wb') as f:
    pickle.dump((entities_sub, sentences_sub), f)
    
import pickle
with open('Remaining data.pkl', 'rb') as f:
    loaded_data = pickle.load(f)
loaded_annotations, loaded_sentences = loaded_data

In [460]:
import os
import shutil

# Source directory containing JSON files
source_directory = '/Users/ritvikkhandelwal/Desktop/elsevier docs/Elsevier projects/Knowledge minor Gold standard '

# Destination directory to store sorted JSON files
destination_directory = '/Users/ritvikkhandelwal/Desktop/elsevier docs/Elsevier projects/Knowledge minor Gold standard /datapoints'

# Create the destination directory if it doesn't exist
os.makedirs(destination_directory, exist_ok=True)

# List all JSON files in the source directory
json_files = [filename for filename in os.listdir(source_directory) if filename.endswith('.json')]

# Sort the list of JSON files based on the numeric part of the filename
sorted_json_files = sorted(json_files, key=lambda x: int(x.split()[1].split('.')[0]))

# Move each sorted JSON file to the destination directory
for filename in sorted_json_files:
    source_path = os.path.join(source_directory, filename)
    destination_path = os.path.join(destination_directory, filename)
    shutil.move(source_path, destination_path)

print("Files moved and sorted successfully!")


Files moved and sorted successfully!


# 8 entity templates

In [461]:
#template 95-100

# multi turn template

In [462]:
#template 100-110